# Project Five 
# Game of Thrones - Season One

## Importing and Cleaning

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import nltk
from nltk.tag import pos_tag
from nltk.tokenize import word_tokenize
from nltk.tokenize import sent_tokenize
from textblob import TextBlob
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import NMF, LatentDirichletAllocation
import gensim
from nltk.tag import pos_tag
import re

Using Theano backend.


In [2]:
pd.set_option('display.max_columns', 125)
pd.set_option('display.max_rows', 125)

In [3]:
df_s1 = pd.read_json('/Users/zoemarkovits/Metis/project_five_got/scrape/season_one.json')

In [4]:
df_s1[['title','script_text']]

title  \
0                      [Winter is Coming]   
1                         [The Kingsroad]   
2                             [Lord Snow]   
3  [Cripples, Bastards and Broken Things]   
4                 [The Wolf and The Lion]   
5                        [A Golden Crown]   
6                    [You Win Or You Die]   
7                        [The Pointy End]   
8                                [Baelor]   
9                        [Fire and Blood]   

                                         script_text  
0  [[First scene opens with three Rangers riding ...  
1  [\n, \n, Jorah Mormont:,  You need to drink, c...  
2  [\n, \n, King’s Landing Guard:,  Welcome, Lord...  
3  [\n, \n, Old Nan:,  The little Lord's been dre...  
4  [\n, Eddard Stark:,  He'd never worn this armo...  
5  [\n, \n, Eddard Stark:,   Your pardon, your Gr...  
6  [\n, \n, \nPoor Ned Stark. Brave man, terrible...  
7  [King's Landing, \n, \n, Syrio Forel: ,  Yah! ...  
8  [\n, Varys: ,  You've seen better days, my lor...  
9  [\n, \n, Yoren: ,  Look at me. Look at me! Do ...

In [5]:
df_s1['title'] = df_s1['title'].map(lambda x: str(x)[3:-2])

In [6]:
df_s1.title

0                        Winter is Coming
1                           The Kingsroad
2                               Lord Snow
3    Cripples, Bastards and Broken Things
4                   The Wolf and The Lion
5                          A Golden Crown
6                      You Win Or You Die
7                          The Pointy End
8                                  Baelor
9                          Fire and Blood
Name: title, dtype: object

In [7]:
names1_01 = ['WAYMAR ROYCE','WILL','GARED','ROYCE','JON','SEPTA MORDANE','NED','ROBB','BRAN','JON/ROBB','CASSEL',
             'CATELYN','THEON','JAIME','CERSEI','MAESTER LUWIN','LUWIN','ARYA','SANSA','ROBERT','TYRION','ROS',
             'VISERYS','DAENERYS','MAID','ILLYRIO','BENJEN','JORAH','KHAL DROGO','THE HOUND']

names1_02 = ['Jorah Mormont','Daenerys Targaryen','Doreah','Irri','Viserys Targaryen','Joffrey Baratheon',
             'Tyrion Lannister','Sandor Clegane','Jaime Lannister','Myrcella Baratheon','Cersei Baratheon',
             'Catelyn Stark','Jon Snow','Arya Stark','Eddard Stark','Robb Stark','Robert Baratheon','Benjen Stark',
             'Maester Luwin','Assassin','Jhiqui','Theon Greyjoy','Rodrick Cassel','Mycah','Soldier 1','Soldier 2',
             'Jory Cassel','Soldier']

names1_03 = ['King’s Landing Guard','Eddard Stark','Jory Cassel','Jaime Lannister','Eddard Stark','Varys',
             'Renly Baratheon','Petyr Baelish','Grand Maester Pycelle','Cersei Baratheon','Joffrey Baratheon',
             'Septa Mordane','Arya Stark','Sansa Stark','Old Nan','Bran Stark','Robb Stark','Rodrick Cassel',
             'Catelyn Stark','Guard','Alliser Thorne','Tyrion Lannister','Jeor Mormont','Grenn','Jon Snow',
             'Pyp','Rast','Barristan Selmy','Robert Baratheon','Lancel Lannister','Daenerys Targaryen',
             'Jorah Mormont','Viserys Targaryen','Irri','Rakharo','Benjen Stark','Yoren','Maester Aemon',
             'Jeor Mormont','Khal Drogo','Syrio Forel','Arya Stark']

names1_04 = ['Old Nan','Theon Greyjoy','Bran Stark','Tyrion Lannister','Robb Stark','Maester Luwin','Grenn',
             'Jon Snow','Pyp','Alliser Thorne','Samwell Tarly','Jorah Mormont','Viserys Targaryen',
             'Daenerys Targaryen','Doreah','Septa Mordane','Sansa Stark','Janos Slynt','Eddard Stark','Varys',
             'Renly Baratheon','Petyr Baelish','Grand Maester Pycelle','Arya Stark','Jory Cassel','Hugh of the Vale',
             'Tobho Mott','Gendry','Jaime Lannister','Robert Baratheon','Rast','Irri','Cersei Baratheon','Marillion',
             'Catelyn Stark','Rodrick Cassel','Masha Heddle','Bronn','Yoren','Knight of House Whent',
             'Knight of House Bracken']

names1_05 = ['Eddard Stark','Barristan Selmy','Lancel Lannister','Robert Baratheon','Sansa Stark','Petyr Baelish',
             'Renly Baratheon','Loras Tyrell','Sandor Clegane','Catelyn Stark','Marillion','Tyrion Lannister',
             'Rodrik Cassel','Bronn','Maester Luwin','Bran Stark','Theon Greyjoy','Ros','Arya Stark','Varys',
             'Illyrio Mopatis','Guard 1','Guard 2','Jory Cassel','Yoren','Vardis Egen','Steward',
             'Grand Maester Pycelle','Lysa Arryn','Robin Arryn','Mord','Cersei Baratheon','Mhaegen','Jaime Lannister']

names1_06 = ['Eddard Stark','Cersei Baratheon','Robert Baratheon','Irri','Daenerys Targaryen','Robb Stark',
             'Bran Stark','Theon Greyjoy','Osha','Wildling','Wildling 2','Tyrion Lannister','Arya Stark','Syrio Forel',
             'Jorah Mormont','Viserys Targaryen','Mord','Lysa Arryn','Robin Arryn','Catelyn Stark','Knight 1',
             'Knight 2','Knight 3','Knight 4','Knight 5','Ser Vardis','Lancel Lannister','Renly Baratheon',
             'Barristan Selmy','Man','Grand Maester Pycelle','Petyr Baelish','Beric Dondarrion','Mordane',
             'Sansa Stark','Joffrey Baratheon','Ros','Khal Drogo',]

names1_07 = ['Jaime Lannister','Tywin Lannister','Cersei Lannister','Ned Stark','Ros','Petyr Baelish','Theon Greyjoy',
             'Osha','Maester Luwin','Samwell Tarly','Jon Snow','Night Watch stable boy','Renly Baratheon',
             'Robert Baratheon','Barristan Selmy','Lord Varys','Khal Drogo','Daenerys Stormborn','Jorah Mormont',
             'Wine Merchant','Doreah','Rakharo','Jeor Mormont','Alliser Thorne','Jaremy Rykker','Othell Yarwyck',
             'Maester Aemon','Pypar','Tomard','Messenger','Varly','Lord Varys','Janos Slynt','King Joffrey']

names1_08 = ['Syrio Forel','Steward of House Stark','Septa Mordane','Sansa Stark','Arya Stark','Meryn Trant',
             'Sandor Clegane','Stable Boy','Lord Varys','Ned Stark','Jeor Mormont','Othell Yarwyck','Jon Snow',
             'Samwell Tarly','Ser Alliser','Nights Watch brother','Grand Maester Pycelle','Cersei Lannister',
             'Petyr Baelish','Robb Stark','Robb Stark','Theon Greyjoy','Catelyn Stark','Lysa Arryn','Robin Arryn',
             'Bronn','Tyrion Lannister','Shagga','Daenarys Stormborn','Rakharo','Jorah Mormont','Dothraki Man',
             'Mago','Qotho','Khal Drogo','Mirri Maz Duur','Greatjon Umber','Brann Stark','Rickon Stark','Osha',
             'Hodor','Rodrik Cassel','Kevan Lannister','Tywin Lannister','Jamie Lannister','Messenger','Stark guard',
             'Lannister scout','Barristan Selmy','King Joffrey','King’s Landing Page']

names1_09 = ['Varys','Eddard Stark','Robb Stark','Theon Greyjoy','Catelyn Stark','Greatjon Umber','Everyone',
             'Walder Frey','Stevron Frey','Ryger Rivers','Voices outside','Jeor Mormont','Jon Snow',
             'Unidentified Night’s Watchers','Night’s Watcher #1','Night’s Watcher #2','Pyp','Grenn','All',
             'Samwell Tarly','Maester Aemon','Daenerys Targaryen','Khal Drogo','Cohollo','Qotho','Kevan Lannister',
             'Tywin Lannister','Tyrion Lannister','Bronn','Prostitute','Shae','Jorah Mormont','Mirri Maz Duur',
             'Rakharo','Irri','Rodrik Cassel','Stark bannermen','Jaime Lannister','Arya Stark','King’s Landing Baker',
             'Street Urchin','Populace','Grand Maester Pycelle','Joffrey Baratheon','Sansa Stark','Cersei Baratheon',
             'Yoren']

names1_10 = ['Yoren','Arya Stark','Bran Stark','Osha','Rickon Stark','Maester Luwin','Several Stark Bannermen',
             'Robb Stark','Catelyn Stark','Marillion','Joffrey Baratheon','Sansa Stark','Sandor Clegane',
             'Jonos Bracken','Galbart Glover','Greatjon Umber','Rickard Karstark','Theon Greyjoy','All','Stark Guard',
             'Jaime Lannister','Lancel Lannister','Cersei Lannister','Tywin Lannister','Tyrion Lannister',
             'Leo Lefford','Addam Marbrand','Kevan Lannister','Daenerys Targaryen','Jorah Mormont','Mirri Maz Duur',
             'Samwell Tarly','Jon Snow','Shae','Sam, Pyp, and Grenn','Pyp','Grenn','Grand Maester Pycelle','Ros',
             'Varys','Petyr Baelish','Hot Pie','Lommy Greenhands','Gendry','Jeor Mormont','Rakharo']

### Episode One

In [8]:
df_s1.script_text[0]

[u'[First scene opens with three Rangers riding through a tunnel, leaving the Wall, and going into the woods. (Eerie music in background) One Ranger splits off and finds a campsite full of mutilated bodies, including a child hanging from a tree branch. ',
 u' The Ranger rides back to the other two.]',
 u'\n',
 u'\n',
 u'\n',
 u'\nWILL: ',
 u'\n',
 u'\nWAYMAR ROYCE: How close did you get?',
 u'\n',
 u'\nWILL: Close as any man would.',
 u'\n',
 u'\nGARED: We should head back to the wall.',
 u'\n',
 u'\n',
 u'\n',
 u'\nGARED: Our orders were to track the wildlings. We tracked them. They won\u2019t trouble us no more.',
 u'\n',
 u'\nROYCE: You don\u2019t think he\u2019ll ask us how they died? Get back on your horse.',
 u'\n',
 u'\n[GARED grumbles.]',
 u'\n',
 u'\nWILL: Whatever did it to them could do it to us. They even killed the children.',
 u'\n',
 u'\nROYCE: It\u2019s a good thing we\u2019re not children. You want to run away south, run away. Of course, they will behead you as a deser

In [9]:
script_text1_01 = df_s1.script_text[0]
print type(script_text1_01)

script_text1_01

<type 'list'>


[u'[First scene opens with three Rangers riding through a tunnel, leaving the Wall, and going into the woods. (Eerie music in background) One Ranger splits off and finds a campsite full of mutilated bodies, including a child hanging from a tree branch. ',
 u' The Ranger rides back to the other two.]',
 u'\n',
 u'\n',
 u'\n',
 u'\nWILL: ',
 u'\n',
 u'\nWAYMAR ROYCE: How close did you get?',
 u'\n',
 u'\nWILL: Close as any man would.',
 u'\n',
 u'\nGARED: We should head back to the wall.',
 u'\n',
 u'\n',
 u'\n',
 u'\nGARED: Our orders were to track the wildlings. We tracked them. They won\u2019t trouble us no more.',
 u'\n',
 u'\nROYCE: You don\u2019t think he\u2019ll ask us how they died? Get back on your horse.',
 u'\n',
 u'\n[GARED grumbles.]',
 u'\n',
 u'\nWILL: Whatever did it to them could do it to us. They even killed the children.',
 u'\n',
 u'\nROYCE: It\u2019s a good thing we\u2019re not children. You want to run away south, run away. Of course, they will behead you as a deser

In [10]:
script_split = [i.split('\n') for i in script_text1_01]
script_split

[[u'[First scene opens with three Rangers riding through a tunnel, leaving the Wall, and going into the woods. (Eerie music in background) One Ranger splits off and finds a campsite full of mutilated bodies, including a child hanging from a tree branch. '],
 [u' The Ranger rides back to the other two.]'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'WILL: '],
 [u'', u''],
 [u'', u'WAYMAR ROYCE: How close did you get?'],
 [u'', u''],
 [u'', u'WILL: Close as any man would.'],
 [u'', u''],
 [u'', u'GARED: We should head back to the wall.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u'GARED: Our orders were to track the wildlings. We tracked them. They won\u2019t trouble us no more.'],
 [u'', u''],
 [u'',
  u'ROYCE: You don\u2019t think he\u2019ll ask us how they died? Get back on your horse.'],
 [u'', u''],
 [u'', u'[GARED grumbles.]'],
 [u'', u''],
 [u'',
  u'WILL: Whatever did it to them could do it to us. They even killed the children.'],
 [u'', u''],
 [u'',
  u'ROYCE: It\u201

In [11]:
string_script_text = ' '

for i in script_split:
    for e in i:
        string_script_text = string_script_text + ' ' + e

In [12]:
string_script_text

u'  [First scene opens with three Rangers riding through a tunnel, leaving the Wall, and going into the woods. (Eerie music in background) One Ranger splits off and finds a campsite full of mutilated bodies, including a child hanging from a tree branch.   The Ranger rides back to the other two.]        WILL:     WAYMAR ROYCE: How close did you get?    WILL: Close as any man would.    GARED: We should head back to the wall.        GARED: Our orders were to track the wildlings. We tracked them. They won\u2019t trouble us no more.    ROYCE: You don\u2019t think he\u2019ll ask us how they died? Get back on your horse.    [GARED grumbles.]    WILL: Whatever did it to them could do it to us. They even killed the children.    ROYCE: It\u2019s a good thing we\u2019re not children. You want to run away south, run away. Of course, they will behead you as a deserter \u2026 If I don\u2019t catch you first. Get back on your horse. I won\u2019t say it again.    [WILL glares, but obeys. Sometime late

In [13]:
words = word_tokenize(string_script_text)
words

[u'[',
 u'First',
 u'scene',
 u'opens',
 u'with',
 u'three',
 u'Rangers',
 u'riding',
 u'through',
 u'a',
 u'tunnel',
 u',',
 u'leaving',
 u'the',
 u'Wall',
 u',',
 u'and',
 u'going',
 u'into',
 u'the',
 u'woods',
 u'.',
 u'(',
 u'Eerie',
 u'music',
 u'in',
 u'background',
 u')',
 u'One',
 u'Ranger',
 u'splits',
 u'off',
 u'and',
 u'finds',
 u'a',
 u'campsite',
 u'full',
 u'of',
 u'mutilated',
 u'bodies',
 u',',
 u'including',
 u'a',
 u'child',
 u'hanging',
 u'from',
 u'a',
 u'tree',
 u'branch',
 u'.',
 u'The',
 u'Ranger',
 u'rides',
 u'back',
 u'to',
 u'the',
 u'other',
 u'two',
 u'.',
 u']',
 u'WILL',
 u':',
 u'WAYMAR',
 u'ROYCE',
 u':',
 u'How',
 u'close',
 u'did',
 u'you',
 u'get',
 u'?',
 u'WILL',
 u':',
 u'Close',
 u'as',
 u'any',
 u'man',
 u'would',
 u'.',
 u'GARED',
 u':',
 u'We',
 u'should',
 u'head',
 u'back',
 u'to',
 u'the',
 u'wall',
 u'.',
 u'GARED',
 u':',
 u'Our',
 u'orders',
 u'were',
 u'to',
 u'track',
 u'the',
 u'wildlings',
 u'.',
 u'We',
 u'tracked',
 u'them',
 u'.

In [14]:
sentences = sent_tokenize(string_script_text)
sentences

[u'  [First scene opens with three Rangers riding through a tunnel, leaving the Wall, and going into the woods.',
 u'(Eerie music in background) One Ranger splits off and finds a campsite full of mutilated bodies, including a child hanging from a tree branch.',
 u'The Ranger rides back to the other two.]',
 u'WILL:     WAYMAR ROYCE: How close did you get?',
 u'WILL: Close as any man would.',
 u'GARED: We should head back to the wall.',
 u'GARED: Our orders were to track the wildlings.',
 u'We tracked them.',
 u'They won\u2019t trouble us no more.',
 u'ROYCE: You don\u2019t think he\u2019ll ask us how they died?',
 u'Get back on your horse.',
 u'[GARED grumbles.]',
 u'WILL: Whatever did it to them could do it to us.',
 u'They even killed the children.',
 u'ROYCE: It\u2019s a good thing we\u2019re not children.',
 u'You want to run away south, run away.',
 u'Of course, they will behead you as a deserter \u2026 If I don\u2019t catch you first.',
 u'Get back on your horse.',
 u'I won\u2019

In [15]:
dialogue = []

for sentence in sentences:
    if sentence.split(':')[0] in (names1_01):
        dialogue.append(sentence)

In [16]:
dialogue

[u'WILL:     WAYMAR ROYCE: How close did you get?',
 u'WILL: Close as any man would.',
 u'GARED: We should head back to the wall.',
 u'GARED: Our orders were to track the wildlings.',
 u'ROYCE: You don\u2019t think he\u2019ll ask us how they died?',
 u'WILL: Whatever did it to them could do it to us.',
 u'ROYCE: It\u2019s a good thing we\u2019re not children.',
 u'ROYCE: Your dead men seem to have moved camp.',
 u'WILL: They were here.',
 u'GARED: See where they went.',
 u'ROYCE: What is it?',
 u'GARED: It\u2019s \u2026    [As he speaks, a CREATURE with glowing blue eyes rises behind ROYCE.',
 u'SANSA: Thank you.',
 u'SEPTA MORDANE: I love the detail that you\u2019ve managed to get in this corners.',
 u'NED: And which one of you was a marksman at ten?',
 u'JON: Don\u2019t think too much, Bran.',
 u'ROBB: Relax your bow arm.',
 u'JON/ROBB: Quick, Bran, faster!',
 u'ROBB: Lad, go run back and get the rest.',
 u'WILL: I know I broke my oath.',
 u'NED: In the name of Robert of the House Ba

In [17]:
from collections import defaultdict

speakers = defaultdict(list)
for sentence in dialogue:
    speakers[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers

defaultdict(list,
            {u'ARYA': [u' Arya.', u' That\u2019s Jaime Lannister.'],
             u'BENJEN': [u' Is he dead yet?',
              u' You got bigger.',
              u' Well, you\u2019re always welcome on the wall.',
              u' Jon\u2026    JON',
              u' The Wall isn\u2019t going anywhere.',
              u' You don\u2019t understand what you\u2019d be giving up.',
              u' You might, if you knew what it meant.',
              u' You at a feast -- It\u2019s like a bear in a trap.',
              u' Of course I did.',
              u' The two he was with are still missing.',
              u' Maybe.',
              u' Robb boy.'],
             u'BRAN': [u' Is it true he saw the White Walkers?',
              u' So he was lying?',
              u' Where will they go?',
              u' Please, father!',
              u' I saw the king!',
              u' But he\u2019s coming right now!',
              u' What?',
              u' Come on, you.',
     

In [18]:
speakers['BENJEN']

[u' Is he dead yet?',
 u' You got bigger.',
 u' Well, you\u2019re always welcome on the wall.',
 u' Jon\u2026    JON',
 u' The Wall isn\u2019t going anywhere.',
 u' You don\u2019t understand what you\u2019d be giving up.',
 u' You might, if you knew what it meant.',
 u' You at a feast -- It\u2019s like a bear in a trap.',
 u' Of course I did.',
 u' The two he was with are still missing.',
 u' Maybe.',
 u' Robb boy.']

In [19]:
episode_one = pd.DataFrame.from_dict(speakers, orient="index")
print episode_one.shape

(27, 33)


In [20]:
#from numpy import nan
#episode_one.fillna(value=str(0), inplace=True)

In [21]:
episode_one.info()

<class 'pandas.core.frame.DataFrame'>
Index: 27 entries, KHAL DROGO to ROYCE
Data columns (total 33 columns):
0     27 non-null object
1     24 non-null object
2     23 non-null object
3     19 non-null object
4     16 non-null object
5     15 non-null object
6     14 non-null object
7     13 non-null object
8     12 non-null object
9     11 non-null object
10    11 non-null object
11    8 non-null object
12    6 non-null object
13    5 non-null object
14    4 non-null object
15    4 non-null object
16    2 non-null object
17    2 non-null object
18    2 non-null object
19    2 non-null object
20    2 non-null object
21    2 non-null object
22    1 non-null object
23    1 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
31    1 non-null object
32    1 non-null object
dtypes: object(33)
memory usage: 7.2+ KB


In [22]:
episode_one.head()

0   \
KHAL DROGO                                                No.   
NED               And which one of you was a marksman at ten?   
TYRION                                                   Mmh.   
JAIME        As your brother, I feel it’s my duty to warn you   
ILLYRIO                            (Greets them in Dothraki.)   

                                                           1   \
KHAL DROGO                                                No.   
NED          In the name of Robert of the House Baratheon,...   
TYRION                       I did hear something about that.   
JAIME                                                  CERSEI   
ILLYRIO                                Come forward, my dear.   

                                                           2   \
KHAL DROGO                                                No.   
NED             King of the Andals and the First Men …    JON   
TYRION                                 And the other brother?   
JAIME        If he told the king, both our heads would be ...   
ILLYRIO                                 The ceremony is over.   

                                                           3   \
KHAL DROGO                                               None   
NED          Lord of the Seven Kingdoms and protector of t...   
TYRION                                There’s the pretty one.   
JAIME                       That’s an honor I can do without.   
ILLYRIO                                 Trust me, Your Grace.   

                                                           4   \
KHAL DROGO                                               None   
NED          The White Walkers have been gone for thousand...   
TYRION                         I hear he hates that nickname.   
JAIME                                           Don’t get up.   
ILLYRIO                                 It won’t be long now.   

                                             5   \
KHAL DROGO                                 None   
NED                 A madman sees what he sees.   
TYRION                             Clever girl.   
JAIME        I hear we might be neighbors soon.   
ILLYRIO                                   Soon.   

                                                           6   \
KHAL DROGO                                               None   
NED               There are no mountain lions in these woods.   
TYRION                         The gods gave me one blessing.   
JAIME        I’m sure we’ll have a tournament to celebrate...   
ILLYRIO                            I wouldn’t ask Khal Drogo.   

                                                           7   \
KHAL DROGO                                               None   
NED                                          Tough old beast.   
TYRION       Should I explain to you the meaning of a clos...   
JAIME                                                     No?   
ILLYRIO      If Khal Drogo has promised you a crown, you s...   

                                      8   \
KHAL DROGO                          None   
NED                     I’m sorry, Bran.   
TYRION                             JAIME   
JAIME                         Well said.   
ILLYRIO      When their omens favor war.   

                                                           9   \
KHAL DROGO                                               None   
NED                           You will train them yourselves.   
TYRION                                        Close the door!   
JAIME                                 Are you completely mad?   
ILLYRIO      A Dothraki wedding without at least three dea...   

                                             10  \
KHAL DROGO                                 None   
NED                        Hey,, hey, hey, hey.   
TYRION       Your uncle’s in the Night’s Watch.   
JAIME                           It’s all right.   
ILLYRIO                Dragons’ eggs, Daenerys.   

                                                  11

In [23]:
def remove_stops(sentence):
    characters = ['?','!','.',',',':',';']
    stoplist = stopwords.words('english') + characters
    try: 
        new_sentence = re.sub(r'[^a-zA-Z ]','', sentence)
        new_sentence = new_sentence.lower()
        new_sentence = new_sentence.split()
        new_sentence = [word for word in new_sentence if word not in stoplist]
        new_sentence = ' '.join(new_sentence)
        return new_sentence
    except:
        return sentence   

In [24]:
test = episode_one[0].apply(remove_stops)
test

KHAL DROGO                                                   
NED                                          one marksman ten
TYRION                                                    mmh
JAIME                                  brother feel duty warn
ILLYRIO                                       greets dothraki
VISERYS                                              daenerys
ROBERT                                                    cat
DAENERYS         weve guests year hes never asked us anything
ROS                                     hear kings winterfell
SEPTA MORDANE           love detail youve managed get corners
JON                                      dont think much bran
BENJEN                                               dead yet
LUWIN                                        pardon lord lady
THEON                                           mountain lion
JON/ROBB                                    quick bran faster
CERSEI                                   never worry anything
THE HOUN

In [25]:
for column in episode_one.columns:
    for x in range(len(episode_one[column])):
        episode_one[column][x] = remove_stops(episode_one[column][x])

In [26]:
episode_one.info()

<class 'pandas.core.frame.DataFrame'>
Index: 27 entries, KHAL DROGO to ROYCE
Data columns (total 33 columns):
0     27 non-null object
1     24 non-null object
2     23 non-null object
3     19 non-null object
4     16 non-null object
5     15 non-null object
6     14 non-null object
7     13 non-null object
8     12 non-null object
9     11 non-null object
10    11 non-null object
11    8 non-null object
12    6 non-null object
13    5 non-null object
14    4 non-null object
15    4 non-null object
16    2 non-null object
17    2 non-null object
18    2 non-null object
19    2 non-null object
20    2 non-null object
21    2 non-null object
22    1 non-null object
23    1 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
31    1 non-null object
32    1 non-null object
dtypes: object(33)
memory usage: 7.2+ KB


In [27]:
episode_one.index = episode_one.index.str.title()

In [28]:
episode_one.shape

(27, 33)

In [29]:
episode_one.head()

0   \
Khal Drogo                           
Ned               one marksman ten   
Tyrion                         mmh   
Jaime       brother feel duty warn   
Illyrio            greets dothraki   

                                                         1   \
Khal Drogo                                                    
Ned         name robert house baratheon first name jon bran   
Tyrion                                       hear something   
Jaime                                                cersei   
Illyrio                                   come forward dear   

                                                   2   \
Khal Drogo                                              
Ned                         king andals first men jon   
Tyrion                                        brother   
Jaime       told king heads would skewered city gates   
Illyrio                                      ceremony   

                                                           3   \
Khal Drogo                                               None   
Ned         lord seven kingdoms protector realm eddard hou...   
Tyrion                                      theres pretty one   
Jaime                                     thats honor without   
Illyrio                                           trust grace   

                                            4                          5   \
Khal Drogo                                None                       None   
Ned         white walkers gone thousands years           madman sees sees   
Tyrion                     hear hates nickname                clever girl   
Jaime                                 dont get  hear might neighbors soon   
Illyrio                              wont long                       soon   

                                                           6   \
Khal Drogo                                               None   
Ned                                      mountain lions woods   
Tyrion                                 gods gave one blessing   
Jaime       im sure well tournament celebrate new title ac...   
Illyrio                                wouldnt ask khal drogo   

                                                        7                8   \
Khal Drogo                                            None             None   
Ned                                        tough old beast    im sorry bran   
Tyrion      explain meaning closed door whorehouse brother            jaime   
Jaime                                                             well said   
Illyrio                    khal drogo promised crown shall  omens favor war   

                                                           9   \
Khal Drogo                                               None   
Ned                                                     train   
Tyrion                                             close door   
Jaime                                          completely mad   
Illyrio     dothraki wedding without least three deaths co...   

                               10                    11                 12  \
Khal Drogo                   None                  None               None   
Ned               hey hey hey hey  guarding north grace              queen   
Tyrion        uncles nights watch                offend  lady stark mother   
Jaime                       right      heard first time                ten   
Illyrio     dragons eggs daenerys                  None               None   

                                       13  \
Khal Drogo                           None   
Ned                        tell jon arryn   
Tyrion      dwarves bastards fathers eyes   
Jaime                         things love   
Illyrio                              None   

                                               14             15  \
Khal Drogo                                   None           None   
Ned                                                          aye   
Tyrion      get without sq

### Episode Two

In [30]:
df_s1.script_text[1]

[u'\n',
 u'\n',
 u'Jorah Mormont:',
 u' You need to drink, child... And eat.',
 u'\n',
 u'\n',
 u'Daenerys Targaryen:',
 u" Isn't there anything else?",
 u'\n',
 u'\n',
 u'Jorah Mormont:',
 u" The Dothraki have two things in abundance: grass and horses. People can't live on grass... In the Shadow Lands beyond Asshai, they say there are fields of ghost grass with stalks as pale as milk that glow in the night. It murders all other grass. The Dothraki believe that one day it will cover everything. That's the way the world will end\u2026 It'll get easier.",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Doreah:',
 u' Khaleesi!',
 u'\n',
 u'Irri:',
 u' Your hands.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Jorah Mormont:',
 u" We're still not far from Pentos, your Grace. Magister Illyrio has extended his hospitality. You'd be more comfortable there.",
 u'\n',
 u'Viserys Targaryen:',
 u" I have no interest in hospitality or comfort. I'll stay with Drogo until he fulfils his end of the bargain and I have my cr

In [31]:
script_text1_02 = df_s1.script_text[1]
print type(script_text1_02)

script_text1_02

<type 'list'>


[u'\n',
 u'\n',
 u'Jorah Mormont:',
 u' You need to drink, child... And eat.',
 u'\n',
 u'\n',
 u'Daenerys Targaryen:',
 u" Isn't there anything else?",
 u'\n',
 u'\n',
 u'Jorah Mormont:',
 u" The Dothraki have two things in abundance: grass and horses. People can't live on grass... In the Shadow Lands beyond Asshai, they say there are fields of ghost grass with stalks as pale as milk that glow in the night. It murders all other grass. The Dothraki believe that one day it will cover everything. That's the way the world will end\u2026 It'll get easier.",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Doreah:',
 u' Khaleesi!',
 u'\n',
 u'Irri:',
 u' Your hands.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Jorah Mormont:',
 u" We're still not far from Pentos, your Grace. Magister Illyrio has extended his hospitality. You'd be more comfortable there.",
 u'\n',
 u'Viserys Targaryen:',
 u" I have no interest in hospitality or comfort. I'll stay with Drogo until he fulfils his end of the bargain and I have my cr

In [32]:
script_split2 = [i.split('\n') for i in script_text1_02]
script_split2

[[u'', u''],
 [u'', u''],
 [u'Jorah Mormont:'],
 [u' You need to drink, child... And eat.'],
 [u'', u''],
 [u'', u''],
 [u'Daenerys Targaryen:'],
 [u" Isn't there anything else?"],
 [u'', u''],
 [u'', u''],
 [u'Jorah Mormont:'],
 [u" The Dothraki have two things in abundance: grass and horses. People can't live on grass... In the Shadow Lands beyond Asshai, they say there are fields of ghost grass with stalks as pale as milk that glow in the night. It murders all other grass. The Dothraki believe that one day it will cover everything. That's the way the world will end\u2026 It'll get easier."],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Doreah:'],
 [u' Khaleesi!'],
 [u'', u''],
 [u'Irri:'],
 [u' Your hands.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Jorah Mormont:'],
 [u" We're still not far from Pentos, your Grace. Magister Illyrio has extended his hospitality. You'd be more comfortable there."],
 [u'', u''],
 [u'Viserys Targaryen:'],
 [u" I have no intere

In [33]:
string_script_text2 = ' '

for i in script_split2:
    for e in i:
        string_script_text2 = string_script_text2 + ' ' + e

In [34]:
string_script_text2

u'      Jorah Mormont:  You need to drink, child... And eat.     Daenerys Targaryen:  Isn\'t there anything else?     Jorah Mormont:  The Dothraki have two things in abundance: grass and horses. People can\'t live on grass... In the Shadow Lands beyond Asshai, they say there are fields of ghost grass with stalks as pale as milk that glow in the night. It murders all other grass. The Dothraki believe that one day it will cover everything. That\'s the way the world will end\u2026 It\'ll get easier.         Doreah:  Khaleesi!   Irri:  Your hands.         Jorah Mormont:  We\'re still not far from Pentos, your Grace. Magister Illyrio has extended his hospitality. You\'d be more comfortable there.   Viserys Targaryen:  I have no interest in hospitality or comfort. I\'ll stay with Drogo until he fulfils his end of the bargain and I have my crown.   Jorah Mormont:  As you wish, your Grace.      - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -         Joffrey Ba

In [35]:
words2 = word_tokenize(string_script_text2)
words2

[u'Jorah',
 u'Mormont',
 u':',
 u'You',
 u'need',
 u'to',
 u'drink',
 u',',
 u'child',
 u'...',
 u'And',
 u'eat',
 u'.',
 u'Daenerys',
 u'Targaryen',
 u':',
 u'Is',
 u"n't",
 u'there',
 u'anything',
 u'else',
 u'?',
 u'Jorah',
 u'Mormont',
 u':',
 u'The',
 u'Dothraki',
 u'have',
 u'two',
 u'things',
 u'in',
 u'abundance',
 u':',
 u'grass',
 u'and',
 u'horses',
 u'.',
 u'People',
 u'ca',
 u"n't",
 u'live',
 u'on',
 u'grass',
 u'...',
 u'In',
 u'the',
 u'Shadow',
 u'Lands',
 u'beyond',
 u'Asshai',
 u',',
 u'they',
 u'say',
 u'there',
 u'are',
 u'fields',
 u'of',
 u'ghost',
 u'grass',
 u'with',
 u'stalks',
 u'as',
 u'pale',
 u'as',
 u'milk',
 u'that',
 u'glow',
 u'in',
 u'the',
 u'night',
 u'.',
 u'It',
 u'murders',
 u'all',
 u'other',
 u'grass',
 u'.',
 u'The',
 u'Dothraki',
 u'believe',
 u'that',
 u'one',
 u'day',
 u'it',
 u'will',
 u'cover',
 u'everything',
 u'.',
 u'That',
 u"'s",
 u'the',
 u'way',
 u'the',
 u'world',
 u'will',
 u'end\u2026',
 u'It',
 u"'ll",
 u'get',
 u'easier',
 u'.

In [36]:
sentences2 = sent_tokenize(string_script_text2)
sentences2

[u'      Jorah Mormont:  You need to drink, child... And eat.',
 u"Daenerys Targaryen:  Isn't there anything else?",
 u'Jorah Mormont:  The Dothraki have two things in abundance: grass and horses.',
 u"People can't live on grass...",
 u'In the Shadow Lands beyond Asshai, they say there are fields of ghost grass with stalks as pale as milk that glow in the night.',
 u'It murders all other grass.',
 u'The Dothraki believe that one day it will cover everything.',
 u"That's the way the world will end\u2026 It'll get easier.",
 u'Doreah:  Khaleesi!',
 u'Irri:  Your hands.',
 u"Jorah Mormont:  We're still not far from Pentos, your Grace.",
 u'Magister Illyrio has extended his hospitality.',
 u"You'd be more comfortable there.",
 u'Viserys Targaryen:  I have no interest in hospitality or comfort.',
 u"I'll stay with Drogo until he fulfils his end of the bargain and I have my crown.",
 u'Jorah Mormont:  As you wish, your Grace.',
 u"- - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -

In [37]:
dialogue2 = []

for sentence in sentences2:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_02):
            dialogue2.append(sentence)

In [38]:
dialogue2

[u"Daenerys Targaryen:  Isn't there anything else?",
 u'Jorah Mormont:  The Dothraki have two things in abundance: grass and horses.',
 u'Doreah:  Khaleesi!',
 u'Irri:  Your hands.',
 u"Jorah Mormont:  We're still not far from Pentos, your Grace.",
 u'Viserys Targaryen:  I have no interest in hospitality or comfort.',
 u'Jorah Mormont:  As you wish, your Grace.',
 u'Tyrion Lannister:  Before you go, you will call on Lord and Lady Stark and offer your sympathies.',
 u'Joffrey Baratheon:  What good will my sympathies do them?',
 u'Tyrion Lannister:  None.',
 u'Joffrey Baratheon:  The boy means nothing to me.',
 u"Tyrion Lannister:  One word and I'll hit you again.",
 u"Joffrey Baratheon:  I'm telling mother!",
 u'Tyrion Lannister:  Go!',
 u"Joffrey Baratheon:  You can't...   Tyrion Lannister:  Do you understand?",
 u'Tyrion Lannister:  Bread.',
 u'Jaime Lannister:  Little brother.',
 u'Tyrion Lannister:  Beloved siblings.',
 u'Myrcella Baratheon:  Is Bran going to die?',
 u'Tyrion Lannis

In [39]:
from collections import defaultdict

speakers2 = defaultdict(list)
for sentence in dialogue2:
    speakers2[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers2

defaultdict(list,
            {u'Arya Stark': [u'  Watch.',
              u'   Shut up.',
              u'  I think so.',
              u'   I know which end to use.',
              u'   Sansa can keep her sewing needles.',
              u'  What are you doing here?',
              u'  Stop it!',
              u'   Nymeria!',
              u"   You've got to go.",
              u'   Go!',
              u'  No.',
              u"   That's not true!",
              u"   That's not what happened!",
              u'   Liar!',
              u'  Liar!',
              u'   Liar liar liar!',
              u"  Lady wasn't there!"],
             u'Assassin': [u"  You're not supposed to be here."],
             u'Catelyn Stark': [u'   I would have dressed, your Grace.',
              u'  I never knew.',
              u'   I am grateful..   Cersei Baratheon',
              u"   You've said it.",
              u'  I want you to leave.',
              u'  17 years ago you rode off with Robert Barath

In [40]:
speakers2['Arya Stark']

[u'  Watch.',
 u'   Shut up.',
 u'  I think so.',
 u'   I know which end to use.',
 u'   Sansa can keep her sewing needles.',
 u'  What are you doing here?',
 u'  Stop it!',
 u'   Nymeria!',
 u"   You've got to go.",
 u'   Go!',
 u'  No.',
 u"   That's not true!",
 u"   That's not what happened!",
 u'   Liar!',
 u'  Liar!',
 u'   Liar liar liar!',
 u"  Lady wasn't there!"]

In [41]:
episode_two = pd.DataFrame.from_dict(speakers2, orient="index")
print episode_two.shape

(27, 30)


In [42]:
#from numpy import nan
#episode_two.fillna(value=str(0), inplace=True)

In [43]:
episode_two.info()

<class 'pandas.core.frame.DataFrame'>
Index: 27 entries, Joffrey Baratheon to Jon Snow
Data columns (total 30 columns):
0     27 non-null object
1     21 non-null object
2     18 non-null object
3     16 non-null object
4     11 non-null object
5     11 non-null object
6     11 non-null object
7     11 non-null object
8     11 non-null object
9     10 non-null object
10    10 non-null object
11    9 non-null object
12    8 non-null object
13    7 non-null object
14    7 non-null object
15    6 non-null object
16    5 non-null object
17    3 non-null object
18    1 non-null object
19    1 non-null object
20    1 non-null object
21    1 non-null object
22    1 non-null object
23    1 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
dtypes: object(30)
memory usage: 6.5+ KB


In [44]:
episode_two.head()

0   \
Joffrey Baratheon              What good will my sympathies do them?   
Cersei Baratheon                                   What do you mean?   
Robert Baratheon     What do you say, just you and me on the King...   
Eddard Stark                                       I have no choice.   
Jaime Lannister                                      Little brother.   

                                                                  1   \
Joffrey Baratheon                       The boy means nothing to me.   
Cersei Baratheon     It's no mercy, letting a child linger in suc...   
Robert Baratheon     There were wars to fight, women to marry... ...   
Eddard Stark                                                You can.   
Jaime Lannister      Tell me you're not thinking of taking the bl...   

                                                                  2   \
Joffrey Baratheon                                I'm telling mother!   
Cersei Baratheon                 I still can't believe you're going.   
Robert Baratheon        There was that one... Oh, what was her name?   
Eddard Stark         The next time we see each other, we'll talk ...   
Jaime Lannister                                            Good man.   

                                                              3   \
Joffrey Baratheon                You can't...   Tyrion Lannister   
Cersei Baratheon     The children don't need to hear your filth.   
Robert Baratheon                                         Bessie!   
Eddard Stark                    I've half a mind to go with you.   
Jaime Lannister                              At someone, I mean.   

                                                               4   \
Joffrey Baratheon     My princess can drink as much as she wants.   
Cersei Baratheon                               This is your home.   
Robert Baratheon                                       That's it.   
Eddard Stark               You should have asked me 20 years ago.   
Jaime Lannister                                              None   

                                                        5   \
Joffrey Baratheon                             Your sister?   
Cersei Baratheon                         It was years ago.   
Robert Baratheon     Trust me, that's not the worst thing.   
Eddard Stark                       I recall a few chances.   
Jaime Lannister                                       None   

                                                                  6   \
Joffrey Baratheon      A butcher's boy who wants to be a Knight, eh?   
Cersei Baratheon      How dare you speak to your King in that man...   
Robert Baratheon     Soon enough that child will spread her legs ...   
Eddard Stark                                                 Bessie.   
Jaime Lannister                                                 None   

                                                                  7   \
Joffrey Baratheon     I'm your prince, not your lord, and I said ...   
Cersei Baratheon     Your girl and that butcher's boy attacked my...   
Robert Baratheon                        Oh, it's unspeakable to you?   
Eddard Stark                                                  Wylla.   
Jaime Lannister                                                 None   

                                                                  8   \
Joffrey Baratheon                           And you're not a Knight.   
Cersei Baratheon                      Joffrey told us what happened.   
Robert Baratheon      This Khal Drogo, it's said he has 100,000 m...   
Eddard Stark                          Nor will I.   Robert Baratheon   
Jaime Lannister                                                 None   

                                                                  9   \
Joffrey Baratheon                          I won't hurt him... Much.   
Cersei Baratheon                                          She's not.   
Robert Baratheon      There are still those in the Seve

In [45]:
test2 = episode_two[0].apply(remove_stops)
test2

Joffrey Baratheon                                       good sympathies
Cersei Baratheon                                                   mean
Robert Baratheon      say kingsroad swords sides couple tavern wench...
Eddard Stark                                                     choice
Jaime Lannister                                          little brother
Jhiqui                                                            known
Theon Greyjoy                                                  saw lady
Mycah                                                           ill get
Irri                                                              hands
Arya Stark                                                        watch
Tyrion Lannister               go call lord lady stark offer sympathies
Catelyn Stark                                       would dressed grace
Soldier                                      found trace direwolf grace
Viserys Targaryen                          interest hospitality 

In [46]:
for column in episode_two.columns:
    for x in range(len(episode_two[column])):
        episode_two[column][x] = remove_stops(episode_two[column][x])

In [47]:
episode_two.info()

<class 'pandas.core.frame.DataFrame'>
Index: 27 entries, Joffrey Baratheon to Jon Snow
Data columns (total 30 columns):
0     27 non-null object
1     21 non-null object
2     18 non-null object
3     16 non-null object
4     11 non-null object
5     11 non-null object
6     11 non-null object
7     11 non-null object
8     11 non-null object
9     10 non-null object
10    10 non-null object
11    9 non-null object
12    8 non-null object
13    7 non-null object
14    7 non-null object
15    6 non-null object
16    5 non-null object
17    3 non-null object
18    1 non-null object
19    1 non-null object
20    1 non-null object
21    1 non-null object
22    1 non-null object
23    1 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
dtypes: object(30)
memory usage: 6.5+ KB


In [48]:
episode_two.shape

(27, 30)

In [49]:
episode_two.head()

0   \
Joffrey Baratheon                                    good sympathies   
Cersei Baratheon                                                mean   
Robert Baratheon   say kingsroad swords sides couple tavern wench...   
Eddard Stark                                                  choice   
Jaime Lannister                                       little brother   

                                                          1   \
Joffrey Baratheon                          boy means nothing   
Cersei Baratheon             mercy letting child linger pain   
Robert Baratheon   wars fight women marry never chance young   
Eddard Stark                                                   
Jaime Lannister             tell youre thinking taking black   

                                               2   \
Joffrey Baratheon               im telling mother   
Cersei Baratheon   still cant believe youre going   
Robert Baratheon                      one oh name   
Eddard Stark       next time see well talk mother   
Jaime Lannister                          good man   

                                              3                          4   \
Joffrey Baratheon          cant tyrion lannister  princess drink much wants   
Cersei Baratheon   children dont need hear filth                       home   
Robert Baratheon                          bessie                      thats   
Eddard Stark                    ive half mind go            asked years ago   
Jaime Lannister                     someone mean                       None   

                                        5   \
Joffrey Baratheon                   sister   
Cersei Baratheon                 years ago   
Robert Baratheon   trust thats worst thing   
Eddard Stark                recall chances   
Jaime Lannister                       None   

                                                             6   \
Joffrey Baratheon                  butchers boy wants knight eh   
Cersei Baratheon                         dare speak king manner   
Robert Baratheon   soon enough child spread legs start breeding   
Eddard Stark                                             bessie   
Jaime Lannister                                            None   

                                               7                          8   \
Joffrey Baratheon  im prince lord said pick sword               youre knight   
Cersei Baratheon   girl butchers boy attacked son   joffrey told us happened   
Robert Baratheon                   oh unspeakable  khal drogo said men horde   
Eddard Stark                                wylla           robert baratheon   
Jaime Lannister                              None                       None   

                                                  9                    10  \
Joffrey Baratheon                     wont hurt much  ill gut little cunt   
Cersei Baratheon                                shes     shes wild animal   
Robert Baratheon   still seven kingdoms call usurper          quiet woman   
Eddard Stark                  worst thing coronation    shes little child   
Jaime Lannister                                 None                 None   

                                             11                   12  \
Joffrey Baratheon                   please dont                   go   
Cersei Baratheon   joffrey bear scars rest life             direwolf   
Robert Baratheon                         enough  child tell happened   
Eddard Stark                      tell speaking   cant get hands one   
Jaime Lannister                            None                 None   

                                                                  13  \
Joffrey Baratheon                                                yes   
Cersei Baratheon                                        another wolf   
Robert Baratheon                                  would whip streets   
Eddard Stark       even million dothraki threat realm long remain...   
Jaime Lannister                      

### Episode Three

In [50]:
df_s1.script_text[2]

[u'\n',
 u'\n',
 u'King\u2019s Landing Guard:',
 u' Welcome, Lord Stark. Grand Maester Pycelle has called a meeting of the Small Council. The honor of your presence is requested.',
 u'\n',
 u'Eddard Stark: ',
 u"Get the girls settled in. I'll be back in time for supper. And, Jory, you go with them.",
 u'\n',
 u'Jory Cassel:',
 u' Yes, my Lord.',
 u'\n',
 u'King\u2019s Landing Guard:',
 u" If you'd like to change into something more appropriate\u2026",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Jaime Lannister:',
 u" Thank the gods you're here, Stark. About time we had some stern northern leadership.",
 u'\n',
 u'Eddard Stark: ',
 u"Glad to see you're protecting the throne.",
 u'\n',
 u'Jaime Lannister:',
 u" Sturdy old thing. How many kings' asses have polished it, I wonder? What's the line? The King shits and the Hand wipes.",
 u'\n',
 u'Eddard Stark: ',
 u' Very handsome armor. Not a scratch on it.',
 u'\n',
 u'Jaime Lannister:',
 u' I know. People have been swinging at me for years, but the

In [51]:
script_text1_03 = df_s1.script_text[2]
print type(script_text1_03)

script_text1_03

<type 'list'>


[u'\n',
 u'\n',
 u'King\u2019s Landing Guard:',
 u' Welcome, Lord Stark. Grand Maester Pycelle has called a meeting of the Small Council. The honor of your presence is requested.',
 u'\n',
 u'Eddard Stark: ',
 u"Get the girls settled in. I'll be back in time for supper. And, Jory, you go with them.",
 u'\n',
 u'Jory Cassel:',
 u' Yes, my Lord.',
 u'\n',
 u'King\u2019s Landing Guard:',
 u" If you'd like to change into something more appropriate\u2026",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Jaime Lannister:',
 u" Thank the gods you're here, Stark. About time we had some stern northern leadership.",
 u'\n',
 u'Eddard Stark: ',
 u"Glad to see you're protecting the throne.",
 u'\n',
 u'Jaime Lannister:',
 u" Sturdy old thing. How many kings' asses have polished it, I wonder? What's the line? The King shits and the Hand wipes.",
 u'\n',
 u'Eddard Stark: ',
 u' Very handsome armor. Not a scratch on it.',
 u'\n',
 u'Jaime Lannister:',
 u' I know. People have been swinging at me for years, but the

In [52]:
script_split3 = [i.split('\n') for i in script_text1_03]
script_split3

[[u'', u''],
 [u'', u''],
 [u'King\u2019s Landing Guard:'],
 [u' Welcome, Lord Stark. Grand Maester Pycelle has called a meeting of the Small Council. The honor of your presence is requested.'],
 [u'', u''],
 [u'Eddard Stark: '],
 [u"Get the girls settled in. I'll be back in time for supper. And, Jory, you go with them."],
 [u'', u''],
 [u'Jory Cassel:'],
 [u' Yes, my Lord.'],
 [u'', u''],
 [u'King\u2019s Landing Guard:'],
 [u" If you'd like to change into something more appropriate\u2026"],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Jaime Lannister:'],
 [u" Thank the gods you're here, Stark. About time we had some stern northern leadership."],
 [u'', u''],
 [u'Eddard Stark: '],
 [u"Glad to see you're protecting the throne."],
 [u'', u''],
 [u'Jaime Lannister:'],
 [u" Sturdy old thing. How many kings' asses have polished it, I wonder? What's the line? The King shits and the Hand wipes."],
 [u'', u''],
 [u'Eddard Stark: '],
 [u' Very handsome armor. Not a scratch on it.'],


In [53]:
string_script_text3 = ' '

for i in script_split3:
    for e in i:
        string_script_text3 = string_script_text3 + ' ' + e

In [54]:
string_script_text3

u'      King\u2019s Landing Guard:  Welcome, Lord Stark. Grand Maester Pycelle has called a meeting of the Small Council. The honor of your presence is requested.   Eddard Stark:  Get the girls settled in. I\'ll be back in time for supper. And, Jory, you go with them.   Jory Cassel:  Yes, my Lord.   King\u2019s Landing Guard:  If you\'d like to change into something more appropriate\u2026         Jaime Lannister:  Thank the gods you\'re here, Stark. About time we had some stern northern leadership.   Eddard Stark:  Glad to see you\'re protecting the throne.   Jaime Lannister:  Sturdy old thing. How many kings\' asses have polished it, I wonder? What\'s the line? The King shits and the Hand wipes.   Eddard Stark:   Very handsome armor. Not a scratch on it.   Jaime Lannister:  I know. People have been swinging at me for years, but they always seem to miss.   Eddard Stark:  You\'ve chosen your opponents wisely then.          - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - 

In [55]:
words3 = word_tokenize(string_script_text3)
words3

[u'King\u2019s',
 u'Landing',
 u'Guard',
 u':',
 u'Welcome',
 u',',
 u'Lord',
 u'Stark',
 u'.',
 u'Grand',
 u'Maester',
 u'Pycelle',
 u'has',
 u'called',
 u'a',
 u'meeting',
 u'of',
 u'the',
 u'Small',
 u'Council',
 u'.',
 u'The',
 u'honor',
 u'of',
 u'your',
 u'presence',
 u'is',
 u'requested',
 u'.',
 u'Eddard',
 u'Stark',
 u':',
 u'Get',
 u'the',
 u'girls',
 u'settled',
 u'in',
 u'.',
 u'I',
 u"'ll",
 u'be',
 u'back',
 u'in',
 u'time',
 u'for',
 u'supper',
 u'.',
 u'And',
 u',',
 u'Jory',
 u',',
 u'you',
 u'go',
 u'with',
 u'them',
 u'.',
 u'Jory',
 u'Cassel',
 u':',
 u'Yes',
 u',',
 u'my',
 u'Lord',
 u'.',
 u'King\u2019s',
 u'Landing',
 u'Guard',
 u':',
 u'If',
 u'you',
 u"'d",
 u'like',
 u'to',
 u'change',
 u'into',
 u'something',
 u'more',
 u'appropriate\u2026',
 u'Jaime',
 u'Lannister',
 u':',
 u'Thank',
 u'the',
 u'gods',
 u'you',
 u"'re",
 u'here',
 u',',
 u'Stark',
 u'.',
 u'About',
 u'time',
 u'we',
 u'had',
 u'some',
 u'stern',
 u'northern',
 u'leadership',
 u'.',
 u'Eddard

In [56]:
sentences3 = sent_tokenize(string_script_text3)
sentences3

[u'      King\u2019s Landing Guard:  Welcome, Lord Stark.',
 u'Grand Maester Pycelle has called a meeting of the Small Council.',
 u'The honor of your presence is requested.',
 u'Eddard Stark:  Get the girls settled in.',
 u"I'll be back in time for supper.",
 u'And, Jory, you go with them.',
 u'Jory Cassel:  Yes, my Lord.',
 u"King\u2019s Landing Guard:  If you'd like to change into something more appropriate\u2026         Jaime Lannister:  Thank the gods you're here, Stark.",
 u'About time we had some stern northern leadership.',
 u"Eddard Stark:  Glad to see you're protecting the throne.",
 u'Jaime Lannister:  Sturdy old thing.',
 u"How many kings' asses have polished it, I wonder?",
 u"What's the line?",
 u'The King shits and the Hand wipes.',
 u'Eddard Stark:   Very handsome armor.',
 u'Not a scratch on it.',
 u'Jaime Lannister:  I know.',
 u'People have been swinging at me for years, but they always seem to miss.',
 u"Eddard Stark:  You've chosen your opponents wisely then.",
 u'

In [57]:
dialogue3 = []

for sentence in sentences3:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_03):
            dialogue3.append(sentence)

/Users/zoemarkovits/anaconda/lib/python2.7/site-packages/ipykernel_launcher.py:6: UnicodeWarning: Unicode equal comparison failed to convert both arguments to Unicode - interpreting them as being unequal
  


In [58]:
dialogue3

[u'Eddard Stark:  Get the girls settled in.',
 u'Jory Cassel:  Yes, my Lord.',
 u"Eddard Stark:  Glad to see you're protecting the throne.",
 u'Jaime Lannister:  Sturdy old thing.',
 u'Eddard Stark:   Very handsome armor.',
 u'Jaime Lannister:  I know.',
 u"Eddard Stark:  You've chosen your opponents wisely then.",
 u'Eddard Stark:  Lord Varys.',
 u'Varys:  I was grievously sorry to hear of your troubles on the Kingsroad.',
 u"Eddard Stark:   A shame you didn't say a prayer for the butcher's son.",
 u'Renly Baratheon:  And you look tired from the road.',
 u'Eddard Stark:   Grand Maester.',
 u'Eddard Stark:  And you served another King.',
 u'Eddard Stark:   Without the King?',
 u"Renly Baratheon:  Winter may be coming, but I'm afraid the same cannot be said for my brother.",
 u'Varys:  His Grace has many cares.',
 u'Petyr Baelish:   We are the lords of small matters here.',
 u"Renly Baratheon:  My brother instructs us to stage a tournament in honor of Lord Stark's appointment as Hand of

In [59]:
from collections import defaultdict

speakers3 = defaultdict(list)
for sentence in dialogue3:
    speakers3[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers3

defaultdict(list,
            {u'Alliser Thorne': [u'  Next!',
              u'  Next!',
              u"  Lord Snow, it appears you're the least useless person here."],
             u'Arya Stark': [u"   I'm practicing.",
              u'  The Prince.',
              u'  The Hound does whatever the Prince tells him to do.',
              u"  You're a liar.",
              u'  Go away!',
              u'   Mine.',
              u"  I wasn't playing.",
              u"   It's called Needle.",
              u"  Stick 'em with the pointy end.",
              u'  I was trying to learn.',
              u'  I hate them!',
              u'  So was I!',
              u'  But how you can let her marry someone like that?',
              u'  Winter is coming.',
              u"  I don't hate her.",
              u'  I can keep it?',
              u'   Who are you?',
              u"   It's too heavy.",
              u'  What if I drop it?',
              u"  I'm a girl."],
             u'Barristan

In [60]:
speakers3['Arya Stark']

[u"   I'm practicing.",
 u'  The Prince.',
 u'  The Hound does whatever the Prince tells him to do.',
 u"  You're a liar.",
 u'  Go away!',
 u'   Mine.',
 u"  I wasn't playing.",
 u"   It's called Needle.",
 u"  Stick 'em with the pointy end.",
 u'  I was trying to learn.',
 u'  I hate them!',
 u'  So was I!',
 u'  But how you can let her marry someone like that?',
 u'  Winter is coming.',
 u"  I don't hate her.",
 u'  I can keep it?',
 u'   Who are you?',
 u"   It's too heavy.",
 u'  What if I drop it?',
 u"  I'm a girl."]

In [61]:
episode_three = pd.DataFrame.from_dict(speakers3, orient="index")
print episode_three.shape

(37, 37)


In [62]:
#from numpy import nan
#episode_three.fillna(value=str(0), inplace=True)

In [63]:
episode_three.info()

<class 'pandas.core.frame.DataFrame'>
Index: 37 entries, Joffrey Baratheon to Jon Snow
Data columns (total 37 columns):
0     37 non-null object
1     32 non-null object
2     28 non-null object
3     23 non-null object
4     20 non-null object
5     18 non-null object
6     16 non-null object
7     13 non-null object
8     10 non-null object
9     9 non-null object
10    7 non-null object
11    6 non-null object
12    6 non-null object
13    6 non-null object
14    5 non-null object
15    4 non-null object
16    4 non-null object
17    4 non-null object
18    3 non-null object
19    3 non-null object
20    2 non-null object
21    2 non-null object
22    2 non-null object
23    2 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
31    1 non-null object
32    1 non-null object
33    1 non-null object
34    1 non-null object
35    1 non-null object
36    1

In [64]:
episode_three.head()

0   \
Joffrey Baratheon                                         It's ugly.   
Benjen Stark                                   I'm the First Ranger.   
Petyr Baelish                We are the lords of small matters here.   
Cersei Baratheon     A King should have scars, you fought off a d...   
Robert Baratheon                                         Who was it?   

                                                     1   \
Joffrey Baratheon                     I'm not like him.   
Benjen Stark          The kind I don't want to believe.   
Petyr Baelish                            Mmm, how much?   
Cersei Baratheon                       That's not true.   
Robert Baratheon                       How'd you do it?   

                                                                  2   \
Joffrey Baratheon                            Do I have to marry her?   
Benjen Stark                                       You're not going.   
Petyr Baelish        I'm telling you the Crown is six million in ...   
Cersei Baratheon                                                Yes.   
Robert Baratheon                                          Quick one.   

                                                             3   \
Joffrey Baratheon                              I don't want to.   
Benjen Stark         The Night's Watch is a joke to you, is it?   
Petyr Baelish               The Master of Coin finds the money.   
Cersei Baratheon                              No, but you will.   
Robert Baratheon                   What do you mean it's empty?   

                                                                  4   \
Joffrey Baratheon           We allow the northerners too much power.   
Benjen Stark          I hope we've provided you with some good st...   
Petyr Baelish                                           As you will.   
Cersei Baratheon                          How would you handle them?   
Robert Baratheon                          Is that what empty means?!   

                                                                  5   \
Joffrey Baratheon     I'd double their taxes and command them to ...   
Benjen Stark                                  Call me what you like.   
Petyr Baelish                                                   Cat!   
Cersei Baratheon                                       A royal army?   
Robert Baratheon                                                None   

                                                                  6   \
Joffrey Baratheon         Why should every lord command his own men?   
Benjen Stark         You know, my brother once told me that nothi...   
Petyr Baelish                 No one will come looking for you here.   
Cersei Baratheon                       And if the northerners rebel?   
Robert Baratheon                                                None   

                                                                  7   \
Joffrey Baratheon                                    I'd crush them.   
Benjen Stark                                           You're right.   
Petyr Baelish                                 A dear friend told me.   
Cersei Baratheon     And these 10,000 northern troops, would they...   
Robert Baratheon                                                None   

                                                                  8   \
Joffrey Baratheon                                            For me.   
Benjen Stark                             Enjoy the capital, brother.   
Petyr Baelish                                             Good news?   
Cersei Baratheon      But you've just invaded their homeland, ask...   
Robert Baratheon                                                None   

                                                                  9   \
Joffrey Baratheon                                    I'm not asking.   
Benjen Stark                                                    None   
Petyr Baelish                                                

In [65]:
test3 = episode_three[0].apply(remove_stops)
test3

Joffrey Baratheon                                         ugly
Benjen Stark                                   im first ranger
Petyr Baelish                              lords small matters
Cersei Baratheon                    king scars fought direwolf
Robert Baratheon                                              
Khal Drogo                                                know
Rast                                                care faces
Yoren                        brains guts lungs heart fried fat
Maester Aemon                    many winters seen lord tyrion
Tyrion Lannister                                  charming man
Pyp                                   wonder theyd find wolves
Eddard Stark                                 get girls settled
Bran Stark                                               maybe
Irri                            rakharo ask want dead khaleesi
Arya Stark                                       im practicing
Jaime Lannister                               sturdy ol

In [66]:
for column in episode_three.columns:
    for x in range(len(episode_three[column])):
        episode_three[column][x] = remove_stops(episode_three[column][x])

In [67]:
episode_three.info()

<class 'pandas.core.frame.DataFrame'>
Index: 37 entries, Joffrey Baratheon to Jon Snow
Data columns (total 37 columns):
0     37 non-null object
1     32 non-null object
2     28 non-null object
3     23 non-null object
4     20 non-null object
5     18 non-null object
6     16 non-null object
7     13 non-null object
8     10 non-null object
9     9 non-null object
10    7 non-null object
11    6 non-null object
12    6 non-null object
13    6 non-null object
14    5 non-null object
15    4 non-null object
16    4 non-null object
17    4 non-null object
18    3 non-null object
19    3 non-null object
20    2 non-null object
21    2 non-null object
22    2 non-null object
23    2 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
31    1 non-null object
32    1 non-null object
33    1 non-null object
34    1 non-null object
35    1 non-null object
36    1

In [68]:
episode_three.head()

0                       1   \
Joffrey Baratheon                        ugly                 im like   
Benjen Stark                  im first ranger  kind dont want believe   
Petyr Baelish             lords small matters                mmm much   
Cersei Baratheon   king scars fought direwolf              thats true   
Robert Baratheon                                                 howd   

                                                  2                        3   \
Joffrey Baratheon                              marry                dont want   
Benjen Stark                             youre going        nights watch joke   
Petyr Baelish      im telling crown six million debt  master coin finds money   
Cersei Baratheon                                 yes                            
Robert Baratheon                           quick one               mean empty   

                                                                  4   \
Joffrey Baratheon                       allow northerners much power   
Benjen Stark       hope weve provided good stories tell youre bac...   
Petyr Baelish                                                          
Cersei Baratheon                                        would handle   
Robert Baratheon                                         empty means   

                                                              5   \
Joffrey Baratheon  id double taxes command supply men royal army   
Benjen Stark                                           call like   
Petyr Baelish                                                cat   
Cersei Baratheon                                      royal army   
Robert Baratheon                                            None   

                                                                  6   \
Joffrey Baratheon                             every lord command men   
Benjen Stark       know brother told nothing someone says word re...   
Petyr Baelish                                       one come looking   
Cersei Baratheon                                   northerners rebel   
Robert Baratheon                                                None   

                                                 7   \
Joffrey Baratheon                          id crush   
Benjen Stark                            youre right   
Petyr Baelish                      dear friend told   
Cersei Baratheon   northern troops would fight lord   
Robert Baratheon                               None   

                                                           8   \
Joffrey Baratheon                                               
Benjen Stark                            enjoy capital brother   
Petyr Baelish                                       good news   
Cersei Baratheon   youve invaded homeland asked kill brothers   
Robert Baratheon                                         None   

                                           9                       10  \
Joffrey Baratheon                   im asking                   agree   
Benjen Stark                             None                    None   
Petyr Baelish                                     thought shed safest   
Cersei Baratheon   north cannot held outsider  everyone isnt us enemy   
Robert Baratheon                         None                    None   

                                       11                       12  \
Joffrey Baratheon                    None                     None   
Benjen Stark                         None                     None   
Petyr Baelish      lord tyrion say stolen  ill try keep alive sake   
Cersei Baratheon      hes child years old                  nothing   
Robert Baratheon                     None                     None   

                                 13       14      15      16          17  \
Joffrey Baratheon              None     None    None    None        None   
Benjen Stark                   None     None    None    None        None   
Petyr Baelish      dont tell any

### Episode Four

In [69]:
df_s1.script_text[3]

[u'\n',
 u'\n',
 u'Old Nan:',
 u" The little Lord's been dreaming again.",
 u'\n',
 u'Theon Greyjoy:',
 u' We have visitors.',
 u'\n',
 u'Bran Stark:',
 u" I don't want to see anyone.",
 u'\n',
 u'Theon Greyjoy:',
 u" Really? If I was cooped up all day with no one but this old bat for company, I'd go mad. Anyway, you don't have a choice. Robb's waiting.",
 u'\n',
 u'Bran Stark:',
 u" I don't want to go.",
 u'\n',
 u'Theon Greyjoy:',
 u" Neither do I. But Robb's Lord of Winterfell, which means I do what he says and you do what I say. Hodor! ",
 u' Help Bran down the hall.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Tyrion Lannister:',
 u'  I must say I received a slightly warmer welcome on my last visit.',
 u'\n',
 u'Robb Stark:',
 u" Any man of the Night's Watch is welcome at Winterfell.",
 u'\n',
 u'Tyrion Lannister:',
 u" Any man of the Night's Watch, but not I, eh, boy?",
 u'\n',
 u'Robb Stark:',
 u" I'm not your boy, Lannister. I'm Lord of Winterfell while my father is away.",
 u'\n',
 u'

In [70]:
script_text1_04 = df_s1.script_text[3]
print type(script_text1_04)

script_text1_04

<type 'list'>


[u'\n',
 u'\n',
 u'Old Nan:',
 u" The little Lord's been dreaming again.",
 u'\n',
 u'Theon Greyjoy:',
 u' We have visitors.',
 u'\n',
 u'Bran Stark:',
 u" I don't want to see anyone.",
 u'\n',
 u'Theon Greyjoy:',
 u" Really? If I was cooped up all day with no one but this old bat for company, I'd go mad. Anyway, you don't have a choice. Robb's waiting.",
 u'\n',
 u'Bran Stark:',
 u" I don't want to go.",
 u'\n',
 u'Theon Greyjoy:',
 u" Neither do I. But Robb's Lord of Winterfell, which means I do what he says and you do what I say. Hodor! ",
 u' Help Bran down the hall.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Tyrion Lannister:',
 u'  I must say I received a slightly warmer welcome on my last visit.',
 u'\n',
 u'Robb Stark:',
 u" Any man of the Night's Watch is welcome at Winterfell.",
 u'\n',
 u'Tyrion Lannister:',
 u" Any man of the Night's Watch, but not I, eh, boy?",
 u'\n',
 u'Robb Stark:',
 u" I'm not your boy, Lannister. I'm Lord of Winterfell while my father is away.",
 u'\n',
 u'

In [71]:
script_split4 = [i.split('\n') for i in script_text1_04]
script_split4

[[u'', u''],
 [u'', u''],
 [u'Old Nan:'],
 [u" The little Lord's been dreaming again."],
 [u'', u''],
 [u'Theon Greyjoy:'],
 [u' We have visitors.'],
 [u'', u''],
 [u'Bran Stark:'],
 [u" I don't want to see anyone."],
 [u'', u''],
 [u'Theon Greyjoy:'],
 [u" Really? If I was cooped up all day with no one but this old bat for company, I'd go mad. Anyway, you don't have a choice. Robb's waiting."],
 [u'', u''],
 [u'Bran Stark:'],
 [u" I don't want to go."],
 [u'', u''],
 [u'Theon Greyjoy:'],
 [u" Neither do I. But Robb's Lord of Winterfell, which means I do what he says and you do what I say. Hodor! "],
 [u' Help Bran down the hall.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Tyrion Lannister:'],
 [u'  I must say I received a slightly warmer welcome on my last visit.'],
 [u'', u''],
 [u'Robb Stark:'],
 [u" Any man of the Night's Watch is welcome at Winterfell."],
 [u'', u''],
 [u'Tyrion Lannister:'],
 [u" Any man of the Night's Watch, but not I, eh, boy?"],
 [u'', u''],
 [u

In [72]:
string_script_text4 = ' '

for i in script_split4:
    for e in i:
        string_script_text4 = string_script_text4 + ' ' + e

In [73]:
string_script_text4

u'      Old Nan:  The little Lord\'s been dreaming again.   Theon Greyjoy:  We have visitors.   Bran Stark:  I don\'t want to see anyone.   Theon Greyjoy:  Really? If I was cooped up all day with no one but this old bat for company, I\'d go mad. Anyway, you don\'t have a choice. Robb\'s waiting.   Bran Stark:  I don\'t want to go.   Theon Greyjoy:  Neither do I. But Robb\'s Lord of Winterfell, which means I do what he says and you do what I say. Hodor!   Help Bran down the hall.         Tyrion Lannister:   I must say I received a slightly warmer welcome on my last visit.   Robb Stark:  Any man of the Night\'s Watch is welcome at Winterfell.   Tyrion Lannister:  Any man of the Night\'s Watch, but not I, eh, boy?   Robb Stark:  I\'m not your boy, Lannister. I\'m Lord of Winterfell while my father is away.   Tyrion Lannister:  Then you might learn a lord\'s courtesy.         Tyrion Lannister:  So it\'s true. Hello Bran. Do you remember anything about what happened?   Maester Luwin:  He ha

In [74]:
words4 = word_tokenize(string_script_text4)
words4

[u'Old',
 u'Nan',
 u':',
 u'The',
 u'little',
 u'Lord',
 u"'s",
 u'been',
 u'dreaming',
 u'again',
 u'.',
 u'Theon',
 u'Greyjoy',
 u':',
 u'We',
 u'have',
 u'visitors',
 u'.',
 u'Bran',
 u'Stark',
 u':',
 u'I',
 u'do',
 u"n't",
 u'want',
 u'to',
 u'see',
 u'anyone',
 u'.',
 u'Theon',
 u'Greyjoy',
 u':',
 u'Really',
 u'?',
 u'If',
 u'I',
 u'was',
 u'cooped',
 u'up',
 u'all',
 u'day',
 u'with',
 u'no',
 u'one',
 u'but',
 u'this',
 u'old',
 u'bat',
 u'for',
 u'company',
 u',',
 u'I',
 u"'d",
 u'go',
 u'mad',
 u'.',
 u'Anyway',
 u',',
 u'you',
 u'do',
 u"n't",
 u'have',
 u'a',
 u'choice',
 u'.',
 u'Robb',
 u"'s",
 u'waiting',
 u'.',
 u'Bran',
 u'Stark',
 u':',
 u'I',
 u'do',
 u"n't",
 u'want',
 u'to',
 u'go',
 u'.',
 u'Theon',
 u'Greyjoy',
 u':',
 u'Neither',
 u'do',
 u'I',
 u'.',
 u'But',
 u'Robb',
 u"'s",
 u'Lord',
 u'of',
 u'Winterfell',
 u',',
 u'which',
 u'means',
 u'I',
 u'do',
 u'what',
 u'he',
 u'says',
 u'and',
 u'you',
 u'do',
 u'what',
 u'I',
 u'say',
 u'.',
 u'Hodor',
 u'!',
 u

In [75]:
sentences4 = sent_tokenize(string_script_text4)
sentences4

[u"      Old Nan:  The little Lord's been dreaming again.",
 u'Theon Greyjoy:  We have visitors.',
 u"Bran Stark:  I don't want to see anyone.",
 u'Theon Greyjoy:  Really?',
 u"If I was cooped up all day with no one but this old bat for company, I'd go mad.",
 u"Anyway, you don't have a choice.",
 u"Robb's waiting.",
 u"Bran Stark:  I don't want to go.",
 u'Theon Greyjoy:  Neither do I.',
 u"But Robb's Lord of Winterfell, which means I do what he says and you do what I say.",
 u'Hodor!',
 u'Help Bran down the hall.',
 u'Tyrion Lannister:   I must say I received a slightly warmer welcome on my last visit.',
 u"Robb Stark:  Any man of the Night's Watch is welcome at Winterfell.",
 u"Tyrion Lannister:  Any man of the Night's Watch, but not I, eh, boy?",
 u"Robb Stark:  I'm not your boy, Lannister.",
 u"I'm Lord of Winterfell while my father is away.",
 u"Tyrion Lannister:  Then you might learn a lord's courtesy.",
 u"Tyrion Lannister:  So it's true.",
 u'Hello Bran.',
 u'Do you remember a

In [76]:
dialogue4 = []

for sentence in sentences4:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_04):
            dialogue4.append(sentence)

In [77]:
dialogue4

[u'Theon Greyjoy:  We have visitors.',
 u"Bran Stark:  I don't want to see anyone.",
 u'Theon Greyjoy:  Really?',
 u"Bran Stark:  I don't want to go.",
 u'Theon Greyjoy:  Neither do I.',
 u'Tyrion Lannister:   I must say I received a slightly warmer welcome on my last visit.',
 u"Robb Stark:  Any man of the Night's Watch is welcome at Winterfell.",
 u"Tyrion Lannister:  Any man of the Night's Watch, but not I, eh, boy?",
 u"Robb Stark:  I'm not your boy, Lannister.",
 u"Tyrion Lannister:  Then you might learn a lord's courtesy.",
 u"Tyrion Lannister:  So it's true.",
 u'Maester Luwin:  He has no memory of that day.',
 u'Tyrion Lannister:  Curious.',
 u'Robb Stark:   Why are you here?',
 u'Tyrion Lannister:  Would your charming companion be so kind as to kneel?',
 u'Tyrion Lannister:  Spare me your false courtesies, Lord Stark.',
 u"Theon Greyjoy:  Couldn't resist some northern ass?",
 u'Tyrion Lannister:  Come to see me off, Greyjoy?',
 u"Theon Greyjoy:  He's not my master.",
 u'Tyrion

In [78]:
from collections import defaultdict

speakers4 = defaultdict(list)
for sentence in dialogue4:
    speakers4[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers4

defaultdict(list,
            {u'Alliser Thorne': [u'  On your feet.',
              u"  Looks like the bastard's in love.",
              u"  We're done for today.",
              u'  What are you waiting for?',
              u'  You think this is funny, do you?',
              u'  Enjoying yourselves?',
              u'  A bit nippy, yeah, by the fire, indoors.',
              u"  That's admirable."],
             u'Arya Stark': [u'  Syrio says every hurt is a lesson and every lesson makes you better.',
              u"  Now that Bran's awake will he come live with us?",
              u' He wants to be a knight of the King\u2019s Guard.',
              u'  Can I be Lord of a holdfast?',
              u'  Why do they call you Littlefinger?'],
             u'Bran Stark': [u"  I don't want to see anyone.",
              u"  I don't want to go."],
             u'Bronn': [u'  You can have my room.'],
             u'Catelyn Stark': [u'  And to you.',
              u'  I was still Catelyn T

In [79]:
speakers4['Arya Stark']

[u'  Syrio says every hurt is a lesson and every lesson makes you better.',
 u"  Now that Bran's awake will he come live with us?",
 u' He wants to be a knight of the King\u2019s Guard.',
 u'  Can I be Lord of a holdfast?',
 u'  Why do they call you Littlefinger?']

In [80]:
episode_four = pd.DataFrame.from_dict(speakers4, orient="index")
print episode_four.shape

(36, 45)


In [81]:
#from numpy import nan
#episode_four.fillna(value=str(0), inplace=True)

In [82]:
episode_four.info()

<class 'pandas.core.frame.DataFrame'>
Index: 36 entries, Petyr Baelish to Jon Snow
Data columns (total 45 columns):
0     36 non-null object
1     30 non-null object
2     27 non-null object
3     21 non-null object
4     20 non-null object
5     17 non-null object
6     17 non-null object
7     16 non-null object
8     13 non-null object
9     12 non-null object
10    10 non-null object
11    10 non-null object
12    8 non-null object
13    8 non-null object
14    8 non-null object
15    7 non-null object
16    6 non-null object
17    5 non-null object
18    4 non-null object
19    3 non-null object
20    3 non-null object
21    3 non-null object
22    2 non-null object
23    2 non-null object
24    2 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
31    1 non-null object
32    1 non-null object
33    1 non-null object
34    1 non-null object
35    1 non-null object
36    1 

In [83]:
episode_four.head()

0   \
Petyr Baelish                                     I will?   
Yoren                                       Aye, my Lord.   
Cersei Baratheon          You're missing your tournament.   
Robert Baratheon    I'll bet you smell of blackberry jam!   
Rast                          You are in love, Lord Snow.   

                                                                 1   \
Petyr Baelish       And every inn in the city is full and the wh...   
Yoren                                                          None   
Cersei Baratheon    I thought we might put what happened on the ...   
Robert Baratheon                   I've been sitting here for days!   
Rast                                                           None   

                                          2   \
Petyr Baelish                He never stops.   
Yoren                                   None   
Cersei Baratheon    The only Stark who does.   
Robert Baratheon                   Yes, yes.   
Rast                                    None   

                                                   3   \
Petyr Baelish       I promised Cat that I'd help you.   
Yoren                                            None   
Cersei Baratheon         I might ask the same of you.   
Robert Baratheon                                 None   
Rast                                             None   

                                        4   \
Petyr Baelish       A singularly bad idea.   
Yoren                                 None   
Cersei Baratheon     You can't change him.   
Robert Baratheon                      None   
Rast                                  None   

                                                    5   \
Petyr Baelish                                      No.   
Yoren                                             None   
Cersei Baratheon    You're just a soldier, aren't you?   
Robert Baratheon                                  None   
Rast                                              None   

                                                   6   \
Petyr Baelish       The wiser answer was no, my Lord.   
Yoren                                            None   
Cersei Baratheon                            As was I.   
Robert Baratheon                                 None   
Rast                                             None   

                                                                 7   \
Petyr Baelish       I have my observers, as I said, and it's pos...   
Yoren                                                          None   
Cersei Baratheon                                               None   
Robert Baratheon                                               None   
Rast                                                           None   

                                           8                      9   \
Petyr Baelish       No, it's quite all right.    Ser Gregor Clegane.   
Yoren                                    None                   None   
Cersei Baratheon                         None                   None   
Robert Baratheon                         None                   None   
Rast                                     None                   None   

                                       10                              11  \
Petyr Baelish       Ser Hugh of the Vale.    Not what you were expecting?   
Yoren                                None                            None   
Cersei Baratheon                     None                            None   
Robert Baratheon                     None                            None   
Rast                                 None                            None   

                    12    13    14    15    16    17    18    19    20    21  \
Petyr Baelish     None  None  None  None  None  None  None  None  None  None   
Yoren             None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon  None  None  None  None  None  None  None  None  None  None   
Robert Baratheon 

In [84]:
test4 = episode_four[0].apply(remove_stops)
test4

Petyr Baelish                                                          
Yoren                                                          aye lord
Cersei Baratheon                               youre missing tournament
Robert Baratheon                           ill bet smell blackberry jam
Rast                                                     love lord snow
Janos Slynt           call lord stark ser city packed people floodin...
Tyrion Lannister      must say received slightly warmer welcome last...
Samwell Tarly                                                      hurt
Pyp                                                         well fought
Theon Greyjoy                                                  visitors
Eddard Stark                                           kings tournament
Bran Stark                                         dont want see anyone
Irri                                                       yes khaleesi
Arya Stark            syrio says every hurt lesson every lesson 

In [85]:
for column in episode_four.columns:
    for x in range(len(episode_four[column])):
        episode_four[column][x] = remove_stops(episode_four[column][x])

In [86]:
episode_four.head()

0   \
Petyr Baelish                                    
Yoren                                 aye lord   
Cersei Baratheon      youre missing tournament   
Robert Baratheon  ill bet smell blackberry jam   
Rast                            love lord snow   

                                                                 1   \
Petyr Baelish          every inn city full whores walking bowlegged   
Yoren                                                          None   
Cersei Baratheon  thought might put happened kingsroad behind us...   
Robert Baratheon                                   ive sitting days   
Rast                                                           None   

                           2                     3                    4   \
Petyr Baelish     never stops  promised cat id help  singularly bad idea   
Yoren                    None                  None                 None   
Cersei Baratheon        stark             might ask          cant change   
Robert Baratheon      yes yes                  None                 None   
Rast                     None                  None                 None   

                                   5                  6   \
Petyr Baelish                          wiser answer lord   
Yoren                            None               None   
Cersei Baratheon  youre soldier arent                      
Robert Baratheon                 None               None   
Rast                             None               None   

                                                                 7   \
Petyr Baelish     observers said possible saw lord arryn visit a...   
Yoren                                                          None   
Cersei Baratheon                                               None   
Robert Baratheon                                               None   
Rast                                                           None   

                           8                   9              10         11  \
Petyr Baelish     quite right  ser gregor clegane  ser hugh vale  expecting   
Yoren                    None                None           None       None   
Cersei Baratheon         None                None           None       None   
Robert Baratheon         None                None           None       None   
Rast                     None                None           None       None   

                    12    13    14    15    16    17    18    19    20    21  \
Petyr Baelish     None  None  None  None  None  None  None  None  None  None   
Yoren             None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon  None  None  None  None  None  None  None  None  None  None   
Robert Baratheon  None  None  None  None  None  None  None  None  None  None   
Rast              None  None  None  None  None  None  None  None  None  None   

                    22    23    24    25    26    27    28    29    30    31  \
Petyr Baelish     None  None  None  None  None  None  None  None  None  None   
Yoren             None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon  None  None  None  None  None  None  None  None  None  None   
Robert Baratheon  None  None  None  None  None  None  None  None  None  None   
Rast              None  None  None  None  None  None  None  None  None  None   

                    32    33    34    35    36    37    38    39    40    41  \
Petyr Baelish     None  None  None  None  None  None  None  None  None  None   
Yoren             None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon  None  None  None  None  None  None  None  None  None  None   
Robert Baratheon  None  None  None  None  None  None  None  None  None  None   
Rast              None  None  None  None  None  None  None  None  None  None   

                    42    43    44  
Petyr Baelish     None  None  None  
Yoren             None  None  None  
Cersei Baratheon  None  None  None  
Rober

### Episode Five

In [87]:
df_s1.script_text[4]

[u'\n',
 u'Eddard Stark:',
 u" He'd never worn this armor before.",
 u'\n',
 u'Barristan Selmy:',
 u' Bad luck for him... Going against the Mountain.',
 u'\n',
 u'Eddard Stark:',
 u' Who determines the draw?',
 u'\n',
 u' ',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Eddard Stark:',
 u' And that lad... He was a squire until a few months ago. How could he afford a new suit of armor?',
 u'\n',
 u'Barristan Selmy:',
 u' Perhaps Lord Arryn left him some money? I hear the King wants to joust today.',
 u'\n',
 u'Eddard Stark:',
 u' Yes. That will never happen.',
 u'\n',
 u'Barristan Selmy:',
 u' Robert tends to do what he wants.',
 u'\n',
 u'Eddard Stark:',
 u" If the King got what he wanted all the time, we'd still be fighting a damned rebellion.",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Robert Baratheon:',
 u' Fat? Fat, is it? Is that how you speak to your King? That was funny, is it?',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Robert Baratheon:',
 u' Oh, it\u2019s funny, is it?',
 u'\

In [88]:
script_text1_05 = df_s1.script_text[4]
print type(script_text1_05)

script_text1_05

<type 'list'>


[u'\n',
 u'Eddard Stark:',
 u" He'd never worn this armor before.",
 u'\n',
 u'Barristan Selmy:',
 u' Bad luck for him... Going against the Mountain.',
 u'\n',
 u'Eddard Stark:',
 u' Who determines the draw?',
 u'\n',
 u' ',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Eddard Stark:',
 u' And that lad... He was a squire until a few months ago. How could he afford a new suit of armor?',
 u'\n',
 u'Barristan Selmy:',
 u' Perhaps Lord Arryn left him some money? I hear the King wants to joust today.',
 u'\n',
 u'Eddard Stark:',
 u' Yes. That will never happen.',
 u'\n',
 u'Barristan Selmy:',
 u' Robert tends to do what he wants.',
 u'\n',
 u'Eddard Stark:',
 u" If the King got what he wanted all the time, we'd still be fighting a damned rebellion.",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Robert Baratheon:',
 u' Fat? Fat, is it? Is that how you speak to your King? That was funny, is it?',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Robert Baratheon:',
 u' Oh, it\u2019s funny, is it?',
 u'\

In [89]:
script_split5 = [i.split('\n') for i in script_text1_05]
script_split5

[[u'', u''],
 [u'Eddard Stark:'],
 [u" He'd never worn this armor before."],
 [u'', u''],
 [u'Barristan Selmy:'],
 [u' Bad luck for him... Going against the Mountain.'],
 [u'', u''],
 [u'Eddard Stark:'],
 [u' Who determines the draw?'],
 [u'', u''],
 [u' '],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Eddard Stark:'],
 [u' And that lad... He was a squire until a few months ago. How could he afford a new suit of armor?'],
 [u'', u''],
 [u'Barristan Selmy:'],
 [u' Perhaps Lord Arryn left him some money? I hear the King wants to joust today.'],
 [u'', u''],
 [u'Eddard Stark:'],
 [u' Yes. That will never happen.'],
 [u'', u''],
 [u'Barristan Selmy:'],
 [u' Robert tends to do what he wants.'],
 [u'', u''],
 [u'Eddard Stark:'],
 [u" If the King got what he wanted all the time, we'd still be fighting a damned rebellion."],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Robert Baratheon:'],
 [u' Fat? Fat, is it? Is that how you speak 

In [90]:
string_script_text5 = ' '

for i in script_split5:
    for e in i:
        string_script_text5 = string_script_text5 + ' ' + e

In [91]:
string_script_text5

u'    Eddard Stark:  He\'d never worn this armor before.   Barristan Selmy:  Bad luck for him... Going against the Mountain.   Eddard Stark:  Who determines the draw?                 Eddard Stark:  And that lad... He was a squire until a few months ago. How could he afford a new suit of armor?   Barristan Selmy:  Perhaps Lord Arryn left him some money? I hear the King wants to joust today.   Eddard Stark:  Yes. That will never happen.   Barristan Selmy:  Robert tends to do what he wants.   Eddard Stark:  If the King got what he wanted all the time, we\'d still be fighting a damned rebellion.           Robert Baratheon:  Fat? Fat, is it? Is that how you speak to your King? That was funny, is it?         Robert Baratheon:  Oh, it\u2019s funny, is it?   Lancel Lannister:  No, Your Grace.   Robert Baratheon:  No? You don\'t like the Hand\'s joke?   Eddard Stark:  You\'re torturing the poor boy.   Robert Baratheon:  You heard the Hand. The King\'s too fat for his armor! Go find the breastpl

In [92]:
words5 = word_tokenize(string_script_text5)
words5

[u'Eddard',
 u'Stark',
 u':',
 u'He',
 u"'d",
 u'never',
 u'worn',
 u'this',
 u'armor',
 u'before',
 u'.',
 u'Barristan',
 u'Selmy',
 u':',
 u'Bad',
 u'luck',
 u'for',
 u'him',
 u'...',
 u'Going',
 u'against',
 u'the',
 u'Mountain',
 u'.',
 u'Eddard',
 u'Stark',
 u':',
 u'Who',
 u'determines',
 u'the',
 u'draw',
 u'?',
 u'Eddard',
 u'Stark',
 u':',
 u'And',
 u'that',
 u'lad',
 u'...',
 u'He',
 u'was',
 u'a',
 u'squire',
 u'until',
 u'a',
 u'few',
 u'months',
 u'ago',
 u'.',
 u'How',
 u'could',
 u'he',
 u'afford',
 u'a',
 u'new',
 u'suit',
 u'of',
 u'armor',
 u'?',
 u'Barristan',
 u'Selmy',
 u':',
 u'Perhaps',
 u'Lord',
 u'Arryn',
 u'left',
 u'him',
 u'some',
 u'money',
 u'?',
 u'I',
 u'hear',
 u'the',
 u'King',
 u'wants',
 u'to',
 u'joust',
 u'today',
 u'.',
 u'Eddard',
 u'Stark',
 u':',
 u'Yes',
 u'.',
 u'That',
 u'will',
 u'never',
 u'happen',
 u'.',
 u'Barristan',
 u'Selmy',
 u':',
 u'Robert',
 u'tends',
 u'to',
 u'do',
 u'what',
 u'he',
 u'wants',
 u'.',
 u'Eddard',
 u'Stark',
 u':

In [93]:
sentences5 = sent_tokenize(string_script_text5)
sentences5

[u"    Eddard Stark:  He'd never worn this armor before.",
 u'Barristan Selmy:  Bad luck for him...',
 u'Going against the Mountain.',
 u'Eddard Stark:  Who determines the draw?',
 u'Eddard Stark:  And that lad...',
 u'He was a squire until a few months ago.',
 u'How could he afford a new suit of armor?',
 u'Barristan Selmy:  Perhaps Lord Arryn left him some money?',
 u'I hear the King wants to joust today.',
 u'Eddard Stark:  Yes.',
 u'That will never happen.',
 u'Barristan Selmy:  Robert tends to do what he wants.',
 u"Eddard Stark:  If the King got what he wanted all the time, we'd still be fighting a damned rebellion.",
 u'Robert Baratheon:  Fat?',
 u'Fat, is it?',
 u'Is that how you speak to your King?',
 u'That was funny, is it?',
 u'Robert Baratheon:  Oh, it\u2019s funny, is it?',
 u'Lancel Lannister:  No, Your Grace.',
 u'Robert Baratheon:  No?',
 u"You don't like the Hand's joke?",
 u"Eddard Stark:  You're torturing the poor boy.",
 u'Robert Baratheon:  You heard the Hand.',
 

In [94]:
dialogue5 = []

for sentence in sentences5:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_05):
            dialogue5.append(sentence)

In [95]:
dialogue5

[u'Barristan Selmy:  Bad luck for him...',
 u'Eddard Stark:  Who determines the draw?',
 u'Eddard Stark:  And that lad...',
 u'Barristan Selmy:  Perhaps Lord Arryn left him some money?',
 u'Eddard Stark:  Yes.',
 u'Barristan Selmy:  Robert tends to do what he wants.',
 u"Eddard Stark:  If the King got what he wanted all the time, we'd still be fighting a damned rebellion.",
 u'Robert Baratheon:  Fat?',
 u'Robert Baratheon:  Oh, it\u2019s funny, is it?',
 u'Lancel Lannister:  No, Your Grace.',
 u'Robert Baratheon:  No?',
 u"Eddard Stark:  You're torturing the poor boy.",
 u'Robert Baratheon:  You heard the Hand.',
 u'Eddard Stark:  The breastplate stretcher?',
 u'Robert Baratheon:  How long before he figures it out?',
 u'Eddard Stark:  Maybe you should have one invented.',
 u'Robert Baratheon:  All right, all right.',
 u'Eddard Stark:  You have no business jousting.',
 u'Robert Baratheon:  Why?',
 u"Eddard Stark:  And who's going to hit you back?",
 u'Robert Baratheon:  Anybody who can.

In [96]:
from collections import defaultdict

speakers5 = defaultdict(list)
for sentence in dialogue5:
    speakers5[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers5

defaultdict(list,
            {u'Arya Stark': [u"  I'm not a beggar.",
              u'  I want to see my father.',
              u'  My father is Hand of the King!',
              u'  They said they were going to kill you.',
              u"  I didn't see them, but I think one was fat.",
              u"  I'm not lying!",
              u"  I'm a girl!",
              u'  How many guards does my father have?',
              u"  You wouldn't let anyone kill him, would you?"],
             u'Barristan Selmy': [u'  Bad luck for him...',
              u'  Perhaps Lord Arryn left him some money?',
              u'  Robert tends to do what he wants.'],
             u'Bran Stark': [u'  Words - "Ours is the fury".',
              u'  The Westerlands - sigil - a lion.',
              u'  Lords - the Lannisters.',
              u'  "Unbowed, unbent, unbroken".',
              u'  "Righteous in wrath".',
              u'  "Family, duty, honor".',
              u'  "Family, duty, honor"... Is that

In [97]:
speakers5['Arya Stark']

[u"  I'm not a beggar.",
 u'  I want to see my father.',
 u'  My father is Hand of the King!',
 u'  They said they were going to kill you.',
 u"  I didn't see them, but I think one was fat.",
 u"  I'm not lying!",
 u"  I'm a girl!",
 u'  How many guards does my father have?',
 u"  You wouldn't let anyone kill him, would you?"]

In [98]:
episode_five = pd.DataFrame.from_dict(speakers5, orient="index")
print episode_five.shape

(32, 61)


In [99]:
#from numpy import nan
#episode_five.fillna(value=str(0), inplace=True)

In [100]:
episode_five.info()

<class 'pandas.core.frame.DataFrame'>
Index: 32 entries, Petyr Baelish to Jory Cassel
Data columns (total 61 columns):
0     32 non-null object
1     28 non-null object
2     25 non-null object
3     20 non-null object
4     18 non-null object
5     16 non-null object
6     16 non-null object
7     15 non-null object
8     15 non-null object
9     13 non-null object
10    12 non-null object
11    11 non-null object
12    10 non-null object
13    8 non-null object
14    8 non-null object
15    7 non-null object
16    6 non-null object
17    6 non-null object
18    6 non-null object
19    6 non-null object
20    6 non-null object
21    5 non-null object
22    5 non-null object
23    5 non-null object
24    5 non-null object
25    4 non-null object
26    4 non-null object
27    4 non-null object
28    4 non-null object
29    4 non-null object
30    3 non-null object
31    2 non-null object
32    2 non-null object
33    2 non-null object
34    2 non-null object
35    2 non-null object
36  

In [101]:
episode_five.head()

0   \
Petyr Baelish                     100 gold dragons on the Mountain.   
Cersei Baratheon    Without a Hand, everything will fall to pieces.   
Robert Baratheon                                               Fat?   
Illyrio Mopatis       And when he knows the truth, what will he do?   
Robin Arryn                                                  Mommy?   

                                                            1   \
Petyr Baelish       Now what will I buy with 100 gold dragons?   
Cersei Baratheon                                           No.   
Robert Baratheon                        Oh, it’s funny, is it?   
Illyrio Mopatis                          What good is war now?   
Robin Arryn                                       He's little.   

                                                  2   \
Petyr Baelish       Loras knew his mare was in heat.   
Cersei Baratheon            The Dothraki don't sail.   
Robert Baratheon                                 No?   
Illyrio Mopatis                        We need time.   
Robin Arryn                       You can't hurt us!   

                                                   3   \
Petyr Baelish       No honor but quite a bit of gold.   
Cersei Baratheon                  Is my father wrong?   
Robert Baratheon                  You heard the Hand.   
Illyrio Mopatis                         It never was.   
Robin Arryn                                      None   

                                                    4   \
Petyr Baelish                     You do move quietly.   
Cersei Baratheon              We still outnumber them.   
Robert Baratheon    How long before he figures it out?   
Illyrio Mopatis                                   None   
Robin Arryn                                       None   

                                              5                    6   \
Petyr Baelish       You look a bit lonely today.                Am I?   
Cersei Baratheon                           Five.    What do you want?   
Robert Baratheon           All right, all right.                 Why?   
Illyrio Mopatis                             None                 None   
Robin Arryn                                 None                 None   

                                                                 7   \
Petyr Baelish       I'm a purveyor of beauty and discretion, bot...   
Cersei Baratheon                                      Our marriage.   
Robert Baratheon                                   Anybody who can.   
Illyrio Mopatis                                                None   
Robin Arryn                                                    None   

                                                                 8   \
Petyr Baelish       All desires are valid to a man with a full p...   
Cersei Baratheon                                         Every day.   
Robert Baratheon    Are you telling me those cowards would let m...   
Illyrio Mopatis                                                None   
Robin Arryn                                                    None   

                                                                 9   \
Petyr Baelish       Strictly speaking, such a thing would not be...   
Cersei Baratheon        Well, seventeen years is quite a long time.   
Robert Baratheon                           Hmm... A bloody idiot...   
Illyrio Mopatis                                                None   
Robin Arryn                                                    None   

                              10  \
Petyr Baelish           Tell me.   
Cersei Baratheon    Yes, it tis.   
Robert Baratheon           What?   
Illyrio Mopatis             None   
Robin Arryn                 None   

                                                                 11  \
Petyr Baelish        Since you last saw me or since I last saw you?   
Cersei Baratheon    At first, just saying her name, even in priv...   
Robert Baratheon        Stop this madness in the name of your 

In [102]:
test5 = episode_five[0].apply(remove_stops)
test5

Petyr Baelish                                   gold dragons mountain
Cersei Baratheon                  without hand everything fall pieces
Robert Baratheon                                                  fat
Illyrio Mopatis                                           knows truth
Robin Arryn                                                     mommy
Yoren                                                    yoren please
Mord                                               go sleep dwarf man
Tyrion Lannister                                                 wise
Theon Greyjoy                                  important enough likes
Vardis Egen                               ser vardis egen knight vale
Mhaegen                                                 tell see lord
Eddard Stark                                          determines draw
Bran Stark                                                 words fury
Lysa Arryn                                                           
Arya Stark          

In [103]:
for column in episode_five.columns:
    for x in range(len(episode_five[column])):
        episode_five[column][x] = remove_stops(episode_five[column][x])

In [104]:
episode_five.head()

0                 1   \
Petyr Baelish                   gold dragons mountain  buy gold dragons   
Cersei Baratheon  without hand everything fall pieces                     
Robert Baratheon                                  fat          oh funny   
Illyrio Mopatis                           knows truth          good war   
Robin Arryn                                     mommy        hes little   

                                    2                     3                4   \
Petyr Baelish     loras knew mare heat  honor quite bit gold     move quietly   
Cersei Baratheon    dothraki dont sail          father wrong  still outnumber   
Robert Baratheon                                  heard hand     long figures   
Illyrio Mopatis              need time                 never             None   
Robin Arryn               cant hurt us                  None             None   

                                     5     6   \
Petyr Baelish     look bit lonely today         
Cersei Baratheon                   five  want   
Robert Baratheon            right right         
Illyrio Mopatis                    None  None   
Robin Arryn                        None  None   

                                                               7   \
Petyr Baelish     im purveyor beauty discretion equally important   
Cersei Baratheon                                         marriage   
Robert Baratheon                                          anybody   
Illyrio Mopatis                                              None   
Robin Arryn                                                  None   

                                             8   \
Petyr Baelish      desires valid man full purse   
Cersei Baratheon                      every day   
Robert Baratheon  telling cowards would let win   
Illyrio Mopatis                            None   
Robin Arryn                                None   

                                                                 9        10  \
Petyr Baelish     strictly speaking thing would accordance kings...     tell   
Cersei Baratheon               well seventeen years quite long time  yes tis   
Robert Baratheon                                   hmm bloody idiot            
Illyrio Mopatis                                                None     None   
Robin Arryn                                                    None     None   

                                                                 11  \
Petyr Baelish                         since last saw since last saw   
Cersei Baratheon  first saying name even private felt like breat...   
Robert Baratheon                             stop madness name king   
Illyrio Mopatis                                                None   
Robin Arryn                                                    None   

                                                                 12  \
Petyr Baelish                                              saw eyes   
Cersei Baratheon  harm could lyanna starks ghost either us haven...   
Robert Baratheon                                     whore pregnant   
Illyrio Mopatis                                                None   
Robin Arryn                                                    None   

                                   13                                  14  \
Petyr Baelish        council business                      know something   
Cersei Baratheon  felt something know  even lost first boy quite actually   
Robert Baratheon  warned would happen                               honor   
Illyrio Mopatis                  None                                None   
Robin Arryn                      None                                None   

                                         15  \
Petyr Baelish                           yes   
Cersei Baratheon  doesnt make feel anything   
Robert Baratheon                careful ned   
Illyrio Mopatis                        None   
Robin Arryn                            None   

               

### Episode Six

In [105]:
df_s1.script_text[5]

[u'\n',
 u'\n',
 u'Eddard Stark:',
 u'  Your pardon, your Grace.',
 u'\n',
 u'Cersei Baratheon:',
 u' Do you know what your wife has done?',
 u'\n',
 u'Eddard Stark:',
 u'  She did nothing I did not command.',
 u'\n',
 u'Robert Baratheon:',
 u' Who\u2019d have thought she had it in her?',
 u'\n',
 u'Cersei Baratheon:',
 u' By what right dare you lay hands on my blood?',
 u'\n',
 u'Eddard Stark:',
 u'  I am the King\u2019s Hand -',
 u'\n',
 u'Cersei Baratheon:',
 u' You were the King\u2019s Hand!',
 u'\n',
 u'Eddard Stark:',
 u'  - trying to keep the peace -',
 u'\n',
 u'Cersei Baratheon:',
 u' You shall now be held accountable.',
 u'\n',
 u'Robert Baratheon:',
 u' Oh, will both of you shut your mouths? Catelyn will release Tyrion and you\u2019ll make your peace with Jaime.',
 u'\n',
 u'Eddard Stark:',
 u' He butchered my men.',
 u'\n',
 u'Cersei Baratheon:',
 u' Lord Stark was returning drunk from a brothel when his men attacked Jaime.',
 u'\n',
 u'Robert Baratheon:',
 u' Quiet, woman.

In [106]:
script_text1_06 = df_s1.script_text[5]
print type(script_text1_06)

script_text1_06

<type 'list'>


[u'\n',
 u'\n',
 u'Eddard Stark:',
 u'  Your pardon, your Grace.',
 u'\n',
 u'Cersei Baratheon:',
 u' Do you know what your wife has done?',
 u'\n',
 u'Eddard Stark:',
 u'  She did nothing I did not command.',
 u'\n',
 u'Robert Baratheon:',
 u' Who\u2019d have thought she had it in her?',
 u'\n',
 u'Cersei Baratheon:',
 u' By what right dare you lay hands on my blood?',
 u'\n',
 u'Eddard Stark:',
 u'  I am the King\u2019s Hand -',
 u'\n',
 u'Cersei Baratheon:',
 u' You were the King\u2019s Hand!',
 u'\n',
 u'Eddard Stark:',
 u'  - trying to keep the peace -',
 u'\n',
 u'Cersei Baratheon:',
 u' You shall now be held accountable.',
 u'\n',
 u'Robert Baratheon:',
 u' Oh, will both of you shut your mouths? Catelyn will release Tyrion and you\u2019ll make your peace with Jaime.',
 u'\n',
 u'Eddard Stark:',
 u' He butchered my men.',
 u'\n',
 u'Cersei Baratheon:',
 u' Lord Stark was returning drunk from a brothel when his men attacked Jaime.',
 u'\n',
 u'Robert Baratheon:',
 u' Quiet, woman.

In [107]:
script_split6 = [i.split('\n') for i in script_text1_06]
script_split6

[[u'', u''],
 [u'', u''],
 [u'Eddard Stark:'],
 [u'  Your pardon, your Grace.'],
 [u'', u''],
 [u'Cersei Baratheon:'],
 [u' Do you know what your wife has done?'],
 [u'', u''],
 [u'Eddard Stark:'],
 [u'  She did nothing I did not command.'],
 [u'', u''],
 [u'Robert Baratheon:'],
 [u' Who\u2019d have thought she had it in her?'],
 [u'', u''],
 [u'Cersei Baratheon:'],
 [u' By what right dare you lay hands on my blood?'],
 [u'', u''],
 [u'Eddard Stark:'],
 [u'  I am the King\u2019s Hand -'],
 [u'', u''],
 [u'Cersei Baratheon:'],
 [u' You were the King\u2019s Hand!'],
 [u'', u''],
 [u'Eddard Stark:'],
 [u'  - trying to keep the peace -'],
 [u'', u''],
 [u'Cersei Baratheon:'],
 [u' You shall now be held accountable.'],
 [u'', u''],
 [u'Robert Baratheon:'],
 [u' Oh, will both of you shut your mouths? Catelyn will release Tyrion and you\u2019ll make your peace with Jaime.'],
 [u'', u''],
 [u'Eddard Stark:'],
 [u' He butchered my men.'],
 [u'', u''],
 [u'Cersei Baratheon:'],
 [u' Lord Stark wa

In [108]:
string_script_text6 = ' '

for i in script_split6:
    for e in i:
        string_script_text6 = string_script_text6 + ' ' + e

In [109]:
string_script_text6

u'      Eddard Stark:   Your pardon, your Grace.   Cersei Baratheon:  Do you know what your wife has done?   Eddard Stark:   She did nothing I did not command.   Robert Baratheon:  Who\u2019d have thought she had it in her?   Cersei Baratheon:  By what right dare you lay hands on my blood?   Eddard Stark:   I am the King\u2019s Hand -   Cersei Baratheon:  You were the King\u2019s Hand!   Eddard Stark:   - trying to keep the peace -   Cersei Baratheon:  You shall now be held accountable.   Robert Baratheon:  Oh, will both of you shut your mouths? Catelyn will release Tyrion and you\u2019ll make your peace with Jaime.   Eddard Stark:  He butchered my men.   Cersei Baratheon:  Lord Stark was returning drunk from a brothel when his men attacked Jaime.   Robert Baratheon:  Quiet, woman.   Eddard Stark:   Jaime has fled the city. Give me leave to bring him back to justice.   Cersei Baratheon:  I took you for a king.   Robert Baratheon:  Hold your tongue.   Cersei Baratheon:  He\u2019s attack

In [110]:
words6 = word_tokenize(string_script_text6)
words6

[u'Eddard',
 u'Stark',
 u':',
 u'Your',
 u'pardon',
 u',',
 u'your',
 u'Grace',
 u'.',
 u'Cersei',
 u'Baratheon',
 u':',
 u'Do',
 u'you',
 u'know',
 u'what',
 u'your',
 u'wife',
 u'has',
 u'done',
 u'?',
 u'Eddard',
 u'Stark',
 u':',
 u'She',
 u'did',
 u'nothing',
 u'I',
 u'did',
 u'not',
 u'command',
 u'.',
 u'Robert',
 u'Baratheon',
 u':',
 u'Who\u2019d',
 u'have',
 u'thought',
 u'she',
 u'had',
 u'it',
 u'in',
 u'her',
 u'?',
 u'Cersei',
 u'Baratheon',
 u':',
 u'By',
 u'what',
 u'right',
 u'dare',
 u'you',
 u'lay',
 u'hands',
 u'on',
 u'my',
 u'blood',
 u'?',
 u'Eddard',
 u'Stark',
 u':',
 u'I',
 u'am',
 u'the',
 u'King\u2019s',
 u'Hand',
 u'-',
 u'Cersei',
 u'Baratheon',
 u':',
 u'You',
 u'were',
 u'the',
 u'King\u2019s',
 u'Hand',
 u'!',
 u'Eddard',
 u'Stark',
 u':',
 u'-',
 u'trying',
 u'to',
 u'keep',
 u'the',
 u'peace',
 u'-',
 u'Cersei',
 u'Baratheon',
 u':',
 u'You',
 u'shall',
 u'now',
 u'be',
 u'held',
 u'accountable',
 u'.',
 u'Robert',
 u'Baratheon',
 u':',
 u'Oh',
 u',',

In [111]:
sentences6 = sent_tokenize(string_script_text6)
sentences6

[u'      Eddard Stark:   Your pardon, your Grace.',
 u'Cersei Baratheon:  Do you know what your wife has done?',
 u'Eddard Stark:   She did nothing I did not command.',
 u'Robert Baratheon:  Who\u2019d have thought she had it in her?',
 u'Cersei Baratheon:  By what right dare you lay hands on my blood?',
 u'Eddard Stark:   I am the King\u2019s Hand -   Cersei Baratheon:  You were the King\u2019s Hand!',
 u'Eddard Stark:   - trying to keep the peace -   Cersei Baratheon:  You shall now be held accountable.',
 u'Robert Baratheon:  Oh, will both of you shut your mouths?',
 u'Catelyn will release Tyrion and you\u2019ll make your peace with Jaime.',
 u'Eddard Stark:  He butchered my men.',
 u'Cersei Baratheon:  Lord Stark was returning drunk from a brothel when his men attacked Jaime.',
 u'Robert Baratheon:  Quiet, woman.',
 u'Eddard Stark:   Jaime has fled the city.',
 u'Give me leave to bring him back to justice.',
 u'Cersei Baratheon:  I took you for a king.',
 u'Robert Baratheon:  Hold 

In [112]:
dialogue6 = []

for sentence in sentences6:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_06):
            dialogue6.append(sentence)

In [113]:
dialogue6

[u'Cersei Baratheon:  Do you know what your wife has done?',
 u'Eddard Stark:   She did nothing I did not command.',
 u'Robert Baratheon:  Who\u2019d have thought she had it in her?',
 u'Cersei Baratheon:  By what right dare you lay hands on my blood?',
 u'Eddard Stark:   I am the King\u2019s Hand -   Cersei Baratheon:  You were the King\u2019s Hand!',
 u'Eddard Stark:   - trying to keep the peace -   Cersei Baratheon:  You shall now be held accountable.',
 u'Robert Baratheon:  Oh, will both of you shut your mouths?',
 u'Eddard Stark:  He butchered my men.',
 u'Cersei Baratheon:  Lord Stark was returning drunk from a brothel when his men attacked Jaime.',
 u'Robert Baratheon:  Quiet, woman.',
 u'Eddard Stark:   Jaime has fled the city.',
 u'Cersei Baratheon:  I took you for a king.',
 u'Robert Baratheon:  Hold your tongue.',
 u'Cersei Baratheon:  He\u2019s attacked my brother and abducted the other.',
 u'Cersei Baratheon:  I shall wear this like a badge of honor.',
 u'Robert Baratheon:

In [114]:
from collections import defaultdict

speakers6 = defaultdict(list)
for sentence in dialogue6:
    speakers6[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers6

defaultdict(list,
            {u'Arya Stark': [u'  They killed Jory.',
              u'   Yes -   Syrio Forel',
              u'  I don\u2019t like dolls and k -   Syrio Forel',
              u'   Are you dying because of your leg?',
              u'   You can\u2019t.',
              u'   Can\u2019t we take Syrio back with us?',
              u'  Seven hells.',
              u'  The lion\u2019s not his sigil, idiot.',
              u'   Come on!'],
             u'Barristan Selmy': [u'  I don\u2019t believe so, your Grace.'],
             u'Beric Dondarrion': [u'  As you command.'],
             u'Bran Stark': [u'  Come on, Dancer.',
              u'  Robb?',
              u'  I\u2019m not alone, my brother is with me.',
              u'  I can\u2019t.',
              u'  I\u2019m Brandon Stark of Winterfell and if you don\u2019t let me be, I\u2019ll have you all killed!',
              u'  Robb!',
              u'  No, don\u2019t.',
              u'  Yes, it doesn\u2019t hurt.'],
     

In [115]:
speakers6['Arya Stark']

[u'  They killed Jory.',
 u'   Yes -   Syrio Forel',
 u'  I don\u2019t like dolls and k -   Syrio Forel',
 u'   Are you dying because of your leg?',
 u'   You can\u2019t.',
 u'   Can\u2019t we take Syrio back with us?',
 u'  Seven hells.',
 u'  The lion\u2019s not his sigil, idiot.',
 u'   Come on!']

In [116]:
episode_six = pd.DataFrame.from_dict(speakers6, orient="index")
print episode_six.shape

(36, 22)


In [117]:
#from numpy import nan
#episode_six.fillna(value=str(0), inplace=True)

In [118]:
episode_six.info()

<class 'pandas.core.frame.DataFrame'>
Index: 36 entries, Joffrey Baratheon to Syrio Forel
Data columns (total 22 columns):
0     36 non-null object
1     26 non-null object
2     24 non-null object
3     22 non-null object
4     18 non-null object
5     17 non-null object
6     14 non-null object
7     12 non-null object
8     10 non-null object
9     9 non-null object
10    9 non-null object
11    8 non-null object
12    7 non-null object
13    5 non-null object
14    4 non-null object
15    4 non-null object
16    4 non-null object
17    3 non-null object
18    3 non-null object
19    3 non-null object
20    3 non-null object
21    2 non-null object
dtypes: object(22)
memory usage: 6.5+ KB


In [119]:
episode_six.head()

0   \
Joffrey Baratheon                                           My lady.   
Petyr Baelish                                                  Fish.   
Cersei Baratheon                Do you know what your wife has done?   
Robert Baratheon               Who’d have thought she had it in her?   
Khal Drogo           (speaks Dothraki, motions to the other side ...   

                                                                  1   \
Joffrey Baratheon     You’ll be queen one day, it’s only fitting ...   
Petyr Baelish            (whisper) That sounds like someone we know.   
Cersei Baratheon       By what right dare you lay hands on my blood?   
Robert Baratheon              Oh, will both of you shut your mouths?   
Khal Drogo                                          You are no king.   

                                                                  2   \
Joffrey Baratheon                                    You’re my lady.   
Petyr Baelish        I’ve heard him called “Tywin Lannister’s mad...   
Cersei Baratheon     Lord Stark was returning drunk from a brothe...   
Robert Baratheon                                       Quiet, woman.   
Khal Drogo                     (speaks Dothraki)   Viserys Targaryen   

                                                       3   \
Joffrey Baratheon                                    None   
Petyr Baelish        A bold move, my Lord, and admirable.   
Cersei Baratheon                   I took you for a king.   
Robert Baratheon                        Hold your tongue.   
Khal Drogo                            A crown for a king.   

                                                                  4   \
Joffrey Baratheon                                               None   
Petyr Baelish                                                   None   
Cersei Baratheon     He’s attacked my brother and abducted the ot...   
Robert Baratheon         Wear it in silence or I’ll honor you again.   
Khal Drogo                                                      None   

                                                           5   \
Joffrey Baratheon                                        None   
Petyr Baelish                                            None   
Cersei Baratheon     I shall wear this like a badge of honor.   
Robert Baratheon                     See what she does to me?   
Khal Drogo                                               None   

                                                                  6   \
Joffrey Baratheon                                               None   
Petyr Baelish                                                   None   
Cersei Baratheon                                                None   
Robert Baratheon     So tell your wife to return that little shit...   
Khal Drogo                                                      None   

                                                                  7   \
Joffrey Baratheon                                               None   
Petyr Baelish                                                   None   
Cersei Baratheon                                                None   
Robert Baratheon     I’m half a kingdom in debt to his bloody fat...   
Khal Drogo                                                      None   

                                8                                 9   \
Joffrey Baratheon             None                              None   
Petyr Baelish                 None                              None   
Cersei Baratheon              None                              None   
Robert Baratheon     Piss on that!    Killing things clears my head.   
Khal Drogo                    None                              None   

                                         10         11  \
Joffrey Baratheon                      None       None   
Petyr Baelish                          None       None   
Cersei Baratheon                       None       None   
Robert Baratheon     Oh, what was I saying?  

In [120]:
test6 = episode_six[0].apply(remove_stops)
test6

Joffrey Baratheon                                                  lady
Petyr Baelish                                                      fish
Cersei Baratheon                                         know wife done
Robert Baratheon                                           whod thought
Khal Drogo               speaks dothraki motions side hut jorah mormont
Robin Arryn                                               happened next
Sansa Stark                                               well shouldnt
Eddard Stark                                            nothing command
Mord                                             dwarf man making noise
Tyrion Lannister                                        would like rich
Wildling                                                       dont see
Theon Greyjoy                                               blood blood
Ser Vardis                                                   heart lady
Osha                                              alone deep dar

In [121]:
for column in episode_six.columns:
    for x in range(len(episode_six[column])):
        episode_six[column][x] = remove_stops(episode_six[column][x])

In [122]:
episode_six.head()

0   \
Joffrey Baratheon                                            lady   
Petyr Baelish                                                fish   
Cersei Baratheon                                   know wife done   
Robert Baratheon                                     whod thought   
Khal Drogo         speaks dothraki motions side hut jorah mormont   

                                                      1   \
Joffrey Baratheon  youll queen one day fitting look part   
Petyr Baelish           whisper sounds like someone know   
Cersei Baratheon              right dare lay hands blood   
Robert Baratheon                          oh shut mouths   
Khal Drogo                                          king   

                                                                  2   \
Joffrey Baratheon                                         youre lady   
Petyr Baelish      ive heard called tywin lannisters mad dog im s...   
Cersei Baratheon   lord stark returning drunk brothel men attacke...   
Robert Baratheon                                         quiet woman   
Khal Drogo                         speaks dothraki viserys targaryen   

                                         3                              4   \
Joffrey Baratheon                      None                           None   
Petyr Baelish      bold move lord admirable                           None   
Cersei Baratheon                  took king  hes attacked brother abducted   
Robert Baratheon                hold tongue         wear silence ill honor   
Khal Drogo                       crown king                           None   

                                            5   \
Joffrey Baratheon                         None   
Petyr Baelish                             None   
Cersei Baratheon   shall wear like badge honor   
Robert Baratheon                           see   
Khal Drogo                                None   

                                                               6   \
Joffrey Baratheon                                            None   
Petyr Baelish                                                None   
Cersei Baratheon                                             None   
Robert Baratheon   tell wife return little shit imp kings landing   
Khal Drogo                                                   None   

                                                   7     8   \
Joffrey Baratheon                                None  None   
Petyr Baelish                                    None  None   
Cersei Baratheon                                 None  None   
Robert Baratheon   im half kingdom debt bloody father  piss   
Khal Drogo                                       None  None   

                                           9          10    11  \
Joffrey Baratheon                        None       None  None   
Petyr Baelish                            None       None  None   
Cersei Baratheon                         None       None  None   
Robert Baratheon   killing things clears head  oh saying         
Khal Drogo                               None       None  None   

                                                                  12  \
Joffrey Baratheon                                               None   
Petyr Baelish                                                   None   
Cersei Baratheon                                                None   
Robert Baratheon   enemy right open vicious like sending bloody i...   
Khal Drogo                                                      None   

                                 13     14                         15  \
Joffrey Baratheon              None   None                       None   
Petyr Baelish                  None   None                       None   
Cersei Baratheon               None   None                       None   
Robert Baratheon   exhilarating yes  think  ever make eight barristan   
Khal Drogo                     None   None                       None   

                     

### Episode Seven

In [123]:
df_s1.script_text[6]

[u'\n',
 u'\n',
 u'\nPoor Ned Stark. Brave man, terrible judgment.',
 u'\n',
 u'Tywin Lannister: ',
 u' Attacking him was stupid.',
 u'\n',
 u'Tywin Lannister: ',
 u' ',
 u'\nAre you gonna say something clever? Go on, say something clever.',
 u'\n',
 u'\n',
 u'Tywin Lannister: ',
 u' Why is he still alive?',
 u'\n',
 u'Jaime Lannister: ',
 u' Tyrion?',
 u'\n',
 u'Tywin Lannister: ',
 u' Ned Stark.',
 u'\n',
 u'Jaime Lannister: ',
 u' One of our men interfered, speared him through the leg before I could finish him.',
 u'\n',
 u'Tywin Lannister: ',
 u' Why is he still alive?',
 u'\n',
 u'Jaime Lannister: ',
 u" It wouldn't have been clean.",
 u'\n',
 u'Tywin Lannister: ',
 u' Clean...',
 u'\n',
 u'Tywin Lannister: ',
 u' You spend too much time worrying about what other people think of you.',
 u'\n',
 u'Jaime Lannister: ',
 u' I could care less what anyone thinks of me.',
 u'\n',
 u'Tywin Lannister: ',
 u" Now that's what you want people to think of you.",
 u'\n',
 u'Jaime Lannister: ',


In [124]:
script_text1_07 = df_s1.script_text[6]
print type(script_text1_07)

script_text1_07

<type 'list'>


[u'\n',
 u'\n',
 u'\nPoor Ned Stark. Brave man, terrible judgment.',
 u'\n',
 u'Tywin Lannister: ',
 u' Attacking him was stupid.',
 u'\n',
 u'Tywin Lannister: ',
 u' ',
 u'\nAre you gonna say something clever? Go on, say something clever.',
 u'\n',
 u'\n',
 u'Tywin Lannister: ',
 u' Why is he still alive?',
 u'\n',
 u'Jaime Lannister: ',
 u' Tyrion?',
 u'\n',
 u'Tywin Lannister: ',
 u' Ned Stark.',
 u'\n',
 u'Jaime Lannister: ',
 u' One of our men interfered, speared him through the leg before I could finish him.',
 u'\n',
 u'Tywin Lannister: ',
 u' Why is he still alive?',
 u'\n',
 u'Jaime Lannister: ',
 u" It wouldn't have been clean.",
 u'\n',
 u'Tywin Lannister: ',
 u' Clean...',
 u'\n',
 u'Tywin Lannister: ',
 u' You spend too much time worrying about what other people think of you.',
 u'\n',
 u'Jaime Lannister: ',
 u' I could care less what anyone thinks of me.',
 u'\n',
 u'Tywin Lannister: ',
 u" Now that's what you want people to think of you.",
 u'\n',
 u'Jaime Lannister: ',


In [125]:
script_split7 = [i.split('\n') for i in script_text1_07]
script_split7

[[u'', u''],
 [u'', u''],
 [u'', u'Poor Ned Stark. Brave man, terrible judgment.'],
 [u'', u''],
 [u'Tywin Lannister: '],
 [u' Attacking him was stupid.'],
 [u'', u''],
 [u'Tywin Lannister: '],
 [u' '],
 [u'', u'Are you gonna say something clever? Go on, say something clever.'],
 [u'', u''],
 [u'', u''],
 [u'Tywin Lannister: '],
 [u' Why is he still alive?'],
 [u'', u''],
 [u'Jaime Lannister: '],
 [u' Tyrion?'],
 [u'', u''],
 [u'Tywin Lannister: '],
 [u' Ned Stark.'],
 [u'', u''],
 [u'Jaime Lannister: '],
 [u' One of our men interfered, speared him through the leg before I could finish him.'],
 [u'', u''],
 [u'Tywin Lannister: '],
 [u' Why is he still alive?'],
 [u'', u''],
 [u'Jaime Lannister: '],
 [u" It wouldn't have been clean."],
 [u'', u''],
 [u'Tywin Lannister: '],
 [u' Clean...'],
 [u'', u''],
 [u'Tywin Lannister: '],
 [u' You spend too much time worrying about what other people think of you.'],
 [u'', u''],
 [u'Jaime Lannister: '],
 [u' I could care less what anyone thinks of 

In [126]:
string_script_text7 = ' '

for i in script_split7:
    for e in i:
        string_script_text7 = string_script_text7 + ' ' + e

In [127]:
string_script_text7

u'       Poor Ned Stark. Brave man, terrible judgment.   Tywin Lannister:   Attacking him was stupid.   Tywin Lannister:     Are you gonna say something clever? Go on, say something clever.     Tywin Lannister:   Why is he still alive?   Jaime Lannister:   Tyrion?   Tywin Lannister:   Ned Stark.   Jaime Lannister:   One of our men interfered, speared him through the leg before I could finish him.   Tywin Lannister:   Why is he still alive?   Jaime Lannister:   It wouldn\'t have been clean.   Tywin Lannister:   Clean...   Tywin Lannister:   You spend too much time worrying about what other people think of you.   Jaime Lannister:   I could care less what anyone thinks of me.   Tywin Lannister:   Now that\'s what you want people to think of you.   Jaime Lannister:   It\'s the truth.   Tywin Lannister:  When you hear them whispering "Kingslayer" behind your back, doesn\'t it bother you?   Jaime Lannister:   Of course it bothers me.   Tywin Lannister:   The lion doesn\'t concern himself wit

In [128]:
words7 = word_tokenize(string_script_text7)
words7

[u'Poor',
 u'Ned',
 u'Stark',
 u'.',
 u'Brave',
 u'man',
 u',',
 u'terrible',
 u'judgment',
 u'.',
 u'Tywin',
 u'Lannister',
 u':',
 u'Attacking',
 u'him',
 u'was',
 u'stupid',
 u'.',
 u'Tywin',
 u'Lannister',
 u':',
 u'Are',
 u'you',
 u'gon',
 u'na',
 u'say',
 u'something',
 u'clever',
 u'?',
 u'Go',
 u'on',
 u',',
 u'say',
 u'something',
 u'clever',
 u'.',
 u'Tywin',
 u'Lannister',
 u':',
 u'Why',
 u'is',
 u'he',
 u'still',
 u'alive',
 u'?',
 u'Jaime',
 u'Lannister',
 u':',
 u'Tyrion',
 u'?',
 u'Tywin',
 u'Lannister',
 u':',
 u'Ned',
 u'Stark',
 u'.',
 u'Jaime',
 u'Lannister',
 u':',
 u'One',
 u'of',
 u'our',
 u'men',
 u'interfered',
 u',',
 u'speared',
 u'him',
 u'through',
 u'the',
 u'leg',
 u'before',
 u'I',
 u'could',
 u'finish',
 u'him',
 u'.',
 u'Tywin',
 u'Lannister',
 u':',
 u'Why',
 u'is',
 u'he',
 u'still',
 u'alive',
 u'?',
 u'Jaime',
 u'Lannister',
 u':',
 u'It',
 u'would',
 u"n't",
 u'have',
 u'been',
 u'clean',
 u'.',
 u'Tywin',
 u'Lannister',
 u':',
 u'Clean',
 u'...',

In [129]:
sentences7 = sent_tokenize(string_script_text7)
sentences7

[u'       Poor Ned Stark.',
 u'Brave man, terrible judgment.',
 u'Tywin Lannister:   Attacking him was stupid.',
 u'Tywin Lannister:     Are you gonna say something clever?',
 u'Go on, say something clever.',
 u'Tywin Lannister:   Why is he still alive?',
 u'Jaime Lannister:   Tyrion?',
 u'Tywin Lannister:   Ned Stark.',
 u'Jaime Lannister:   One of our men interfered, speared him through the leg before I could finish him.',
 u'Tywin Lannister:   Why is he still alive?',
 u"Jaime Lannister:   It wouldn't have been clean.",
 u'Tywin Lannister:   Clean...   Tywin Lannister:   You spend too much time worrying about what other people think of you.',
 u'Jaime Lannister:   I could care less what anyone thinks of me.',
 u"Tywin Lannister:   Now that's what you want people to think of you.",
 u"Jaime Lannister:   It's the truth.",
 u'Tywin Lannister:  When you hear them whispering "Kingslayer" behind your back, doesn\'t it bother you?',
 u'Jaime Lannister:   Of course it bothers me.',
 u"Tywin

In [130]:
dialogue7 = []

for sentence in sentences7:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_07):
            dialogue7.append(sentence)

In [131]:
dialogue7

[u'Tywin Lannister:   Attacking him was stupid.',
 u'Tywin Lannister:     Are you gonna say something clever?',
 u'Tywin Lannister:   Why is he still alive?',
 u'Jaime Lannister:   Tyrion?',
 u'Tywin Lannister:   Ned Stark.',
 u'Jaime Lannister:   One of our men interfered, speared him through the leg before I could finish him.',
 u'Tywin Lannister:   Why is he still alive?',
 u"Jaime Lannister:   It wouldn't have been clean.",
 u'Tywin Lannister:   Clean...   Tywin Lannister:   You spend too much time worrying about what other people think of you.',
 u'Jaime Lannister:   I could care less what anyone thinks of me.',
 u"Tywin Lannister:   Now that's what you want people to think of you.",
 u"Jaime Lannister:   It's the truth.",
 u'Tywin Lannister:  When you hear them whispering "Kingslayer" behind your back, doesn\'t it bother you?',
 u'Jaime Lannister:   Of course it bothers me.',
 u"Tywin Lannister:   The lion doesn't concern himself with the opinions of the sheep.",
 u"Jaime Lannist

In [132]:
from collections import defaultdict

speakers7 = defaultdict(list)
for sentence in dialogue7:
    speakers7[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers7

defaultdict(list,
            {u'Barristan Selmy': [u'   He was reeling from the wine.',
              u"   His squire, from the king's own skin."],
             u'Cersei Lannister': [u"   You're in pain.",
              u"   Perhaps it's time to go home.",
              u'   Do you, Lord Stark?',
              u'   Jaime would have killed him.',
              u'   My brother is worth a thousand of your friend.',
              u'   The Targaryens wed brothers and sisters for 300 years to keep bloodlines pure.',
              u'   Jaime and I are more than brother and sister.',
              u'   No more than I love mine.',
              u'   Thank the Gods.',
              u'   Hated him?',
              u'   And what of my wrath, Lord Stark?',
              u'   Oh, but it was.',
              u'   Robert, my sweet...   Robert Baratheon'],
             u'Daenerys Stormborn': [u'   According to the prophecy, the stallions will ride to the ends of the world.',
              u'   The ear

In [133]:
speakers7['Ned Stark']

[u"   I've had worse, my lady.",
 u'   I know the truth Jon Arryn died for.',
 u'   Has he done this before?',
 u'   Your brother Or your lover?',
 u'   My son saw you with him.',
 u'   With all my heart.',
 u"   And they are all Jaime's.",
 u"   You've always hated him.",
 u"   When the King returns from his hunt, I'll tell him the truth.",
 u"   I've made many mistakes in my life, but that wasn't one of them.",
 u'   You damned fool.',
 u'   I will.',
 u"   I'll, I'll do everything I can to honor your memory.",
 u'   Give him milk of the poppy.',
 u'   No man could have protected him from himself.',
 u'   His squire?',
 u'   His Grace has had a change of heart concerning Daenerys Targaryen.',
 u'   No.',
 u'   There is no other choice.',
 u'   You promised Catelyn you would help me.']

In [134]:
episode_seven = pd.DataFrame.from_dict(speakers7, orient="index")
print episode_seven.shape

(21, 20)


In [135]:
#from numpy import nan
#episode_seven.fillna(value=str(0), inplace=True)

In [136]:
episode_seven.info()

<class 'pandas.core.frame.DataFrame'>
Index: 21 entries, Barristan Selmy to Jaime Lannister
Data columns (total 20 columns):
0     21 non-null object
1     20 non-null object
2     15 non-null object
3     14 non-null object
4     14 non-null object
5     12 non-null object
6     12 non-null object
7     11 non-null object
8     9 non-null object
9     9 non-null object
10    9 non-null object
11    7 non-null object
12    4 non-null object
13    1 non-null object
14    1 non-null object
15    1 non-null object
16    1 non-null object
17    1 non-null object
18    1 non-null object
19    1 non-null object
dtypes: object(20)
memory usage: 3.4+ KB


In [137]:
episode_seven.head()

0   \
Barristan Selmy     He was reeling from the wine.   
Petyr Baelish                        No no no no!   
Samwell Tarly                       I miss girls.   
Ned Stark                I've had worse, my lady.   
Wine Merchant                 Virzetha gizikhven!   

                                                                1   \
Barristan Selmy              His squire, from the king's own skin.   
Petyr Baelish                          Let's start over, shall we?   
Samwell Tarly       One blast for a Ranger returning, two for W...   
Ned Stark                     I know the truth Jon Arryn died for.   
Wine Merchant                                   Daenerys Stormborn   

                                                 2   \
Barristan Selmy                                None   
Petyr Baelish        I'm saving myself for another.   
Samwell Tarly                                  None   
Ned Stark                  Has he done this before?   
Wine Merchant       My Lady, you are from Westeros.   

                                             3                            4   \
Barristan Selmy                            None                         None   
Petyr Baelish                  A stupid saying.              No, not really.   
Samwell Tarly                              None                         None   
Ned Stark           Your brother Or your lover?     My son saw you with him.   
Wine Merchant                         Princess.                        That?   

                                                    5   \
Barristan Selmy                                   None   
Petyr Baelish                          For many years.   
Samwell Tarly                                     None   
Ned Stark                           With all my heart.   
Wine Merchant       The honor...the honor is all mine.   

                                                                6   \
Barristan Selmy                                               None   
Petyr Baelish                                               Oh no.   
Samwell Tarly                                                 None   
Ned Stark                                And they are all Jaime's.   
Wine Merchant       You know there are many in your homeland th...   

                                               7   \
Barristan Selmy                              None   
Petyr Baelish            Oh, everything, my dear.   
Samwell Tarly                                None   
Ned Stark                You've always hated him.   
Wine Merchant       The wine is for the Khaleesi.   

                                                                8   \
Barristan Selmy                                               None   
Petyr Baelish                       So it will be Stannis and war?   
Samwell Tarly                                                 None   
Ned Stark           When the King returns from his hunt, I'll t...   
Wine Merchant       It would be a crime to drink a wine this ri...   

                                                                9   \
Barristan Selmy                                               None   
Petyr Baelish                         So why did you call me here?   
Samwell Tarly                                                 None   
Ned Stark           I've made many mistakes in my life, but tha...   
Wine Merchant                            As the princess commands.   

                                  10          11  \
Barristan Selmy                 None        None   
Petyr Baelish           Look at you.        None   
Samwell Tarly                   None        None   
Ned Stark           You damned fool.     I will.   
Wine Merchant       Sweet, isn't it?         Me?   

                                                                12  \
Barristan Selmy                                               None   
Petyr Baelish                                                 None   
Samwell Tarly                            

In [138]:
test7 = episode_seven[0].apply(remove_stops)
test7

Barristan Selmy                                       reeling wine
Petyr Baelish                                                     
Samwell Tarly                                           miss girls
Ned Stark                                           ive worse lady
Wine Merchant                                   virzetha gizikhven
Theon Greyjoy                                     youre lucky girl
Renly Baratheon                                                ned
Tywin Lannister                                   attacking stupid
Rakharo                                                huhuh huhuh
Cersei Lannister                                        youre pain
Osha                                                          come
Khal Drogo                  stallion mounts world need iron chairs
Jorah Mormont                         dothraki things time reasons
Maester Luwin                                        theon greyjoy
Daenerys Stormborn    according prophecy stallions ride ends w

In [139]:
for column in episode_seven.columns:
    for x in range(len(episode_seven[column])):
        episode_seven[column][x] = remove_stops(episode_seven[column][x])

In [140]:
episode_seven.head(15)

0   \
Barristan Selmy                                     reeling wine   
Petyr Baelish                                                      
Samwell Tarly                                         miss girls   
Ned Stark                                         ive worse lady   
Wine Merchant                                 virzetha gizikhven   
Theon Greyjoy                                   youre lucky girl   
Renly Baratheon                                              ned   
Tywin Lannister                                 attacking stupid   
Rakharo                                              huhuh huhuh   
Cersei Lannister                                      youre pain   
Osha                                                        come   
Khal Drogo                stallion mounts world need iron chairs   
Jorah Mormont                       dothraki things time reasons   
Maester Luwin                                      theon greyjoy   
Daenerys Stormborn  according prophecy stallions ride ends world   

                                                                   1   \
Barristan Selmy                                     squire kings skin   
Petyr Baelish                                        lets start shall   
Samwell Tarly       one blast ranger returning two wildlings three...   
Ned Stark                                   know truth jon arryn died   
Wine Merchant                                      daenerys stormborn   
Theon Greyjoy                                            iron islands   
Renly Baratheon                                                  None   
Tywin Lannister                            gonna say something clever   
Rakharo                                                           huh   
Cersei Lannister                                 perhaps time go home   
Osha                                                         far away   
Khal Drogo                                  earth ends black salt sea   
Jorah Mormont       forgive khaleesi ancestor aegon conqueror didn...   
Maester Luwin                       two mutually exclusive experience   
Daenerys Stormborn                earth end sea many dirts beyond sea   

                                                       2   \
Barristan Selmy                                      None   
Petyr Baelish                           im saving another   
Samwell Tarly                                        None   
Ned Stark                                            done   
Wine Merchant                               lady westeros   
Theon Greyjoy              youve never heard iron islands   
Renly Baratheon                                      None   
Tywin Lannister                               still alive   
Rakharo                                              None   
Cersei Lannister                               lord stark   
Osha                   trust youve never heard im neither   
Khal Drogo                                           dirt   
Jorah Mormont         ah well dragons makes things easier   
Maester Luwin       chances wont nearby next time happens   
Daenerys Stormborn                              lands yes   

                                                      3   \
Barristan Selmy                                     None   
Petyr Baelish                              stupid saying   
Samwell Tarly                                       None   
Ned Stark                                  brother lover   
Wine Merchant                                   princess   
Theon Greyjoy                                 trust lord   
Renly Baratheon                                     None   
Tywin Lannister                                ned stark   
Rakharo                                             None   
Cersei Lannister                      jaime would killed   
Osha                                               whats   
Khal Drogo          lets speak wooden horses iron chairs   
Jorah Mormont                  ever seen dragon

### Episode Eight

In [141]:
df_s1.script_text[7]

[u"King's Landing",
 u'\n',
 u'\n',
 u'Syrio Forel: ',
 u' Yah! Left high, left low.',
 u'\n',
 u'\n',
 u'\n',
 u'Syrio Forel: ',
 u' Right low, lunge right.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Steward of House Stark: ',
 u' If you break anything, the Septa will have my head. What is...',
 u'\n',
 u'\n',
 u'Kingsguard',
 u'\n',
 u'\n',
 u'Septa Mordane: ',
 u' Your sister knew perfectly well we were to leave today.',
 u'\nHow she could forget...',
 u'\n',
 u'Sansa Stark: ',
 u" She didn't forget. She's with her dancing master.",
 u"\nShe's with him every morning. She always comes back with scrapes and bruises.",
 u"\nShe's so clumsy.",
 u'\n',
 u'Septa Mordane: ',
 u' Hush! Go back to your room.',
 u'\nBar the doors and do not open them for anyone you do not know.',
 u'\n',
 u'Sansa Stark: ',
 u" What is it? What's happening?",
 u'\n',
 u'Septa Mordane: ',
 u' Do as I told you. Run!',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Syrio Forel: ',
 u' This way! Left, right.',
 u'\nRah! Now you are

In [142]:
script_text1_08 = df_s1.script_text[7]
print type(script_text1_08)

script_text1_08

<type 'list'>


[u"King's Landing",
 u'\n',
 u'\n',
 u'Syrio Forel: ',
 u' Yah! Left high, left low.',
 u'\n',
 u'\n',
 u'\n',
 u'Syrio Forel: ',
 u' Right low, lunge right.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Steward of House Stark: ',
 u' If you break anything, the Septa will have my head. What is...',
 u'\n',
 u'\n',
 u'Kingsguard',
 u'\n',
 u'\n',
 u'Septa Mordane: ',
 u' Your sister knew perfectly well we were to leave today.',
 u'\nHow she could forget...',
 u'\n',
 u'Sansa Stark: ',
 u" She didn't forget. She's with her dancing master.",
 u"\nShe's with him every morning. She always comes back with scrapes and bruises.",
 u"\nShe's so clumsy.",
 u'\n',
 u'Septa Mordane: ',
 u' Hush! Go back to your room.',
 u'\nBar the doors and do not open them for anyone you do not know.',
 u'\n',
 u'Sansa Stark: ',
 u" What is it? What's happening?",
 u'\n',
 u'Septa Mordane: ',
 u' Do as I told you. Run!',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Syrio Forel: ',
 u' This way! Left, right.',
 u'\nRah! Now you are

In [143]:
script_split8 = [i.split('\n') for i in script_text1_08]
script_split8

[[u"King's Landing"],
 [u'', u''],
 [u'', u''],
 [u'Syrio Forel: '],
 [u' Yah! Left high, left low.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Syrio Forel: '],
 [u' Right low, lunge right.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Steward of House Stark: '],
 [u' If you break anything, the Septa will have my head. What is...'],
 [u'', u''],
 [u'', u''],
 [u'Kingsguard'],
 [u'', u''],
 [u'', u''],
 [u'Septa Mordane: '],
 [u' Your sister knew perfectly well we were to leave today.'],
 [u'', u'How she could forget...'],
 [u'', u''],
 [u'Sansa Stark: '],
 [u" She didn't forget. She's with her dancing master."],
 [u'',
  u"She's with him every morning. She always comes back with scrapes and bruises."],
 [u'', u"She's so clumsy."],
 [u'', u''],
 [u'Septa Mordane: '],
 [u' Hush! Go back to your room.'],
 [u'', u'Bar the doors and do not open them for anyone you do not know.'],
 [u'', u''],
 [u'Sansa Stark: '],
 [u" What is it? What's happening?"],
 [u'', u''],
 [u'Septa Mo

In [144]:
string_script_text8 = ' '

for i in script_split8:
    for e in i:
        string_script_text8 = string_script_text8 + ' ' + e

In [145]:
string_script_text8

u'  King\'s Landing     Syrio Forel:   Yah! Left high, left low.       Syrio Forel:   Right low, lunge right.         Steward of House Stark:   If you break anything, the Septa will have my head. What is...     Kingsguard     Septa Mordane:   Your sister knew perfectly well we were to leave today.  How she could forget...   Sansa Stark:   She didn\'t forget. She\'s with her dancing master.  She\'s with him every morning. She always comes back with scrapes and bruises.  She\'s so clumsy.   Septa Mordane:   Hush! Go back to your room.  Bar the doors and do not open them for anyone you do not know.   Sansa Stark:   What is it? What\'s happening?   Septa Mordane:   Do as I told you. Run!         Syrio Forel:   This way! Left, right.  Rah! Now you are dead.   Arya Stark:   You said right, but you went left.   Syrio Forel:   And now you are a dead girl.   Arya Stark:   Only \'cause you lied.   Syrio Forel:   My tongue lied.  My eyes shouted the truth.  You were not seeing.   Arya Stark:   I 

In [146]:
words8 = word_tokenize(string_script_text8)
words8

[u'King',
 u"'s",
 u'Landing',
 u'Syrio',
 u'Forel',
 u':',
 u'Yah',
 u'!',
 u'Left',
 u'high',
 u',',
 u'left',
 u'low',
 u'.',
 u'Syrio',
 u'Forel',
 u':',
 u'Right',
 u'low',
 u',',
 u'lunge',
 u'right',
 u'.',
 u'Steward',
 u'of',
 u'House',
 u'Stark',
 u':',
 u'If',
 u'you',
 u'break',
 u'anything',
 u',',
 u'the',
 u'Septa',
 u'will',
 u'have',
 u'my',
 u'head',
 u'.',
 u'What',
 u'is',
 u'...',
 u'Kingsguard',
 u'Septa',
 u'Mordane',
 u':',
 u'Your',
 u'sister',
 u'knew',
 u'perfectly',
 u'well',
 u'we',
 u'were',
 u'to',
 u'leave',
 u'today',
 u'.',
 u'How',
 u'she',
 u'could',
 u'forget',
 u'...',
 u'Sansa',
 u'Stark',
 u':',
 u'She',
 u'did',
 u"n't",
 u'forget',
 u'.',
 u'She',
 u"'s",
 u'with',
 u'her',
 u'dancing',
 u'master',
 u'.',
 u'She',
 u"'s",
 u'with',
 u'him',
 u'every',
 u'morning',
 u'.',
 u'She',
 u'always',
 u'comes',
 u'back',
 u'with',
 u'scrapes',
 u'and',
 u'bruises',
 u'.',
 u'She',
 u"'s",
 u'so',
 u'clumsy',
 u'.',
 u'Septa',
 u'Mordane',
 u':',
 u'Hush

In [147]:
sentences8 = sent_tokenize(string_script_text8)
sentences8

[u"  King's Landing     Syrio Forel:   Yah!",
 u'Left high, left low.',
 u'Syrio Forel:   Right low, lunge right.',
 u'Steward of House Stark:   If you break anything, the Septa will have my head.',
 u'What is...     Kingsguard     Septa Mordane:   Your sister knew perfectly well we were to leave today.',
 u"How she could forget...   Sansa Stark:   She didn't forget.",
 u"She's with her dancing master.",
 u"She's with him every morning.",
 u'She always comes back with scrapes and bruises.',
 u"She's so clumsy.",
 u'Septa Mordane:   Hush!',
 u'Go back to your room.',
 u'Bar the doors and do not open them for anyone you do not know.',
 u'Sansa Stark:   What is it?',
 u"What's happening?",
 u'Septa Mordane:   Do as I told you.',
 u'Run!',
 u'Syrio Forel:   This way!',
 u'Left, right.',
 u'Rah!',
 u'Now you are dead.',
 u'Arya Stark:   You said right, but you went left.',
 u'Syrio Forel:   And now you are a dead girl.',
 u"Arya Stark:   Only 'cause you lied.",
 u'Syrio Forel:   My tongue l

In [148]:
dialogue8 = []

for sentence in sentences8:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_08):
            dialogue8.append(sentence)

/Users/zoemarkovits/anaconda/lib/python2.7/site-packages/ipykernel_launcher.py:6: UnicodeWarning: Unicode equal comparison failed to convert both arguments to Unicode - interpreting them as being unequal
  


In [149]:
dialogue8

[u'Syrio Forel:   Right low, lunge right.',
 u'Septa Mordane:   Hush!',
 u'Sansa Stark:   What is it?',
 u'Septa Mordane:   Do as I told you.',
 u'Syrio Forel:   This way!',
 u'Arya Stark:   You said right, but you went left.',
 u'Syrio Forel:   And now you are a dead girl.',
 u"Arya Stark:   Only 'cause you lied.",
 u'Syrio Forel:   My tongue lied.',
 u'Arya Stark:   I was so.',
 u'Syrio Forel:   And why is it that Lord Eddard is sending Lannister men in place of his own?',
 u'Meryn Trant:   Mind your place, dancing master.',
 u"Arya Stark:   My father wouldn't send you.",
 u"Arya Stark:   And I don't have to go with you if I don't want.",
 u'Syrio Forel:   Are you men or snakes, that you would threaten a child?',
 u'Syrio Forel:   I am Syrio Forel.',
 u'Syrio Forel:   And you will be speaking to me with more respect.',
 u'Meryn Trant:   Kill the Braavosi.',
 u'Syrio Forel:   Arya child, we are done with dancing for the day.',
 u'Meryn Trant:   Bloody oafs.',
 u'Syrio Forel:   Be gone

In [150]:
from collections import defaultdict

speakers8 = defaultdict(list)
for sentence in dialogue8:
    speakers8[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers8

defaultdict(list,
            {u'Arya Stark': [u'   You said right, but you went left.',
              u"   Only 'cause you lied.",
              u'   I was so.',
              u"   My father wouldn't send you.",
              u"   And I don't have to go with you if I don't want.",
              u'   Come with me.',
              u'   Not today.',
              u'   Not today.',
              u'   Needle.',
              u'   What do you want?',
              u'   Leave me be.',
              u'   Stay away!'],
             u'Barristan Selmy': [u'   Your Grace, I am yours to command.',
              u'   Your Grace, the Kingsguard is a sworn brotherhood.',
              u'   Your Grace...   Cersei Lannister',
              u'   The man who profaned his blade with the blood of the King he had sworn to defend!',
              u'   A hall to die in and men to bury me.',
              u'   Even now I could cut through the five of you like carving a cake!'],
             u'Catelyn Stark': [

In [151]:
speakers8['Arya Stark']

[u'   You said right, but you went left.',
 u"   Only 'cause you lied.",
 u'   I was so.',
 u"   My father wouldn't send you.",
 u"   And I don't have to go with you if I don't want.",
 u'   Come with me.',
 u'   Not today.',
 u'   Not today.',
 u'   Needle.',
 u'   What do you want?',
 u'   Leave me be.',
 u'   Stay away!']

In [152]:
episode_eight = pd.DataFrame.from_dict(speakers8, orient="index")
print episode_eight.shape

(28, 17)


In [153]:
#from numpy import nan
#episode_eight.fillna(value=str(0), inplace=True)

In [154]:
episode_eight.info()

<class 'pandas.core.frame.DataFrame'>
Index: 28 entries, King Joffrey to Jon Snow
Data columns (total 17 columns):
0     28 non-null object
1     25 non-null object
2     19 non-null object
3     15 non-null object
4     13 non-null object
5     11 non-null object
6     10 non-null object
7     10 non-null object
8     6 non-null object
9     5 non-null object
10    4 non-null object
11    4 non-null object
12    2 non-null object
13    1 non-null object
14    1 non-null object
15    1 non-null object
16    1 non-null object
dtypes: object(17)
memory usage: 3.9+ KB


In [155]:
episode_eight.head()

0   \
King Joffrey                    You let my father die.   
Petyr Baelish        The girl is innocent, Your Grace.   
Tyrion Lannister                                Uncle.   
Samwell Tarly                               The smell.   
Sandor Clegane               Who do you think sent me?   

                                              1   \
King Joffrey              Come forward, My Lady.   
Petyr Baelish        A naked Knight, apparently.   
Tyrion Lannister        Sorry to disappoint you.   
Samwell Tarly                     There is none.   
Sandor Clegane                              None   

                                                                 2   \
King Joffrey                             He said I wasn't the King.   
Petyr Baelish                      Do you deny your father's crime?   
Tyrion Lannister     May I present My Lord Father, Tywin son of ...   
Samwell Tarly                                                  None   
Sandor Clegane                                                 None   

                                                        3   \
King Joffrey                                Anything else?   
Petyr Baelish                                         None   
Tyrion Lannister     We have our differences, Jaime and I.   
Samwell Tarly                                         None   
Sandor Clegane                                        None   

                                                  4   \
King Joffrey         Your sweet words have moved me.   
Petyr Baelish                                   None   
Tyrion Lannister                     And the Starks?   
Samwell Tarly                                   None   
Sandor Clegane                                  None   

                                                                 5   \
King Joffrey                                                   None   
Petyr Baelish                                                  None   
Tyrion Lannister     How did my sweet sister persuade the King t...   
Samwell Tarly                                                  None   
Sandor Clegane                                                 None   

                                             6          7     8     9     10  \
King Joffrey                               None       None  None  None  None   
Petyr Baelish                              None       None  None  None  None   
Tyrion Lannister     My sister rules, you mean.     Maybe.  None  None  None   
Samwell Tarly                              None       None  None  None  None   
Sandor Clegane                             None       None  None  None  None   

                    11    12    13    14    15    16  
King Joffrey      None  None  None  None  None  None  
Petyr Baelish     None  None  None  None  None  None  
Tyrion Lannister  None  None  None  None  None  None  
Samwell Tarly     None  None  None  None  None  None  
Sandor Clegane    None  None  None  None  None  None

In [156]:
test8 = episode_eight[0].apply(remove_stops)
test8

King Joffrey                                           let father die
Petyr Baelish                                     girl innocent grace
Tyrion Lannister                                                uncle
Samwell Tarly                                                   smell
Sandor Clegane                                             think sent
Tywin Lannister                               rumors demise unfounded
Arya Stark                                       said right went left
Septa Mordane                                                    hush
Othell Yarwyck             one jafer flowers lord less hand wolf tore
Jeor Mormont                                      othor without doubt
Ned Stark                                                       varys
Stark guard                                              pardon lords
Catelyn Stark                             late lord frey father calls
Meryn Trant                                 mind place dancing master
Ser Alliser         

In [157]:
for column in episode_eight.columns:
    for x in range(len(episode_eight[column])):
        episode_eight[column][x] = remove_stops(episode_eight[column][x])

In [158]:
episode_eight.head()

0                        1   \
King Joffrey           let father die        come forward lady   
Petyr Baelish     girl innocent grace  naked knight apparently   
Tyrion Lannister                uncle         sorry disappoint   
Samwell Tarly                   smell                     none   
Sandor Clegane             think sent                     None   

                                                                 2   \
King Joffrey                                        said wasnt king   
Petyr Baelish                                    deny fathers crime   
Tyrion Lannister  may present lord father tywin son tytos house ...   
Samwell Tarly                                                  None   
Sandor Clegane                                                 None   

                                 3                  4   \
King Joffrey          anything else  sweet words moved   
Petyr Baelish                  None               None   
Tyrion Lannister  differences jaime             starks   
Samwell Tarly                  None               None   
Sandor Clegane                 None               None   

                                                                 5   \
King Joffrey                                                   None   
Petyr Baelish                                                  None   
Tyrion Lannister  sweet sister persuade king imprison dear frien...   
Samwell Tarly                                                  None   
Sandor Clegane                                                 None   

                                 6      7     8     9     10    11    12  \
King Joffrey                   None   None  None  None  None  None  None   
Petyr Baelish                  None   None  None  None  None  None  None   
Tyrion Lannister  sister rules mean  maybe  None  None  None  None  None   
Samwell Tarly                  None   None  None  None  None  None  None   
Sandor Clegane                 None   None  None  None  None  None  None   

                    13    14    15    16  
King Joffrey      None  None  None  None  
Petyr Baelish     None  None  None  None  
Tyrion Lannister  None  None  None  None  
Samwell Tarly     None  None  None  None  
Sandor Clegane    None  None  None  None

### Episode Nine

In [159]:
df_s1.script_text[8]

[u'\n',
 u'Varys: ',
 u" You've seen better days, my lord.",
 u'\n',
 u'Eddard Stark: ',
 u" Another visit? lt seems you're my last friend.",
 u'\n',
 u'Varys: ',
 u' No, no, many still love you. Sansa came to court this morning to plead for your life.',
 u'\n',
 u'Eddard Stark: ',
 u' On her knees begging for me. Hm! Did you laugh with the others?',
 u'\n',
 u'Varys: ',
 u' You do me wrong, my lord. Your blood is the last thing l want.',
 u'\n',
 u'Eddard Stark: ',
 u" l don't know what you want. l've given up trying to guess.",
 u'\n',
 u'Varys: ',
 u" When l was still a boy - before they cut my balls off with a hot knife - l traveled with a group of actors through the free cities. They taught me that each man has a role to play. The same is true at court. l am the master of whisperers. My role is to be sly, obsequious and without scruples. l'm a good actor, my lord.",
 u'\n',
 u'Eddard Stark: ',
 u' Huh. Can you free me from this pit?',
 u'\n',
 u'Varys: ',
 u" l could. But will l? 

In [160]:
script_text1_09 = df_s1.script_text[8]
print type(script_text1_09)

script_text1_09

<type 'list'>


[u'\n',
 u'Varys: ',
 u" You've seen better days, my lord.",
 u'\n',
 u'Eddard Stark: ',
 u" Another visit? lt seems you're my last friend.",
 u'\n',
 u'Varys: ',
 u' No, no, many still love you. Sansa came to court this morning to plead for your life.',
 u'\n',
 u'Eddard Stark: ',
 u' On her knees begging for me. Hm! Did you laugh with the others?',
 u'\n',
 u'Varys: ',
 u' You do me wrong, my lord. Your blood is the last thing l want.',
 u'\n',
 u'Eddard Stark: ',
 u" l don't know what you want. l've given up trying to guess.",
 u'\n',
 u'Varys: ',
 u" When l was still a boy - before they cut my balls off with a hot knife - l traveled with a group of actors through the free cities. They taught me that each man has a role to play. The same is true at court. l am the master of whisperers. My role is to be sly, obsequious and without scruples. l'm a good actor, my lord.",
 u'\n',
 u'Eddard Stark: ',
 u' Huh. Can you free me from this pit?',
 u'\n',
 u'Varys: ',
 u" l could. But will l? 

In [161]:
script_split9 = [i.split('\n') for i in script_text1_09]
script_split9

[[u'', u''],
 [u'Varys: '],
 [u" You've seen better days, my lord."],
 [u'', u''],
 [u'Eddard Stark: '],
 [u" Another visit? lt seems you're my last friend."],
 [u'', u''],
 [u'Varys: '],
 [u' No, no, many still love you. Sansa came to court this morning to plead for your life.'],
 [u'', u''],
 [u'Eddard Stark: '],
 [u' On her knees begging for me. Hm! Did you laugh with the others?'],
 [u'', u''],
 [u'Varys: '],
 [u' You do me wrong, my lord. Your blood is the last thing l want.'],
 [u'', u''],
 [u'Eddard Stark: '],
 [u" l don't know what you want. l've given up trying to guess."],
 [u'', u''],
 [u'Varys: '],
 [u" When l was still a boy - before they cut my balls off with a hot knife - l traveled with a group of actors through the free cities. They taught me that each man has a role to play. The same is true at court. l am the master of whisperers. My role is to be sly, obsequious and without scruples. l'm a good actor, my lord."],
 [u'', u''],
 [u'Eddard Stark: '],
 [u' Huh. Can you 

In [162]:
string_script_text9 = ' '

for i in script_split9:
    for e in i:
        string_script_text9 = string_script_text9 + ' ' + e

In [163]:
string_script_text9

u"    Varys:   You've seen better days, my lord.   Eddard Stark:   Another visit? lt seems you're my last friend.   Varys:   No, no, many still love you. Sansa came to court this morning to plead for your life.   Eddard Stark:   On her knees begging for me. Hm! Did you laugh with the others?   Varys:   You do me wrong, my lord. Your blood is the last thing l want.   Eddard Stark:   l don't know what you want. l've given up trying to guess.   Varys:   When l was still a boy - before they cut my balls off with a hot knife - l traveled with a group of actors through the free cities. They taught me that each man has a role to play. The same is true at court. l am the master of whisperers. My role is to be sly, obsequious and without scruples. l'm a good actor, my lord.   Eddard Stark:   Huh. Can you free me from this pit?   Varys:   l could. But will l? No. As l said, I'm no hero.   Eddard Stark:   What do you want? Tell me. No riddles, no stories. Tell me, what do you want?   Varys:   Pea

In [164]:
words9 = word_tokenize(string_script_text9)
words9

[u'Varys',
 u':',
 u'You',
 u"'ve",
 u'seen',
 u'better',
 u'days',
 u',',
 u'my',
 u'lord',
 u'.',
 u'Eddard',
 u'Stark',
 u':',
 u'Another',
 u'visit',
 u'?',
 u'lt',
 u'seems',
 u'you',
 u"'re",
 u'my',
 u'last',
 u'friend',
 u'.',
 u'Varys',
 u':',
 u'No',
 u',',
 u'no',
 u',',
 u'many',
 u'still',
 u'love',
 u'you',
 u'.',
 u'Sansa',
 u'came',
 u'to',
 u'court',
 u'this',
 u'morning',
 u'to',
 u'plead',
 u'for',
 u'your',
 u'life',
 u'.',
 u'Eddard',
 u'Stark',
 u':',
 u'On',
 u'her',
 u'knees',
 u'begging',
 u'for',
 u'me',
 u'.',
 u'Hm',
 u'!',
 u'Did',
 u'you',
 u'laugh',
 u'with',
 u'the',
 u'others',
 u'?',
 u'Varys',
 u':',
 u'You',
 u'do',
 u'me',
 u'wrong',
 u',',
 u'my',
 u'lord',
 u'.',
 u'Your',
 u'blood',
 u'is',
 u'the',
 u'last',
 u'thing',
 u'l',
 u'want',
 u'.',
 u'Eddard',
 u'Stark',
 u':',
 u'l',
 u'do',
 u"n't",
 u'know',
 u'what',
 u'you',
 u'want',
 u'.',
 u'l',
 u"'ve",
 u'given',
 u'up',
 u'trying',
 u'to',
 u'guess',
 u'.',
 u'Varys',
 u':',
 u'When',
 u'l'

In [165]:
sentences9 = sent_tokenize(string_script_text9)
sentences9

[u"    Varys:   You've seen better days, my lord.",
 u'Eddard Stark:   Another visit?',
 u"lt seems you're my last friend.",
 u'Varys:   No, no, many still love you.',
 u'Sansa came to court this morning to plead for your life.',
 u'Eddard Stark:   On her knees begging for me.',
 u'Hm!',
 u'Did you laugh with the others?',
 u'Varys:   You do me wrong, my lord.',
 u'Your blood is the last thing l want.',
 u"Eddard Stark:   l don't know what you want.",
 u"l've given up trying to guess.",
 u'Varys:   When l was still a boy - before they cut my balls off with a hot knife - l traveled with a group of actors through the free cities.',
 u'They taught me that each man has a role to play.',
 u'The same is true at court.',
 u'l am the master of whisperers.',
 u'My role is to be sly, obsequious and without scruples.',
 u"l'm a good actor, my lord.",
 u'Eddard Stark:   Huh.',
 u'Can you free me from this pit?',
 u'Varys:   l could.',
 u'But will l?',
 u'No.',
 u"As l said, I'm no hero.",
 u'Eddar

In [166]:
dialogue9 = []

for sentence in sentences9:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_09):
            dialogue9.append(sentence)

/Users/zoemarkovits/anaconda/lib/python2.7/site-packages/ipykernel_launcher.py:6: UnicodeWarning: Unicode equal comparison failed to convert both arguments to Unicode - interpreting them as being unequal
  


In [167]:
dialogue9

[u'Eddard Stark:   Another visit?',
 u'Varys:   No, no, many still love you.',
 u'Eddard Stark:   On her knees begging for me.',
 u'Varys:   You do me wrong, my lord.',
 u"Eddard Stark:   l don't know what you want.",
 u'Varys:   When l was still a boy - before they cut my balls off with a hot knife - l traveled with a group of actors through the free cities.',
 u'Eddard Stark:   Huh.',
 u'Varys:   l could.',
 u'Eddard Stark:   What do you want?',
 u'Varys:   Peace.',
 u'Eddard Stark:   Robb?',
 u'Varys:   Boys have been conquerors before.',
 u"Eddard Stark:   Stannis Baratheon is Robert's true heir.",
 u'Varys:   Sansa pleaded so sweetly for your life.',
 u'Eddard Stark:   You want me to serve the woman who murdered my king, who butchered my men, who crippled my son?',
 u'Varys:   l want you to serve the realm!',
 u'Eddard Stark:   You think my life is some precious thing to me?',
 u'Varys:   Pity.',
 u'Theon Greyjoy:   Or so Walder Frey would have you think.',
 u'Catelyn Stark:   Kee

In [168]:
from collections import defaultdict

speakers9 = defaultdict(list)
for sentence in dialogue9:
    speakers9[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers9

defaultdict(list,
            {u'All': [u'   Sword!'],
             u'Arya Stark': [u'   How about a nice fat pigeon?',
              u'   Do you have any stale ones from yesterday?',
              u"   Hey, where's everyone going?",
              u'   Who?',
              u'   Let me go.'],
             u'Bronn': [u'   l took her.',
              u"   From, uh, Ser What's-his-name?",
              u'   He said something.',
              u'   Oh, well.',
              u'    Drink.',
              u"   There's a Braavosi knife game l could teach you.",
              u'   Not if you win.',
              u'   This sounds like a boring game.',
              u'   But my mother hit harder.',
              u'   lt was a woman.',
              u'   Work.',
              u'   The whole shit-stained world could drink off that one.',
              u'   Our lord here used to be married.',
              u'   You hear lots of things playing dice with Lannister soldiers.',
              u"   l'm gues

In [169]:
speakers9['Arya Stark']

[u'   How about a nice fat pigeon?',
 u'   Do you have any stale ones from yesterday?',
 u"   Hey, where's everyone going?",
 u'   Who?',
 u'   Let me go.']

In [170]:
episode_nine = pd.DataFrame.from_dict(speakers9, orient="index")
print episode_nine.shape

(39, 62)


In [171]:
#from numpy import nan
#episode_nine.fillna(value=str(0), inplace=True)

In [172]:
episode_nine.info()

<class 'pandas.core.frame.DataFrame'>
Index: 39 entries, Joffrey Baratheon to Street Urchin
Data columns (total 62 columns):
0     39 non-null object
1     29 non-null object
2     24 non-null object
3     19 non-null object
4     19 non-null object
5     14 non-null object
6     14 non-null object
7     14 non-null object
8     13 non-null object
9     9 non-null object
10    8 non-null object
11    7 non-null object
12    7 non-null object
13    7 non-null object
14    7 non-null object
15    7 non-null object
16    7 non-null object
17    7 non-null object
18    6 non-null object
19    5 non-null object
20    5 non-null object
21    5 non-null object
22    5 non-null object
23    5 non-null object
24    5 non-null object
25    3 non-null object
26    3 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
31    1 non-null object
32    1 non-null object
33    1 non-null object
34    1 non-null object
35    1 non-null object
36

In [173]:
episode_nine.head()

0   \
Joffrey Baratheon     My mother wishes me to let Lord Eddard join...   
Populace                                                    Traitor!   
Cersei Baratheon                            My son, this is madness.   
Khal Drogo                                       My horse…   Cohollo   
Yoren                                                    Don't look!   

                                    1                2     3     4     5   \
Joffrey Baratheon                 None             None  None  None  None   
Populace                      Traitor!    Put him down!  None  None  None   
Cersei Baratheon                  None             None  None  None  None   
Khal Drogo                        None             None  None  None  None   
Yoren                 Shut your mouth.             None  None  None  None   

                     6     7     8     9     10    11    12    13    14    15  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     16    17    18    19    20    21    22    23    24    25  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     26    27    28    29    30    31    32    33    34    35  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     36    37    38    39    40    41    42    43    44    45  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     46    47    48    49    50    51    52    53    54    55  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     56    57    58    59    60    61  
Joffrey Baratheon  None  None  None  None  None  None  
Populace           None  None  None  None  None  None  
Cersei Baratheon   None  None  None  None  None  None  
Khal Drogo         None  None  None  None  None  None  
Yoren              None  None  None  None  None  None

In [174]:
test9 = episode_nine[0].apply(remove_stops)
test9

Joffrey Baratheon       mother wishes let lord eddard join nights watch
Populace                                                        traitor
Cersei Baratheon                                            son madness
Khal Drogo                                                horse cohollo
Yoren                                                         dont look
Shae                                                              ls lm
Maester Aemon                                                  l indeed
Tyrion Lannister                                            oh continue
Samwell Tarly                                                  l l cant
Stevron Frey                                              father forget
Pyp                                                        go lets look
Theon Greyjoy                                   walder frey would think
Tywin Lannister       boy may lack experience sense certain mindless...
Qotho                                                        fel

In [175]:
for column in episode_nine.columns:
    for x in range(len(episode_nine[column])):
        episode_nine[column][x] = remove_stops(episode_nine[column][x])

In [176]:
episode_nine.head()

0   \
Joffrey Baratheon  mother wishes let lord eddard join nights watch   
Populace                                                   traitor   
Cersei Baratheon                                       son madness   
Khal Drogo                                           horse cohollo   
Yoren                                                    dont look   

                           1     2     3     4     5     6     7     8     9   \
Joffrey Baratheon        None  None  None  None  None  None  None  None  None   
Populace              traitor   put  None  None  None  None  None  None  None   
Cersei Baratheon         None  None  None  None  None  None  None  None  None   
Khal Drogo               None  None  None  None  None  None  None  None  None   
Yoren              shut mouth  None  None  None  None  None  None  None  None   

                     10    11    12    13    14    15    16    17    18    19  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     20    21    22    23    24    25    26    27    28    29  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     30    31    32    33    34    35    36    37    38    39  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     40    41    42    43    44    45    46    47    48    49  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     50    51    52    53    54    55    56    57    58    59  \
Joffrey Baratheon  None  None  None  None  None  None  None  None  None  None   
Populace           None  None  None  None  None  None  None  None  None  None   
Cersei Baratheon   None  None  None  None  None  None  None  None  None  None   
Khal Drogo         None  None  None  None  None  None  None  None  None  None   
Yoren              None  None  None  None  None  None  None  None  None  None   

                     60    61  
Joffrey Baratheon  None  None  
Populace           None  None  
Cersei Baratheon   None  None  
Khal Drogo         None  None  
Yoren              None  None

### Episode Ten

In [177]:
df_s1.script_text[9]

[u'\n',
 u'\n',
 u'Yoren: ',
 u" Look at me. Look at me! Do you remember me now, boy, eh? Remember me? There's a bright boy. You'll be coming with me, boy, and you'll be keeping your mouth shut.",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Yoren: ',
 u' Keep your mouth shut, boy. ',
 u'\n',
 u'Arya Stark: ',
 u" l'm not a boy!",
 u'\n',
 u'Yoren: ',
 u" You're not a smart boy, is that what you're trying to say? Do you want to live, boy?! ",
 u" North, boy, we're going north.",
 u'\n',
 u'\n------------------------------------------',
 u'\n',
 u'\n',
 u'\n',
 u'Bran Stark: ',
 u' lt had three eyes. lt told me to come with him, so l did. We went down into the crypts and my father was there.',
 u'\n',
 u'Osha: ',
 u" Your father's not down there, little lord. Not for many years yet.",
 u'\n',
 u'Bran Stark: ',
 u" You're afraid. Just like Hodor.",
 u'\n',
 u'Osha: ',
 u" l'm not afraid of some hole in the ground.",
 u'\n',
 u'Bran Stark: ',
 u" You've lived beyond the Wall. What are you scared of

In [178]:
script_text1_10 = df_s1.script_text[9]
print type(script_text1_10)

script_text1_10

<type 'list'>


[u'\n',
 u'\n',
 u'Yoren: ',
 u" Look at me. Look at me! Do you remember me now, boy, eh? Remember me? There's a bright boy. You'll be coming with me, boy, and you'll be keeping your mouth shut.",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'Yoren: ',
 u' Keep your mouth shut, boy. ',
 u'\n',
 u'Arya Stark: ',
 u" l'm not a boy!",
 u'\n',
 u'Yoren: ',
 u" You're not a smart boy, is that what you're trying to say? Do you want to live, boy?! ",
 u" North, boy, we're going north.",
 u'\n',
 u'\n------------------------------------------',
 u'\n',
 u'\n',
 u'\n',
 u'Bran Stark: ',
 u' lt had three eyes. lt told me to come with him, so l did. We went down into the crypts and my father was there.',
 u'\n',
 u'Osha: ',
 u" Your father's not down there, little lord. Not for many years yet.",
 u'\n',
 u'Bran Stark: ',
 u" You're afraid. Just like Hodor.",
 u'\n',
 u'Osha: ',
 u" l'm not afraid of some hole in the ground.",
 u'\n',
 u'Bran Stark: ',
 u" You've lived beyond the Wall. What are you scared of

In [179]:
script_split10 = [i.split('\n') for i in script_text1_10]
script_split10

[[u'', u''],
 [u'', u''],
 [u'Yoren: '],
 [u" Look at me. Look at me! Do you remember me now, boy, eh? Remember me? There's a bright boy. You'll be coming with me, boy, and you'll be keeping your mouth shut."],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Yoren: '],
 [u' Keep your mouth shut, boy. '],
 [u'', u''],
 [u'Arya Stark: '],
 [u" l'm not a boy!"],
 [u'', u''],
 [u'Yoren: '],
 [u" You're not a smart boy, is that what you're trying to say? Do you want to live, boy?! "],
 [u" North, boy, we're going north."],
 [u'', u''],
 [u'', u'------------------------------------------'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'Bran Stark: '],
 [u' lt had three eyes. lt told me to come with him, so l did. We went down into the crypts and my father was there.'],
 [u'', u''],
 [u'Osha: '],
 [u" Your father's not down there, little lord. Not for many years yet."],
 [u'', u''],
 [u'Bran Stark: '],
 [u" You're afraid. Just like Hodor."],
 [u'', u''],
 [u'Osha: '],
 [u" l'm not afraid

In [180]:
string_script_text10 = ' '

for i in script_split10:
    for e in i:
        string_script_text10 = string_script_text10 + ' ' + e

In [181]:
string_script_text10

u'      Yoren:   Look at me. Look at me! Do you remember me now, boy, eh? Remember me? There\'s a bright boy. You\'ll be coming with me, boy, and you\'ll be keeping your mouth shut.         Yoren:   Keep your mouth shut, boy.    Arya Stark:   l\'m not a boy!   Yoren:   You\'re not a smart boy, is that what you\'re trying to say? Do you want to live, boy?!   North, boy, we\'re going north.    ------------------------------------------       Bran Stark:   lt had three eyes. lt told me to come with him, so l did. We went down into the crypts and my father was there.   Osha:   Your father\'s not down there, little lord. Not for many years yet.   Bran Stark:   You\'re afraid. Just like Hodor.   Osha:   l\'m not afraid of some hole in the ground.   Bran Stark:   You\'ve lived beyond the Wall. What are you scared of? l\'m a crippled boy and l\'m willing to go.       Bran Stark:   That\'s my grandfather, Lord Rickard. He was burned alive by the Mad King, Aerys. That\'s Lyanna, my father\'s sis

In [182]:
words10 = word_tokenize(string_script_text10)
words10

[u'Yoren',
 u':',
 u'Look',
 u'at',
 u'me',
 u'.',
 u'Look',
 u'at',
 u'me',
 u'!',
 u'Do',
 u'you',
 u'remember',
 u'me',
 u'now',
 u',',
 u'boy',
 u',',
 u'eh',
 u'?',
 u'Remember',
 u'me',
 u'?',
 u'There',
 u"'s",
 u'a',
 u'bright',
 u'boy',
 u'.',
 u'You',
 u"'ll",
 u'be',
 u'coming',
 u'with',
 u'me',
 u',',
 u'boy',
 u',',
 u'and',
 u'you',
 u"'ll",
 u'be',
 u'keeping',
 u'your',
 u'mouth',
 u'shut',
 u'.',
 u'Yoren',
 u':',
 u'Keep',
 u'your',
 u'mouth',
 u'shut',
 u',',
 u'boy',
 u'.',
 u'Arya',
 u'Stark',
 u':',
 u'l',
 u"'m",
 u'not',
 u'a',
 u'boy',
 u'!',
 u'Yoren',
 u':',
 u'You',
 u"'re",
 u'not',
 u'a',
 u'smart',
 u'boy',
 u',',
 u'is',
 u'that',
 u'what',
 u'you',
 u"'re",
 u'trying',
 u'to',
 u'say',
 u'?',
 u'Do',
 u'you',
 u'want',
 u'to',
 u'live',
 u',',
 u'boy',
 u'?',
 u'!',
 u'North',
 u',',
 u'boy',
 u',',
 u'we',
 u"'re",
 u'going',
 u'north',
 u'.',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--',
 u'--

In [183]:
sentences10 = sent_tokenize(string_script_text10)
sentences10

[u'      Yoren:   Look at me.',
 u'Look at me!',
 u'Do you remember me now, boy, eh?',
 u'Remember me?',
 u"There's a bright boy.",
 u"You'll be coming with me, boy, and you'll be keeping your mouth shut.",
 u'Yoren:   Keep your mouth shut, boy.',
 u"Arya Stark:   l'm not a boy!",
 u"Yoren:   You're not a smart boy, is that what you're trying to say?",
 u'Do you want to live, boy?!',
 u"North, boy, we're going north.",
 u'------------------------------------------       Bran Stark:   lt had three eyes.',
 u'lt told me to come with him, so l did.',
 u'We went down into the crypts and my father was there.',
 u"Osha:   Your father's not down there, little lord.",
 u'Not for many years yet.',
 u"Bran Stark:   You're afraid.",
 u'Just like Hodor.',
 u"Osha:   l'm not afraid of some hole in the ground.",
 u"Bran Stark:   You've lived beyond the Wall.",
 u'What are you scared of?',
 u"l'm a crippled boy and l'm willing to go.",
 u"Bran Stark:   That's my grandfather, Lord Rickard.",
 u'He was

In [184]:
dialogue10 = []

for sentence in sentences10:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names1_10):
            dialogue10.append(sentence)

In [185]:
dialogue10

[u'Yoren:   Keep your mouth shut, boy.',
 u"Arya Stark:   l'm not a boy!",
 u"Yoren:   You're not a smart boy, is that what you're trying to say?",
 u"Osha:   Your father's not down there, little lord.",
 u"Bran Stark:   You're afraid.",
 u"Osha:   l'm not afraid of some hole in the ground.",
 u"Bran Stark:   You've lived beyond the Wall.",
 u"Bran Stark:   That's my grandfather, Lord Rickard.",
 u'Osha:   You see?',
 u'Rickon Stark:   Here, Shaggydog.',
 u'Bran Stark:   Rickon!',
 u'Osha:   That beast is supposed to be chained in the kennels!',
 u"Rickon Stark:   He doesn't like chains.",
 u'Bran Stark:   What are you doing down here?',
 u'Rickon Stark:   No, l came to see Father.',
 u'Bran Stark:   How many times have l told you?',
 u'Rickon Stark:   He was down here.',
 u'Bran Stark:   Saw him when?',
 u'Rickon Stark:   Last night, when l was sleeping.',
 u'Osha:   You both miss him.',
 u'Catelyn Stark:   Robb.',
 u'Catelyn Stark:   Shh!',
 u"Robb Stark:   l'll kill them all.",
 u'C

In [186]:
from collections import defaultdict

speakers10 = defaultdict(list)
for sentence in dialogue10:
    speakers10[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers10

defaultdict(list,
            {u'Addam Marbrand': [u'   ls it true about Stannis and Renly?',
              u'  Kevan Lannister'],
             u'All': [u'     The King in the North!',
              u'     The King in the North!'],
             u'Arya Stark': [u"   l'm not a boy!",
              u'   Arry.',
              u'     You want it?',
              u'   lt was a gift.',
              u'   Which are you?'],
             u'Bran Stark': [u"   You're afraid.",
              u"   You've lived beyond the Wall.",
              u"   That's my grandfather, Lord Rickard.",
              u'   Rickon!',
              u'   What are you doing down here?',
              u'   How many times have l told you?',
              u'   Saw him when?'],
             u'Catelyn Stark': [u'   Robb.',
              u'   Shh!',
              u'   My boy.',
              u'   l want to see him.',
              u'   Leave us.',
              u'   l will kill you tonight, Ser.',
              u"   That is wha

In [187]:
speakers10['Arya Stark']

[u"   l'm not a boy!",
 u'   Arry.',
 u'     You want it?',
 u'   lt was a gift.',
 u'   Which are you?']

In [188]:
episode_ten = pd.DataFrame.from_dict(speakers10, orient="index")
print episode_ten.shape

(39, 18)


In [189]:
#from numpy import nan
#episode_ten.fillna(value=str(0), inplace=True)

In [190]:
episode_ten.info()

<class 'pandas.core.frame.DataFrame'>
Index: 39 entries, Joffrey Baratheon to Galbart Glover
Data columns (total 18 columns):
0     39 non-null object
1     34 non-null object
2     28 non-null object
3     26 non-null object
4     22 non-null object
5     14 non-null object
6     13 non-null object
7     9 non-null object
8     8 non-null object
9     6 non-null object
10    5 non-null object
11    4 non-null object
12    4 non-null object
13    3 non-null object
14    3 non-null object
15    2 non-null object
16    1 non-null object
17    1 non-null object
dtypes: object(18)
memory usage: 5.8+ KB


In [191]:
episode_ten.head()

0   \
Joffrey Baratheon                                      Very amusing.   
Petyr Baelish         lt's hard for them to simper and bow withou...   
Lommy Greenhands                         He's got a sword, this one.   
Yoren                                     Keep your mouth shut, boy.   
Shae                  And your father said you couldn't take anyo...   

                                                                  1   \
Joffrey Baratheon     Tell me, which do you favor - your fingers ...   
Petyr Baelish         And what would you do, my friend, if you fo...   
Lommy Greenhands                         Maybe he's a little squire.   
Yoren                 You're not a smart boy, is that what you're...   
Shae                                                He knew my name?   

                                                                  2   \
Joffrey Baratheon                            Fingers or your tongue?   
Petyr Baelish         You must be one of the few men in the city ...   
Lommy Greenhands                                  Let's have a look.   
Yoren                                      You're Arry now, hear me?   
Shae                  He said, "Don't bring Shae with you to King...   

                                                                  3   \
Joffrey Baratheon                                              Good.   
Petyr Baelish                                      l picture a gash.   
Lommy Greenhands                                    Take it off him.   
Yoren                 You've a long way to travel, and in bad com...   
Shae                                          Are you ashamed of me?   

                                                                  4   \
Joffrey Baratheon     Ser llyn, who better than you to carry out ...   
Petyr Baelish         Must be strange for you, even after all the...   
Lommy Greenhands                                        Look at him!   
Yoren                             Come on, you sorry sons of whores!   
Shae                                                  I’m funny now?   

                                                                  5   \
Joffrey Baratheon                              l'm done for the day.   
Petyr Baelish         But you carry on whispering in one king's e...   
Lommy Greenhands                                                None   
Yoren                                                           None   
Shae                                                            None   

                                                          6   \
Joffrey Baratheon                       You look quite nice.   
Petyr Baelish         A useful talent, l'm sure you'd agree.   
Lommy Greenhands                                        None   
Yoren                                                   None   
Shae                                                    None   

                                      7                      8   \
Joffrey Baratheon            Your Grace.          Walk with me.   
Petyr Baelish         Playing our roles.     Long may he reign.   
Lommy Greenhands                    None                   None   
Yoren                               None                   None   
Shae                                None                   None   

                                                                  9   \
Joffrey Baratheon     And as soon as you've had your blood, l'll ...   
Petyr Baelish                                                   None   
Lommy Greenhands                                                None   
Yoren                                                           None   
Shae                                                            None   

                                             10         11        12  \
Joffrey Baratheon       This one's your father.     l was.     Well?   
Petyr Baelish                              None       None      None   
Lommy Greenhands               

In [192]:
test10 = episode_ten[0].apply(remove_stops)
test10

Joffrey Baratheon                                           amusing
Petyr Baelish                     lts hard simper bow without heads
Lommy Greenhands                                  hes got sword one
Yoren                                           keep mouth shut boy
Shae                  father said couldnt take anyone kings landing
Jonos Bracken                         cannot mean hold joffrey lord
Tyrion Lannister             stark boy appears less green wed hoped
Samwell Tarly                                       theyll put word
Grenn                                                       samwell
Pyp                                                         ls dead
Theon Greyjoy                                      l brother always
Stark Guard                                              lady stark
Tywin Lannister                                            one stay
Jon Snow                                                get way sam
Osha                                            

In [193]:
for column in episode_ten.columns:
    for x in range(len(episode_ten[column])):
        episode_ten[column][x] = remove_stops(episode_ten[column][x])

In [194]:
episode_ten.head()

0   \
Joffrey Baratheon                                        amusing   
Petyr Baelish                  lts hard simper bow without heads   
Lommy Greenhands                               hes got sword one   
Yoren                                        keep mouth shut boy   
Shae               father said couldnt take anyone kings landing   

                                                 1   \
Joffrey Baratheon         tell favor fingers tongue   
Petyr Baelish            would friend found sitting   
Lommy Greenhands            maybe hes little squire   
Yoren              youre smart boy youre trying say   
Shae                                      knew name   

                                                   2   \
Joffrey Baratheon                      fingers tongue   
Petyr Baelish              must one men city isnt man   
Lommy Greenhands                            lets look   
Yoren                                 youre arry hear   
Shae               said dont bring shae kings landing   

                                                  3   \
Joffrey Baratheon                               good   
Petyr Baelish                         l picture gash   
Lommy Greenhands                                take   
Yoren              youve long way travel bad company   
Shae                                         ashamed   

                                                                  4   \
Joffrey Baratheon                     ser llyn better carry sentence   
Petyr Baelish      must strange even years man another land despi...   
Lommy Greenhands                                                look   
Yoren                                         come sorry sons whores   
Shae                                                        im funny   

                                                    5   \
Joffrey Baratheon                          lm done day   
Petyr Baelish      carry whispering one kings ear next   
Lommy Greenhands                                  None   
Yoren                                             None   
Shae                                              None   

                                                 6              7   \
Joffrey Baratheon                   look quite nice          grace   
Petyr Baelish      useful talent lm sure youd agree  playing roles   
Lommy Greenhands                               None           None   
Yoren                                          None           None   
Shae                                           None           None   

                               8                             9            10  \
Joffrey Baratheon            walk  soon youve blood lll put son  ones father   
Petyr Baelish      long may reign                          None         None   
Lommy Greenhands             None                          None         None   
Yoren                        None                          None         None   
Shae                         None                          None         None   

                     11    12            13    14     15    16    17  
Joffrey Baratheon     l  well  long pleases  obey  lords  None  None  
Petyr Baelish      None  None          None  None   None  None  None  
Lommy Greenhands   None  None          None  None   None  None  None  
Yoren              None  None          None  None   None  None  None  
Shae               None  None          None  None   None  None  None

## Season One

In [195]:
episode_one = episode_one.reset_index()

In [196]:
episode_one_dict = {'Khal Drogo':'Khal Drogo', 
                  'Ned':'Eddard Stark', 
                  'Tyrion':'Tyrion Lannister', 
                  'Jaime':'Jaime Lannister', 
                  'Illyrio':'Illyrio', 
                  'Viserys':'Viserys Targaryen', 
                  'Robert':'Robert Baratheon', 
                  'Daenerys':'Daenerys Targaryen', 
                  'Ros':'Ros', 
                  'Septa Mordane':'Septa Mordane', 
                  'Jon':'Jon Snow', 
                  'Benjen':'Benjen Stark',
                  'Luwin':'Maester Luwin', 
                  'Theon':'Theon Greyjoy', 
                  'Jon/Robb':'Jon/Robb', 
                  'Cersei':'Cersei Baratheon', 
                  'The Hound':'Sandor Clegane', 
                  'Sansa':'Sansa Stark',
                  'Jorah':'Jorah Mormont', 
                  'Gared':'Gared', 
                  'Robb':'Robb Stark', 
                  'Will':'Will', 
                  'Cassel':'Rodrick Cassel', 
                  'Catelyn':'Catelyn Stark', 
                  'Arya':'Arya Stark',
                  'Bran':'Bran Stark', 
                  'Royce':'Royce'}

episode_one['index']=episode_one['index'].replace(episode_one_dict)

In [197]:
episode_one = episode_one.set_index('index')
episode_one.head()

0   \
index                                      
Khal Drogo                                 
Eddard Stark            one marksman ten   
Tyrion Lannister                     mmh   
Jaime Lannister   brother feel duty warn   
Illyrio                  greets dothraki   

                                                               1   \
index                                                               
Khal Drogo                                                          
Eddard Stark      name robert house baratheon first name jon bran   
Tyrion Lannister                                   hear something   
Jaime Lannister                                            cersei   
Illyrio                                         come forward dear   

                                                         2   \
index                                                         
Khal Drogo                                                    
Eddard Stark                      king andals first men jon   
Tyrion Lannister                                    brother   
Jaime Lannister   told king heads would skewered city gates   
Illyrio                                            ceremony   

                                                                 3   \
index                                                                 
Khal Drogo                                                     None   
Eddard Stark      lord seven kingdoms protector realm eddard hou...   
Tyrion Lannister                                  theres pretty one   
Jaime Lannister                                 thats honor without   
Illyrio                                                 trust grace   

                                                  4   \
index                                                  
Khal Drogo                                      None   
Eddard Stark      white walkers gone thousands years   
Tyrion Lannister                 hear hates nickname   
Jaime Lannister                             dont get   
Illyrio                                    wont long   

                                         5   \
index                                         
Khal Drogo                             None   
Eddard Stark               madman sees sees   
Tyrion Lannister                clever girl   
Jaime Lannister   hear might neighbors soon   
Illyrio                                soon   

                                                                 6   \
index                                                                 
Khal Drogo                                                     None   
Eddard Stark                                   mountain lions woods   
Tyrion Lannister                             gods gave one blessing   
Jaime Lannister   im sure well tournament celebrate new title ac...   
Illyrio                                      wouldnt ask khal drogo   

                                                              7   \
index                                                              
Khal Drogo                                                  None   
Eddard Stark                                     tough old beast   
Tyrion Lannister  explain meaning closed door whorehouse brother   
Jaime Lannister                                                    
Illyrio                          khal drogo promised crown shall   

                               8   \
index                               
Khal Drogo                   None   
Eddard Stark        im sorry bran   
Tyrion Lannister            jaime   
Jaime Lannister         well said   
Illyrio           omens favor war   

                                                                 9   \
index                                                                 
Khal Drogo                                                     None   
Eddard Stark                                                  train   
Tyrion Lannister                                         close 

In [198]:
print episode_one.shape
print episode_two.shape

(27, 33)
(27, 30)


In [199]:
episode_two.index

Index([u'Joffrey Baratheon', u'Cersei Baratheon', u'Robert Baratheon',
       u'Eddard Stark', u'Jaime Lannister', u'Jhiqui', u'Theon Greyjoy',
       u'Mycah', u'Irri', u'Arya Stark', u'Tyrion Lannister', u'Catelyn Stark',
       u'Soldier', u'Viserys Targaryen', u'Doreah', u'Assassin', u'Soldier 2',
       u'Soldier 1', u'Rodrick Cassel', u'Daenerys Targaryen',
       u'Jorah Mormont', u'Maester Luwin', u'Robb Stark',
       u'Myrcella Baratheon', u'Jory Cassel', u'Sandor Clegane', u'Jon Snow'],
      dtype='object')

In [200]:
season_one = episode_one.join(episode_two, rsuffix="_two", how='outer')
print season_one.shape

(38, 63)


In [201]:
season_one.head()

0                      1  \
Arya Stark                       arya  thats jaime lannister   
Assassin                          NaN                    NaN   
Benjen Stark                 dead yet             got bigger   
Bran Stark     true saw white walkers                  lying   
Catelyn Stark          gods grow fast        many times told   

                                            2              3  \
Arya Stark                               None           None   
Assassin                                  NaN            NaN   
Benjen Stark   well youre always welcome wall        jon jon   
Bran Stark                                 go  please father   
Catelyn Stark                    want promise      dyou know   

                                      4                            5  \
Arya Stark                         None                         None   
Assassin                            NaN                          NaN   
Benjen Stark   wall isnt going anywhere  dont understand youd giving   
Bran Stark                     saw king             hes coming right   
Catelyn Stark      always look feet lie                  wheres arya   

                              6                     7  \
Arya Stark                 None                  None   
Assassin                    NaN                   NaN   
Benjen Stark   might knew meant  feast like bear trap   
Bran Stark                                       come   
Catelyn Stark             grace                 queen   

                                         8                  9              10  \
Arya Stark                            None               None            None   
Assassin                               NaN                NaN             NaN   
Benjen Stark                        course  two still missing           maybe   
Bran Stark                             ten               None            None   
Catelyn Stark  stupidest prince ever lived               hush  hed leave home   

                        11                          12    13             14  \
Arya Stark            None                        None  None           None   
Assassin               NaN                         NaN   NaN            NaN   
Benjen Stark      robb boy                        None  None           None   
Bran Stark            None                        None  None           None   
Catelyn Stark  sansa sansa  im sure grim kings landing  hear  wont let take   

                                                           15  \
Arya Stark                                               None   
Assassin                                                  NaN   
Benjen Stark                                             None   
Bran Stark                                               None   
Catelyn Stark  ill say listen fat man taking husband anywhere   

                                    16          17                 18  \
Arya Stark                        None        None               None   
Assassin                           NaN         NaN                NaN   
Benjen Stark                      None        None               None   
Bran Stark                        None        None               None   
Catelyn Stark  stops eating time drink  sent eyrie  shes fled capital   

                                                              19  \
Arya Stark                                                  None   
Assassin                                                     NaN   
Benjen Stark                                                None   
Bran Stark                                                  None   
Catelyn Stark  lysas head would spike right wrong people foun...   

                               20                                     21  \
Arya Stark                   None                                   None   
Assassin                      NaN                                    NaN   
Benjen Stark                 None                            

In [202]:
season_one.index

Index([        u'Arya Stark',           u'Assassin',       u'Benjen Stark',
               u'Bran Stark',      u'Catelyn Stark',   u'Cersei Baratheon',
       u'Daenerys Targaryen',             u'Doreah',       u'Eddard Stark',
                    u'Gared',            u'Illyrio',               u'Irri',
          u'Jaime Lannister',             u'Jhiqui',  u'Joffrey Baratheon',
                 u'Jon Snow',           u'Jon/Robb',      u'Jorah Mormont',
              u'Jory Cassel',         u'Khal Drogo',      u'Maester Luwin',
                    u'Mycah', u'Myrcella Baratheon',         u'Robb Stark',
         u'Robert Baratheon',     u'Rodrick Cassel',                u'Ros',
                    u'Royce',     u'Sandor Clegane',        u'Sansa Stark',
            u'Septa Mordane',            u'Soldier',          u'Soldier 1',
                u'Soldier 2',      u'Theon Greyjoy',   u'Tyrion Lannister',
        u'Viserys Targaryen',               u'Will'],
      dtype='object')

In [203]:
episode_three.shape

(37, 37)

In [204]:
episode_three.index

Index([u'Joffrey Baratheon', u'Benjen Stark', u'Petyr Baelish',
       u'Cersei Baratheon', u'Robert Baratheon', u'Khal Drogo', u'Rast',
       u'Yoren', u'Maester Aemon', u'Tyrion Lannister', u'Pyp',
       u'Eddard Stark', u'Bran Stark', u'Irri', u'Arya Stark',
       u'Jaime Lannister', u'Septa Mordane', u'Old Nan', u'Jeor Mormont',
       u'Alliser Thorne', u'Catelyn Stark', u'Varys', u'Viserys Targaryen',
       u'Sansa Stark', u'Rakharo', u'Barristan Selmy', u'Rodrick Cassel',
       u'Daenerys Targaryen', u'Lancel Lannister', u'Jorah Mormont', u'Grenn',
       u'Guard', u'Robb Stark', u'Renly Baratheon', u'Syrio Forel',
       u'Jory Cassel', u'Jon Snow'],
      dtype='object')

In [205]:
season_one = season_one.join(episode_three, rsuffix="_three", how='outer')
season_one.shape

(54, 100)

In [206]:
season_one.index

Index([        u'Arya Stark',           u'Assassin',       u'Benjen Stark',
               u'Bran Stark',      u'Catelyn Stark',   u'Cersei Baratheon',
       u'Daenerys Targaryen',             u'Doreah',       u'Eddard Stark',
                    u'Gared',            u'Illyrio',               u'Irri',
          u'Jaime Lannister',             u'Jhiqui',  u'Joffrey Baratheon',
                 u'Jon Snow',           u'Jon/Robb',      u'Jorah Mormont',
              u'Jory Cassel',         u'Khal Drogo',      u'Maester Luwin',
                    u'Mycah', u'Myrcella Baratheon',         u'Robb Stark',
         u'Robert Baratheon',     u'Rodrick Cassel',                u'Ros',
                    u'Royce',     u'Sandor Clegane',        u'Sansa Stark',
            u'Septa Mordane',            u'Soldier',          u'Soldier 1',
                u'Soldier 2',      u'Theon Greyjoy',   u'Tyrion Lannister',
        u'Viserys Targaryen',               u'Will',      u'Petyr Baelish',
            

In [207]:
episode_four.shape

(36, 45)

In [208]:
episode_four.index

Index([u'Petyr Baelish', u'Yoren', u'Cersei Baratheon', u'Robert Baratheon',
       u'Rast', u'Janos Slynt', u'Tyrion Lannister', u'Samwell Tarly', u'Pyp',
       u'Theon Greyjoy', u'Eddard Stark', u'Bran Stark', u'Irri',
       u'Arya Stark', u'Jaime Lannister', u'Septa Mordane', u'Tobho Mott',
       u'Gendry', u'Marillion', u'Alliser Thorne', u'Catelyn Stark', u'Varys',
       u'Bronn', u'Viserys Targaryen', u'Doreah', u'Sansa Stark',
       u'Rodrick Cassel', u'Daenerys Targaryen', u'Jorah Mormont', u'Grenn',
       u'Maester Luwin', u'Robb Stark', u'Renly Baratheon', u'Masha Heddle',
       u'Jory Cassel', u'Jon Snow'],
      dtype='object')

In [209]:
season_one = season_one.join(episode_four, rsuffix="_four", how='outer')
season_one.shape

(61, 145)

In [210]:
season_one.index

Index([        u'Arya Stark',           u'Assassin',       u'Benjen Stark',
               u'Bran Stark',      u'Catelyn Stark',   u'Cersei Baratheon',
       u'Daenerys Targaryen',             u'Doreah',       u'Eddard Stark',
                    u'Gared',            u'Illyrio',               u'Irri',
          u'Jaime Lannister',             u'Jhiqui',  u'Joffrey Baratheon',
                 u'Jon Snow',           u'Jon/Robb',      u'Jorah Mormont',
              u'Jory Cassel',         u'Khal Drogo',      u'Maester Luwin',
                    u'Mycah', u'Myrcella Baratheon',         u'Robb Stark',
         u'Robert Baratheon',     u'Rodrick Cassel',                u'Ros',
                    u'Royce',     u'Sandor Clegane',        u'Sansa Stark',
            u'Septa Mordane',            u'Soldier',          u'Soldier 1',
                u'Soldier 2',      u'Theon Greyjoy',   u'Tyrion Lannister',
        u'Viserys Targaryen',               u'Will',      u'Petyr Baelish',
            

In [211]:
episode_five.index

Index([u'Petyr Baelish', u'Cersei Baratheon', u'Robert Baratheon',
       u'Illyrio Mopatis', u'Robin Arryn', u'Yoren', u'Mord',
       u'Tyrion Lannister', u'Theon Greyjoy', u'Vardis Egen', u'Mhaegen',
       u'Eddard Stark', u'Bran Stark', u'Lysa Arryn', u'Arya Stark',
       u'Jaime Lannister', u'Catelyn Stark', u'Marillion', u'Bronn',
       u'Steward', u'Rodrik Cassel', u'Varys', u'Sansa Stark',
       u'Barristan Selmy', u'Lancel Lannister', u'Loras Tyrell',
       u'Maester Luwin', u'Renly Baratheon', u'Guard 1', u'Guard 2', u'Ros',
       u'Jory Cassel'],
      dtype='object')

In [212]:
episode_five.shape

(32, 61)

In [213]:
season_one = season_one.join(episode_five, rsuffix="_five", how='outer')
season_one.shape

(72, 206)

In [214]:
episode_six.index

Index([u'Joffrey Baratheon', u'Petyr Baelish', u'Cersei Baratheon',
       u'Robert Baratheon', u'Khal Drogo', u'Robin Arryn', u'Sansa Stark',
       u'Eddard Stark', u'Mord', u'Tyrion Lannister', u'Wildling',
       u'Theon Greyjoy', u'Ser Vardis', u'Osha', u'Bran Stark', u'Irri',
       u'Lysa Arryn', u'Arya Stark', u'Man', u'Mordane', u'Catelyn Stark',
       u'Viserys Targaryen', u'Knight 5', u'Knight 4', u'Knight 3',
       u'Knight 2', u'Knight 1', u'Barristan Selmy', u'Ros',
       u'Daenerys Targaryen', u'Jorah Mormont', u'Beric Dondarrion',
       u'Robb Stark', u'Renly Baratheon', u'Wildling 2', u'Syrio Forel'],
      dtype='object')

In [215]:
episode_six.shape

(36, 22)

In [216]:
season_one = season_one.join(episode_six, rsuffix="_six", how='outer')
season_one.shape

(84, 228)

In [217]:
episode_seven.index

Index([u'Barristan Selmy', u'Petyr Baelish', u'Samwell Tarly', u'Ned Stark',
       u'Wine Merchant', u'Theon Greyjoy', u'Renly Baratheon',
       u'Tywin Lannister', u'Rakharo', u'Cersei Lannister', u'Osha',
       u'Khal Drogo', u'Jorah Mormont', u'Maester Luwin',
       u'Daenerys Stormborn', u'Doreah', u'Ros', u'Lord Varys',
       u'Robert Baratheon', u'Jon Snow', u'Jaime Lannister'],
      dtype='object')

In [218]:
episode_seven = episode_seven.reset_index()

In [219]:
episode_seven_dict = {'Barristan Selmy':'Barristan Selmy',
                      'Petyr Baelish':'Petyr Baelish',
                      'Samwell Tarly':'Samwell Tarly',
                      'Ned Stark':'Eddard Stark',
                      'Wine Merchant':'Wine Merchant',
                      'Theon Greyjoy':'Theon Greyjoy',
                      'Renly Baratheon':'Renly Baratheon',
                      'Tywin Lannister':'Tywin Lannister',
                      'Rakharo':'Rakharo',
                      'Cersei Lannister':'Cersei Baratheon',
                      'Osha':'Osha',
                      'Khal Drogo':'Khal Drogo',
                      'Jorah Mormont':'Jorah Mormont',
                      'Maester Luwin':'Maester Luwin',
                      'Daenerys Stormborn':'Daenerys Targaryen',
                      'Doreah':'Doreah',
                      'Ros':'Ros',
                      'Lord Varys':'Varys',
                      'Robert Baratheon':'Robert Baratheon',
                      'Jon Snow':'Jon Snow',
                      'Jaime Lannister':'Jaime Lannister'}

episode_seven['index'] = episode_seven['index'].replace(episode_seven_dict)

In [220]:
episode_seven = episode_seven.set_index('index')
episode_seven.head()

0   \
index                                 
Barristan Selmy        reeling wine   
Petyr Baelish                         
Samwell Tarly            miss girls   
Eddard Stark         ive worse lady   
Wine Merchant    virzetha gizikhven   

                                                                1   \
index                                                                
Barristan Selmy                                  squire kings skin   
Petyr Baelish                                     lets start shall   
Samwell Tarly    one blast ranger returning two wildlings three...   
Eddard Stark                             know truth jon arryn died   
Wine Merchant                                   daenerys stormborn   

                                2              3        4   \
index                                                        
Barristan Selmy               None           None     None   
Petyr Baelish    im saving another  stupid saying   really   
Samwell Tarly                 None           None     None   
Eddard Stark                  done  brother lover  son saw   
Wine Merchant        lady westeros       princess            

                                  5                                        6   \
index                                                                           
Barristan Selmy                 None                                     None   
Petyr Baelish             many years                                       oh   
Samwell Tarly                   None                                     None   
Eddard Stark                   heart                                   jaimes   
Wine Merchant    honorthe honor mine  know many homeland pray return princess   

                                 7   \
index                                 
Barristan Selmy                None   
Petyr Baelish    oh everything dear   
Samwell Tarly                  None   
Eddard Stark     youve always hated   
Wine Merchant         wine khaleesi   

                                                                8   \
index                                                                
Barristan Selmy                                               None   
Petyr Baelish                                          stannis war   
Samwell Tarly                                                 None   
Eddard Stark                      king returns hunt ill tell truth   
Wine Merchant    would crime drink wine rich without least givi...   

                                                    9            10    11  \
index                                                                       
Barristan Selmy                                   None         None  None   
Petyr Baelish                                     call         look  None   
Samwell Tarly                                     None         None  None   
Eddard Stark     ive made many mistakes life wasnt one  damned fool         
Wine Merchant                        princess commands   sweet isnt         

                                              12               13  \
index                                                               
Barristan Selmy                             None             None   
Petyr Baelish                               None             None   
Samwell Tarly                               None             None   
Eddard Stark     ill ill everything honor memory  give milk poppy   
Wine Merchant                               None             None   

                                  14      15  \
index                                          
Barristan Selmy                 None    None   
Petyr Baelish                   None    None   
Samwell Tarly                   None    None   
Eddard Stark     man could protected  squire   
Wine Merchant                   None    None   

                                                               16    17  \
index                                                           

In [221]:
episode_seven.shape

(21, 20)

In [222]:
season_one = season_one.join(episode_seven, rsuffix="_seven", how='outer')
season_one.shape

(86, 248)

In [223]:
season_one.index

Index([        u'Arya Stark',           u'Assassin',       u'Benjen Stark',
               u'Bran Stark',      u'Catelyn Stark',   u'Cersei Baratheon',
       u'Daenerys Targaryen',             u'Doreah',       u'Eddard Stark',
                    u'Gared',            u'Illyrio',               u'Irri',
          u'Jaime Lannister',             u'Jhiqui',  u'Joffrey Baratheon',
                 u'Jon Snow',           u'Jon/Robb',      u'Jorah Mormont',
              u'Jory Cassel',         u'Khal Drogo',      u'Maester Luwin',
                    u'Mycah', u'Myrcella Baratheon',         u'Robb Stark',
         u'Robert Baratheon',     u'Rodrick Cassel',                u'Ros',
                    u'Royce',     u'Sandor Clegane',        u'Sansa Stark',
            u'Septa Mordane',            u'Soldier',          u'Soldier 1',
                u'Soldier 2',      u'Theon Greyjoy',   u'Tyrion Lannister',
        u'Viserys Targaryen',               u'Will',      u'Petyr Baelish',
            

In [224]:
episode_eight.index

Index([u'King Joffrey', u'Petyr Baelish', u'Tyrion Lannister',
       u'Samwell Tarly', u'Sandor Clegane', u'Tywin Lannister', u'Arya Stark',
       u'Septa Mordane', u'Othell Yarwyck', u'Jeor Mormont', u'Ned Stark',
       u'Stark guard', u'Catelyn Stark', u'Meryn Trant', u'Ser Alliser',
       u'Sansa Stark', u'Shagga', u'Lord Varys', u'Barristan Selmy',
       u'Stable Boy', u'Lannister scout', u'Greatjon Umber',
       u'Cersei Lannister', u'Robb Stark', u'Kevan Lannister', u'Syrio Forel',
       u'Theon Greyjoy', u'Jon Snow'],
      dtype='object')

In [225]:
episode_eight = episode_eight.reset_index()

In [226]:
episode_eight_dict = {'King Joffrey':'Joffrey Baratheon',
                      'Petyr Baelish':'Petyr Baelish',
                      'Tyrion Lannister':'Tyrion Lannister',
                      'Samwell Tarly':'Samwell Tarly',
                      'Sandor Clegane':'Sandor Clegane',
                      'Tywin Lannister':'Tywin Lannister',
                      'Arya Stark':'Arya Stark',
                      'Stark guard':'Stark Guard',
                      'Catelyn Stark':'Catelyn Stark',
                      'Meryn Trant':'Meryn Trant',
                      'Ser Alliser':'Alliser Thorne',
                      'Stable Boy':'Stable Boy',
                      'Lannister scout':'Lannister Scout',
                      'Greatjon Umber':'Greatjon Umber',
                      'Cersei Lannister':'Cersei Baratheon',
                      'Robb Stark':'Robb Stark',
                      'Kevan Lannister':'Kevan Lannister',
                      'Syrio Forel':'Syrio Forel',
                      'Theon Greyjoy':'Theon Greyjoy',
                      'Jon Snow':'Jon Snow'}

episode_eight['index'] = episode_eight['index'].replace(episode_eight_dict)

In [227]:
episode_eight = episode_eight.set_index('index')
episode_eight.head()

0                        1   \
index                                                             
Joffrey Baratheon       let father die        come forward lady   
Petyr Baelish      girl innocent grace  naked knight apparently   
Tyrion Lannister                 uncle         sorry disappoint   
Samwell Tarly                    smell                     none   
Sandor Clegane              think sent                     None   

                                                                  2   \
index                                                                  
Joffrey Baratheon                                    said wasnt king   
Petyr Baelish                                     deny fathers crime   
Tyrion Lannister   may present lord father tywin son tytos house ...   
Samwell Tarly                                                   None   
Sandor Clegane                                                  None   

                                  3                  4   \
index                                                     
Joffrey Baratheon      anything else  sweet words moved   
Petyr Baelish                   None               None   
Tyrion Lannister   differences jaime             starks   
Samwell Tarly                   None               None   
Sandor Clegane                  None               None   

                                                                  5   \
index                                                                  
Joffrey Baratheon                                               None   
Petyr Baelish                                                   None   
Tyrion Lannister   sweet sister persuade king imprison dear frien...   
Samwell Tarly                                                   None   
Sandor Clegane                                                  None   

                                  6      7     8     9     10    11    12  \
index                                                                       
Joffrey Baratheon               None   None  None  None  None  None  None   
Petyr Baelish                   None   None  None  None  None  None  None   
Tyrion Lannister   sister rules mean  maybe  None  None  None  None  None   
Samwell Tarly                   None   None  None  None  None  None  None   
Sandor Clegane                  None   None  None  None  None  None  None   

                     13    14    15    16  
index                                      
Joffrey Baratheon  None  None  None  None  
Petyr Baelish      None  None  None  None  
Tyrion Lannister   None  None  None  None  
Samwell Tarly      None  None  None  None  
Sandor Clegane     None  None  None  None

In [228]:
episode_eight.shape

(28, 17)

In [229]:
season_one.shape

(86, 248)

In [230]:
season_one = season_one.join(episode_eight, rsuffix="_eight", how='outer')
season_one.shape

(96, 265)

In [231]:
season_one.index

Index([        u'Arya Stark',           u'Assassin',       u'Benjen Stark',
               u'Bran Stark',      u'Catelyn Stark',   u'Cersei Baratheon',
       u'Daenerys Targaryen',             u'Doreah',       u'Eddard Stark',
                    u'Gared',            u'Illyrio',               u'Irri',
          u'Jaime Lannister',             u'Jhiqui',  u'Joffrey Baratheon',
                 u'Jon Snow',           u'Jon/Robb',      u'Jorah Mormont',
              u'Jory Cassel',         u'Khal Drogo',      u'Maester Luwin',
                    u'Mycah', u'Myrcella Baratheon',         u'Robb Stark',
         u'Robert Baratheon',     u'Rodrick Cassel',                u'Ros',
                    u'Royce',     u'Sandor Clegane',        u'Sansa Stark',
            u'Septa Mordane',            u'Soldier',          u'Soldier 1',
                u'Soldier 2',      u'Theon Greyjoy',   u'Tyrion Lannister',
        u'Viserys Targaryen',               u'Will',      u'Petyr Baelish',
            

In [232]:
episode_nine.shape

(39, 62)

In [233]:
season_one = season_one.join(episode_nine, rsuffix="_nine", how='outer')
season_one.shape

(107, 327)

In [234]:
season_one.index

Index([        u'Arya Stark',           u'Assassin',       u'Benjen Stark',
               u'Bran Stark',      u'Catelyn Stark',   u'Cersei Baratheon',
       u'Daenerys Targaryen',             u'Doreah',       u'Eddard Stark',
                    u'Gared',
       ...
                     u'Shae',       u'Stevron Frey',              u'Qotho',
              u'Walder Frey',         u'Prostitute',    u'Stark bannermen',
             u'Ryger Rivers',                u'All',           u'Everyone',
            u'Street Urchin'],
      dtype='object', length=107)

In [235]:
episode_ten.index

Index([u'Joffrey Baratheon', u'Petyr Baelish', u'Lommy Greenhands', u'Yoren',
       u'Shae', u'Jonos Bracken', u'Tyrion Lannister', u'Samwell Tarly',
       u'Grenn', u'Pyp', u'Theon Greyjoy', u'Stark Guard', u'Tywin Lannister',
       u'Jon Snow', u'Osha', u'Bran Stark', u'Rickon Stark', u'Arya Stark',
       u'Jaime Lannister', u'Jeor Mormont', u'Gendry', u'Catelyn Stark',
       u'Marillion', u'Varys', u'Hot Pie', u'Sansa Stark', u'Leo Lefford',
       u'All', u'Daenerys Targaryen', u'Jorah Mormont', u'Greatjon Umber',
       u'Cersei Lannister', u'Robb Stark', u'Rickard Karstark',
       u'Kevan Lannister', u'Addam Marbrand', u'Ros', u'Sandor Clegane',
       u'Galbart Glover'],
      dtype='object')

In [236]:
episode_ten = episode_ten.reset_index()

In [237]:
episode_ten_dict = {'Joffrey Baratheon':'Joffrey Baratheon',
                    'Petyr Baelish':'Petyr Baelish',
                    'Lommy Greenhands':'Lommy Greenhands',
                    'Yoren':'Yoren',
                    'Shae':'Shae',
                    'Jonos Bracken':'Jonos Bracken',
                    'Tyrion Lannister':'Tyrion Lannister',
                    'Samwell Tarly':'Samwell Tarly',
                    'Grenn':'Grenn',
                    'Pyp':'Pyp',
                    'Theon Greyjoy':'Theon Greyjoy',
                    'Stark Guard':'Stark Guard',
                    'Tywin Lannister':'Tywin Lannister',
                    'Jon Snow':'Jon Snow',
                    'Osha':'Osha',
                    'Bran Stark':'Bran Stark',
                    'Rickon Stark':'Rickon Stark',
                    'Arya Stark':'Arya Stark',
                    'Jaime Lannister':'Jaime Lannister',
                    'Jeor Mormont':'Jeor Mormont',
                    'Gendry':'Gendry',
                    'Catelyn Stark':'Catelyn Stark',
                    'Marillion':'Marillion',
                    'Varys':'Varys',
                    'Hot Pie':'Hot Pie',
                    'Sansa Stark':'Sansa Stark',
                    'Leo Lefford':'Leo Lefford',
                    'All':'All', 
                    'Daenerys Targaryen':'Daenerys Targaryen', 
                    'Jorah Mormont':'Jorah Mormont', 
                    'Greatjon Umber':'Greatjon Umber',
                    'Cersei Lannister':'Cersei Baratheon', 
                    'Robb Stark':'Robb Stark', 
                    'Rickard Karstark':'Rickard Karstark',
                    'Kevan Lannister':'Kevan Lannister', 
                    'Addam Marbrand':'Addam Marbrand', 
                    'Ros':'Ros', 
                    'Sandor Clegane':'Sandor Clegane',
                    'Galbart Glover':'Galbart Glover'}

episode_ten['index'] = episode_ten['index'].replace(episode_ten_dict)

In [238]:
episode_ten = episode_ten.set_index('index')
episode_ten.head()

0   \
index                                                              
Joffrey Baratheon                                        amusing   
Petyr Baelish                  lts hard simper bow without heads   
Lommy Greenhands                               hes got sword one   
Yoren                                        keep mouth shut boy   
Shae               father said couldnt take anyone kings landing   

                                                 1   \
index                                                 
Joffrey Baratheon         tell favor fingers tongue   
Petyr Baelish            would friend found sitting   
Lommy Greenhands            maybe hes little squire   
Yoren              youre smart boy youre trying say   
Shae                                      knew name   

                                                   2   \
index                                                   
Joffrey Baratheon                      fingers tongue   
Petyr Baelish              must one men city isnt man   
Lommy Greenhands                            lets look   
Yoren                                 youre arry hear   
Shae               said dont bring shae kings landing   

                                                  3   \
index                                                  
Joffrey Baratheon                               good   
Petyr Baelish                         l picture gash   
Lommy Greenhands                                take   
Yoren              youve long way travel bad company   
Shae                                         ashamed   

                                                                  4   \
index                                                                  
Joffrey Baratheon                     ser llyn better carry sentence   
Petyr Baelish      must strange even years man another land despi...   
Lommy Greenhands                                                look   
Yoren                                         come sorry sons whores   
Shae                                                        im funny   

                                                    5   \
index                                                    
Joffrey Baratheon                          lm done day   
Petyr Baelish      carry whispering one kings ear next   
Lommy Greenhands                                  None   
Yoren                                             None   
Shae                                              None   

                                                 6              7   \
index                                                                
Joffrey Baratheon                   look quite nice          grace   
Petyr Baelish      useful talent lm sure youd agree  playing roles   
Lommy Greenhands                               None           None   
Yoren                                          None           None   
Shae                                           None           None   

                               8                             9            10  \
index                                                                          
Joffrey Baratheon            walk  soon youve blood lll put son  ones father   
Petyr Baelish      long may reign                          None         None   
Lommy Greenhands             None                          None         None   
Yoren                        None                          None         None   
Shae                         None                          None         None   

                     11    12            13    14     15    16    17  
index                                                                 
Joffrey Baratheon     l  well  long pleases  obey  lords  None  None  
Petyr Baelish      None  None          None  None   None  None  None  
Lommy Greenhands   None  None          None  None   None  None  None  
Yoren              None  None          None  None   None  None  None  
Shae            

In [239]:
episode_ten.shape

(39, 18)

In [240]:
season_one = season_one.join(episode_ten, rsuffix="_ten", how='outer')
season_one.shape

(115, 345)

In [241]:
season_one.index

Index([        u'Arya Stark',           u'Assassin',       u'Benjen Stark',
               u'Bran Stark',      u'Catelyn Stark',   u'Cersei Baratheon',
       u'Daenerys Targaryen',             u'Doreah',       u'Eddard Stark',
                    u'Gared',
       ...
                 u'Everyone',      u'Street Urchin',   u'Lommy Greenhands',
            u'Jonos Bracken',       u'Rickon Stark',            u'Hot Pie',
              u'Leo Lefford',   u'Rickard Karstark',     u'Addam Marbrand',
           u'Galbart Glover'],
      dtype='object', length=115)

In [242]:
from numpy import nan
season_one.fillna(value=str(0), inplace=True)

In [243]:
season_one.head(115)

0  \
Arya Stark                                                  arya   
Assassin                                                       0   
Benjen Stark                                            dead yet   
Bran Stark                                true saw white walkers   
Catelyn Stark                                     gods grow fast   
Cersei Baratheon                            never worry anything   
Daenerys Targaryen  weve guests year hes never asked us anything   
Doreah                                                         0   
Eddard Stark                                    one marksman ten   
Gared                                             head back wall   
Illyrio                                          greets dothraki   
Irri                                                           0   
Jaime Lannister                           brother feel duty warn   
Jhiqui                                                         0   
Joffrey Baratheon                                              0   
Jon Snow                                    dont think much bran   
Jon/Robb                                       quick bran faster   
Jorah Mormont                            small gift new khaleesi   
Jory Cassel                                                    0   
Khal Drogo                                                         
Maester Luwin                                   pardon lord lady   
Mycah                                                          0   
Myrcella Baratheon                                             0   
Robb Stark                                         relax bow arm   
Robert Baratheon                                             cat   
Rodrick Cassel                                       dont belong   
Ros                                        hear kings winterfell   
Royce                                dont think hell ask us died   
Sandor Clegane                                   rough night imp   
Sansa Stark                                                thank   
Septa Mordane              love detail youve managed get corners   
Soldier                                                        0   
Soldier 1                                                      0   
Soldier 2                                                      0   
Theon Greyjoy                                      mountain lion   
Tyrion Lannister                                             mmh   
Viserys Targaryen                                       daenerys   
Will                                                waymar royce   
Petyr Baelish                                                  0   
Rast                                                           0   
Yoren                                                          0   
Maester Aemon                                                  0   
Pyp                                                            0   
Old Nan                                                        0   
Jeor Mormont                                                   0   
Alliser Thorne                                                 0   
Varys                                                          0   
Rakharo                                                        0   
Barristan Selmy                                                0   
Lancel Lannister                                               0   
Grenn                                                          0   
Guard                                                          0   
Renly Baratheon                                                0   
Syrio Forel                                                    0   
Janos Slynt                                                    0   
Samwell Tarly                                                  0   
Tobho Mott                                                     0   
Gendry                                                         0   
Marillion                                          

In [244]:
season_one.info()

<class 'pandas.core.frame.DataFrame'>
Index: 115 entries, Arya Stark to Galbart Glover
Columns: 345 entries, 0 to 17
dtypes: object(345)
memory usage: 310.9+ KB


In [351]:
season_one.to_pickle('/Users/zoemarkovits/Metis/project_five_got/PKLs/season_one.pkl')

## Character Breakdown

### Arya Stark

In [245]:
Arya = season_one.loc['Arya Stark']
print Arya

0                               arya
1              thats jaime lannister
2                                  0
3                                  0
4                                  0
5                                  0
6                                  0
7                                  0
8                                  0
9                                  0
10                                 0
11                                 0
12                                 0
13                                 0
14                                 0
15                                 0
16                                 0
17                                 0
18                                 0
19                                 0
20                                 0
21                                 0
22                                 0
23                                 0
24                                 0
25                                 0
26                                 0
2

In [246]:
Arya_Text = Arya.values.tolist()
Arya_Text

[u'arya',
 u'thats jaime lannister',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'watch',
 u'shut',
 u'think',
 u'know end use',
 u'sansa keep sewing needles',
 '',
 u'stop',
 u'nymeria',
 u'youve got go',
 u'go',
 '',
 u'thats true',
 u'thats happened',
 u'liar',
 u'liar',
 u'liar liar liar',
 u'lady wasnt',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'im practicing',
 u'prince',
 u'hound whatever prince tells',
 u'youre liar',
 u'go away',
 u'mine',
 u'wasnt playing',
 u'called needle',
 u'stick em pointy end',
 u'trying learn',
 u'hate',
 '',
 u'let marry someone like',
 u'winter coming',
 u'dont hate',
 u'keep',
 '',
 u'heavy',
 u'drop',
 u'im girl',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'syrio says every hurt lesson every lesson makes bett

In [247]:
Arya_Words = []

for word in Arya_Text:
    if len(word)>=1:
        if word != '0':
            Arya_Words.append(word)
        
Arya_Words        

[u'arya',
 u'thats jaime lannister',
 u'watch',
 u'shut',
 u'think',
 u'know end use',
 u'sansa keep sewing needles',
 u'stop',
 u'nymeria',
 u'youve got go',
 u'go',
 u'thats true',
 u'thats happened',
 u'liar',
 u'liar',
 u'liar liar liar',
 u'lady wasnt',
 u'im practicing',
 u'prince',
 u'hound whatever prince tells',
 u'youre liar',
 u'go away',
 u'mine',
 u'wasnt playing',
 u'called needle',
 u'stick em pointy end',
 u'trying learn',
 u'hate',
 u'let marry someone like',
 u'winter coming',
 u'dont hate',
 u'keep',
 u'heavy',
 u'drop',
 u'im girl',
 u'syrio says every hurt lesson every lesson makes better',
 u'brans awake come live us',
 u'wants knight kings guard',
 u'lord holdfast',
 u'call littlefinger',
 u'im beggar',
 u'want see father',
 u'father hand king',
 u'said going kill',
 u'didnt see think one fat',
 u'im lying',
 u'im girl',
 u'many guards father',
 u'wouldnt let anyone kill would',
 u'killed jory',
 u'yes syrio forel',
 u'dont like dolls k syrio forel',
 u'dying leg

In [248]:
Arya_Words_String = ' '.join(Arya_Words)
Arya_Words_String

u'arya thats jaime lannister watch shut think know end use sansa keep sewing needles stop nymeria youve got go go thats true thats happened liar liar liar liar liar lady wasnt im practicing prince hound whatever prince tells youre liar go away mine wasnt playing called needle stick em pointy end trying learn hate let marry someone like winter coming dont hate keep heavy drop im girl syrio says every hurt lesson every lesson makes better brans awake come live us wants knight kings guard lord holdfast call littlefinger im beggar want see father father hand king said going kill didnt see think one fat im lying im girl many guards father wouldnt let anyone kill would killed jory yes syrio forel dont like dolls k syrio forel dying leg cant cant take syrio back us seven hells lions sigil idiot come said right went left cause lied father wouldnt send dont go dont want come today today needle want leave stay away nice fat pigeon stale ones yesterday hey wheres everyone going let go lm boy arry

In [249]:
Arya_String_Length = len(Arya_Words_String)
Arya_String_Length

1011

In [250]:
Arya_Sentiment = TextBlob(Arya_Words_String).sentiment
Arya_Sentiment

Sentiment(polarity=-0.048528138528138524, subjectivity=0.49238095238095236)

### Catelyn Stark

In [251]:
Catelyn = season_one.loc['Catelyn Stark']
print Catelyn

0                                             gods grow fast
1                                            many times told
2                                               want promise
3                                                  dyou know
4                                       always look feet lie
5                                                wheres arya
6                                                      grace
7                                                      queen
8                                stupidest prince ever lived
9                                                       hush
10                                            hed leave home
11                                               sansa sansa
12                                im sure grim kings landing
13                                                      hear
14                                             wont let take
15            ill say listen fat man taking husband anywhere
16                      

In [252]:
Catelyn_Text = Catelyn.values.tolist()
Catelyn_Text

[u'gods grow fast',
 u'many times told',
 u'want promise',
 u'dyou know',
 u'always look feet lie',
 u'wheres arya',
 u'grace',
 u'queen',
 u'stupidest prince ever lived',
 u'hush',
 u'hed leave home',
 u'sansa sansa',
 u'im sure grim kings landing',
 u'hear',
 u'wont let take',
 u'ill say listen fat man taking husband anywhere',
 u'stops eating time drink',
 u'sent eyrie',
 u'shes fled capital',
 u'lysas head would spike right wrong people found letter',
 u'murdered last hand',
 u'spent half life fighting roberts wars',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'would dressed grace',
 u'never knew',
 u'grateful cersei baratheon',
 u'youve said',
 u'want leave',
 u'years ago rode robert baratheon',
 u'thats men always say honor calls',
 u'talk poole',
 u'take care',
 u'hes wrong',
 '',
 u'someone tried kill twice',
 u'dont know',
 u'dont trust raven carry words',
 '',
 u'must',
 u'large party attracts unwanted attention',
 u'prayed seven month',
 '0',
 '0',
 '

In [253]:
Catelyn_Words = []

for word in Catelyn_Text:
    if len(word)>=1:
        if word != '0':
            Catelyn_Words.append(word)
        
Catelyn_Words        

[u'gods grow fast',
 u'many times told',
 u'want promise',
 u'dyou know',
 u'always look feet lie',
 u'wheres arya',
 u'grace',
 u'queen',
 u'stupidest prince ever lived',
 u'hush',
 u'hed leave home',
 u'sansa sansa',
 u'im sure grim kings landing',
 u'hear',
 u'wont let take',
 u'ill say listen fat man taking husband anywhere',
 u'stops eating time drink',
 u'sent eyrie',
 u'shes fled capital',
 u'lysas head would spike right wrong people found letter',
 u'murdered last hand',
 u'spent half life fighting roberts wars',
 u'would dressed grace',
 u'never knew',
 u'grateful cersei baratheon',
 u'youve said',
 u'want leave',
 u'years ago rode robert baratheon',
 u'thats men always say honor calls',
 u'talk poole',
 u'take care',
 u'hes wrong',
 u'someone tried kill twice',
 u'dont know',
 u'dont trust raven carry words',
 u'must',
 u'large party attracts unwanted attention',
 u'prayed seven month',
 u'nine years since ive set foot capital',
 u'would',
 u'instructed',
 u'dare bring',
 u'k

In [254]:
Catelyn_Words_String = ' '.join(Catelyn_Words)
Catelyn_Words_String

u'gods grow fast many times told want promise dyou know always look feet lie wheres arya grace queen stupidest prince ever lived hush hed leave home sansa sansa im sure grim kings landing hear wont let take ill say listen fat man taking husband anywhere stops eating time drink sent eyrie shes fled capital lysas head would spike right wrong people found letter murdered last hand spent half life fighting roberts wars would dressed grace never knew grateful cersei baratheon youve said want leave years ago rode robert baratheon thats men always say honor calls talk poole take care hes wrong someone tried kill twice dont know dont trust raven carry words must large party attracts unwanted attention prayed seven month nine years since ive set foot capital would instructed dare bring know coming kings landing lord varys know coming know whose dagger ned proof petyr promised help us find truth wont forget moment temper still catelyn tully last time stayed lady whent true honest friend father l

In [255]:
Catelyn_String_Length = len(Catelyn_Words_String)
Catelyn_String_Length

2202

In [256]:
TextBlob(Catelyn_Words_String).sentiment

Sentiment(polarity=0.08284313725490197, subjectivity=0.5116946778711486)

### Cersei Lannister Baratheon

In [257]:
Cersei = season_one.loc['Cersei Baratheon']
print Cersei

0                     never worry anything
1                                  husband
2                      scene changes crypt
3                                      yes
4                        hello little dove
5                               youre tall
6                                 bled yet
7                                    dress
8                                   talent
9                    daughter well capital
10                                    stop
11                                  saw us
12                                  saw us
13                                       0
14                                       0
15                                       0
16                                       0
17                                       0
18                                       0
19                                       0
20                                       0
21                                       0
22                                       0
23         

In [258]:
Cersei_Text = Cersei.values.tolist()
Cersei_Text

[u'never worry anything',
 u'husband',
 u'scene changes crypt',
 u'yes',
 u'hello little dove',
 u'youre tall',
 u'bled yet',
 u'dress',
 u'talent',
 u'daughter well capital',
 u'stop',
 u'saw us',
 u'saw us',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'mean',
 u'mercy letting child linger pain',
 u'still cant believe youre going',
 u'children dont need hear filth',
 u'home',
 u'years ago',
 u'dare speak king manner',
 u'girl butchers boy attacked son',
 u'joffrey told us happened',
 u'shes',
 u'shes wild animal',
 u'joffrey bear scars rest life',
 u'direwolf',
 u'another wolf',
 u'beast',
 u'ser ilyn honor',
 u'trick',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'king scars fought direwolf',
 u'thats true',
 u'yes',
 '',
 u'would handle',
 u'royal army',
 u'northerners rebel',
 u'northern troops would fight lord',
 u'youve invaded homeland asked kill brothers',
 u'north c

In [259]:
Cersei_Words = []

for word in Cersei_Text:
    if len(word)>=1:
        if word != '0':
            Cersei_Words.append(word)
        
Cersei_Words        

[u'never worry anything',
 u'husband',
 u'scene changes crypt',
 u'yes',
 u'hello little dove',
 u'youre tall',
 u'bled yet',
 u'dress',
 u'talent',
 u'daughter well capital',
 u'stop',
 u'saw us',
 u'saw us',
 u'mean',
 u'mercy letting child linger pain',
 u'still cant believe youre going',
 u'children dont need hear filth',
 u'home',
 u'years ago',
 u'dare speak king manner',
 u'girl butchers boy attacked son',
 u'joffrey told us happened',
 u'shes',
 u'shes wild animal',
 u'joffrey bear scars rest life',
 u'direwolf',
 u'another wolf',
 u'beast',
 u'ser ilyn honor',
 u'trick',
 u'king scars fought direwolf',
 u'thats true',
 u'yes',
 u'would handle',
 u'royal army',
 u'northerners rebel',
 u'northern troops would fight lord',
 u'youve invaded homeland asked kill brothers',
 u'north cannot held outsider',
 u'everyone isnt us enemy',
 u'hes child years old',
 u'nothing',
 u'comes back',
 u'husband',
 u'let go',
 u'let go',
 u'find proof',
 u'youre missing tournament',
 u'thought might

In [260]:
Cersei_Words_String = ' '.join(Cersei_Words)
Cersei_Words_String

u'never worry anything husband scene changes crypt yes hello little dove youre tall bled yet dress talent daughter well capital stop saw us saw us mean mercy letting child linger pain still cant believe youre going children dont need hear filth home years ago dare speak king manner girl butchers boy attacked son joffrey told us happened shes shes wild animal joffrey bear scars rest life direwolf another wolf beast ser ilyn honor trick king scars fought direwolf thats true yes would handle royal army northerners rebel northern troops would fight lord youve invaded homeland asked kill brothers north cannot held outsider everyone isnt us enemy hes child years old nothing comes back husband let go let go find proof youre missing tournament thought might put happened kingsroad behind us ugliness wolves stark might ask cant change youre soldier arent without hand everything fall pieces dothraki dont sail father wrong still outnumber five want marriage every day well seventeen years quite lon

In [261]:
Cersei_String_Length = len(Cersei_Words_String)
Cersei_String_Length

1899

In [262]:
TextBlob(Cersei_Words_String).sentiment

Sentiment(polarity=-0.06022727272727274, subjectivity=0.47317821067821064)

### Daenerys Targaryen

In [263]:
Daenerys = season_one.loc['Daenerys Targaryen']
print Daenerys

0          weve guests year hes never asked us anything
1                                                      
2                                             thank ser
3                                        thank magister
4                                        shes beautiful
5                                    know common tongue
6                                             word know
7                                                     0
8                                                     0
9                                                     0
10                                                    0
11                                                    0
12                                                    0
13                                                    0
14                                                    0
15                                                    0
16                                                    0
17                                              

In [264]:
Dany_Text = Daenerys.values.tolist()
Dany_Text

[u'weve guests year hes never asked us anything',
 '',
 u'thank ser',
 u'thank magister',
 u'shes beautiful',
 u'know common tongue',
 u'word know',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'isnt anything else',
 u'everywhere',
 u'moon',
 u'leave',
 u'old',
 u'nine',
 u'teach make khal happy',
 u'take three years',
 u'finish man',
 u'well sounds like interesting woman',
 u'dont think dothraki way',
 '',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'tell stop',
 u'command otherwise',
 u'queen',
 '',
 u'please please dont hurt',
 '',
 u'know',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'people',
 u'brother given army dothraki could conquer seven kingdoms',
 '',
 u'know men'

In [265]:
Dany_Words = []

for word in Dany_Text:
    if len(word)>=1:
        if word != '0':
            Dany_Words.append(word)
        
Dany_Words        

[u'weve guests year hes never asked us anything',
 u'thank ser',
 u'thank magister',
 u'shes beautiful',
 u'know common tongue',
 u'word know',
 u'isnt anything else',
 u'everywhere',
 u'moon',
 u'leave',
 u'old',
 u'nine',
 u'teach make khal happy',
 u'take three years',
 u'finish man',
 u'well sounds like interesting woman',
 u'dont think dothraki way',
 u'tell stop',
 u'command otherwise',
 u'queen',
 u'please please dont hurt',
 u'know',
 u'people',
 u'brother given army dothraki could conquer seven kingdoms',
 u'know men',
 u'sold slaves',
 u'hush',
 u'hit',
 u'wasnt commanding',
 u'gift',
 u'please',
 u'stop stop',
 u'youve right braid',
 u'still true king',
 u'pray ser jorah',
 u'pray home',
 u'youre hurt',
 u'prince rides inside',
 u'stop',
 u'viserys please',
 u'says yes',
 u'according prophecy stallions ride ends world',
 u'earth end sea many dirts beyond sea',
 u'lands yes',
 u'chair',
 u'cant help make understand',
 u'brother fool know rightful heir seven kingdoms',
 u'drag

In [266]:
Dany_Words_String = ' '.join(Dany_Words)
Dany_Words_String

u'weve guests year hes never asked us anything thank ser thank magister shes beautiful know common tongue word know isnt anything else everywhere moon leave old nine teach make khal happy take three years finish man well sounds like interesting woman dont think dothraki way tell stop command otherwise queen please please dont hurt know people brother given army dothraki could conquer seven kingdoms know men sold slaves hush hit wasnt commanding gift please stop stop youve right braid still true king pray ser jorah pray home youre hurt prince rides inside stop viserys please says yes according prophecy stallions ride ends world earth end sea many dirts beyond sea lands yes chair cant help make understand brother fool know rightful heir seven kingdoms dragons dont believe rise honor ser hope repay kindness someday says drink hes tired thats well camp find mirri maz duur bring unharmed khal drogo hear denied come cant l wont leave even dies would l run l wont leave stop l never nothing l 

In [267]:
Dany_String_Length = len(Dany_Words_String)
Dany_String_Length

1388

In [268]:
TextBlob(Dany_Words_String).sentiment

Sentiment(polarity=0.28051948051948056, subjectivity=0.5805194805194805)

### Eddard Stark

In [269]:
Eddard = season_one.loc['Eddard Stark']
print Eddard

0                                           one marksman ten
1            name robert house baratheon first name jon bran
2                                  king andals first men jon
3          lord seven kingdoms protector realm eddard hou...
4                         white walkers gone thousands years
5                                           madman sees sees
6                                       mountain lions woods
7                                            tough old beast
8                                              im sorry bran
9                                                      train
10                                           hey hey hey hey
11                                      guarding north grace
12                                                     queen
13                                            tell jon arryn
14                                                          
15                                                       aye
16                      

In [270]:
Eddard_Text = Eddard.values.tolist()
Eddard_Text

[u'one marksman ten',
 u'name robert house baratheon first name jon bran',
 u'king andals first men jon',
 u'lord seven kingdoms protector realm eddard house stark lord winterfell warden north sentence die',
 u'white walkers gone thousands years',
 u'madman sees sees',
 u'mountain lions woods',
 u'tough old beast',
 u'im sorry bran',
 u'train',
 u'hey hey hey hey',
 u'guarding north grace',
 u'queen',
 u'tell jon arryn',
 '',
 u'aye',
 u'im worthy honor',
 u'sister',
 u'boy beheaded',
 u'talking madness',
 u'wildling ambush',
 u'pardon',
 u'yes king honored offer',
 u'dont fight tournaments',
 u'dont fight tournaments fight man real dont want know',
 u'im northman',
 u'king takes wants',
 u'send',
 u'stay',
 u'news',
 u'shes fresh widowed cat',
 u'im still better',
 u'hope ill serve well',
 u'choice',
 '',
 u'next time see well talk mother',
 u'ive half mind go',
 u'asked years ago',
 u'recall chances',
 u'bessie',
 u'wylla',
 u'robert baratheon',
 u'worst thing coronation',
 u'shes li

In [271]:
Eddard_Words = []

for word in Eddard_Text:
    if len(word)>=1:
        if word != '0':
            Eddard_Words.append(word)
        
Eddard_Words        

[u'one marksman ten',
 u'name robert house baratheon first name jon bran',
 u'king andals first men jon',
 u'lord seven kingdoms protector realm eddard house stark lord winterfell warden north sentence die',
 u'white walkers gone thousands years',
 u'madman sees sees',
 u'mountain lions woods',
 u'tough old beast',
 u'im sorry bran',
 u'train',
 u'hey hey hey hey',
 u'guarding north grace',
 u'queen',
 u'tell jon arryn',
 u'aye',
 u'im worthy honor',
 u'sister',
 u'boy beheaded',
 u'talking madness',
 u'wildling ambush',
 u'pardon',
 u'yes king honored offer',
 u'dont fight tournaments',
 u'dont fight tournaments fight man real dont want know',
 u'im northman',
 u'king takes wants',
 u'send',
 u'stay',
 u'news',
 u'shes fresh widowed cat',
 u'im still better',
 u'hope ill serve well',
 u'choice',
 u'next time see well talk mother',
 u'ive half mind go',
 u'asked years ago',
 u'recall chances',
 u'bessie',
 u'wylla',
 u'robert baratheon',
 u'worst thing coronation',
 u'shes little child

In [272]:
Eddard_Words_String = ' '.join(Eddard_Words)
Eddard_Words_String

u'one marksman ten name robert house baratheon first name jon bran king andals first men jon lord seven kingdoms protector realm eddard house stark lord winterfell warden north sentence die white walkers gone thousands years madman sees sees mountain lions woods tough old beast im sorry bran train hey hey hey hey guarding north grace queen tell jon arryn aye im worthy honor sister boy beheaded talking madness wildling ambush pardon yes king honored offer dont fight tournaments dont fight tournaments fight man real dont want know im northman king takes wants send stay news shes fresh widowed cat im still better hope ill serve well choice next time see well talk mother ive half mind go asked years ago recall chances bessie wylla robert baratheon worst thing coronation shes little child tell speaking cant get hands one even million dothraki threat realm long remain side narrow sea cross took right get back back hurt right bed asleep stop stop gladly grace cant mean command grace wolf nort

In [273]:
Eddard_String_Length = len(Eddard_Words_String)
Eddard_String_Length

4794

In [274]:
TextBlob(Eddard_Words_String).sentiment

Sentiment(polarity=0.07185826519159849, subjectivity=0.568094837261504)

### Jaime Lannister

In [275]:
Jaime = season_one.loc['Jaime Lannister']
print Jaime

0                                     brother feel duty warn
1                                                     cersei
2                  told king heads would skewered city gates
3                                        thats honor without
4                                                   dont get
5                                  hear might neighbors soon
6          im sure well tournament celebrate new title ac...
7                                                           
8                                                  well said
9                                             completely mad
10                                                     right
11                                          heard first time
12                                                       ten
13                                               things love
14                                                         0
15                                                         0
16                      

In [276]:
Jaime_Text = Jaime.values.tolist()
Jaime_Text

[u'brother feel duty warn',
 u'cersei',
 u'told king heads would skewered city gates',
 u'thats honor without',
 u'dont get',
 u'hear might neighbors soon',
 u'im sure well tournament celebrate new title accept',
 '',
 u'well said',
 u'completely mad',
 u'right',
 u'heard first time',
 u'ten',
 u'things love',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'little brother',
 u'tell youre thinking taking black',
 u'good man',
 u'someone mean',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'sturdy old thing',
 u'know',
 u'calm',
 u'thinking us',
 u'raving',
 u'ill go war',
 u'never',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'listen',
 u'likes im duty',
 '',
 u'thats got s

In [277]:
Jaime_Words = []

for word in Jaime_Text:
    if len(word)>=1:
        if word != '0':
            Jaime_Words.append(word)
        
Jaime_Words        

[u'brother feel duty warn',
 u'cersei',
 u'told king heads would skewered city gates',
 u'thats honor without',
 u'dont get',
 u'hear might neighbors soon',
 u'im sure well tournament celebrate new title accept',
 u'well said',
 u'completely mad',
 u'right',
 u'heard first time',
 u'ten',
 u'things love',
 u'little brother',
 u'tell youre thinking taking black',
 u'good man',
 u'someone mean',
 u'sturdy old thing',
 u'know',
 u'calm',
 u'thinking us',
 u'raving',
 u'ill go war',
 u'never',
 u'listen',
 u'likes im duty',
 u'thats got scar',
 u'vicious sons whores',
 u'saw youngest greyjoy lads winterfell',
 u'doubt',
 u'dont serve lord stark',
 u'small pack wolves',
 u'get back inside safe',
 u'seems trouble road',
 u'come stark',
 u'youre right',
 u'brother lord stark want back',
 u'tyrion',
 u'one men interfered speared leg could finish',
 u'wouldnt clean',
 u'could care less anyone thinks',
 u'truth',
 u'course bothers',
 u'didnt realize placed high value brothers life',
 u'lion conc

In [278]:
Jaime_Words_String = ' '.join(Jaime_Words)
Jaime_Words_String

u'brother feel duty warn cersei told king heads would skewered city gates thats honor without dont get hear might neighbors soon im sure well tournament celebrate new title accept well said completely mad right heard first time ten things love little brother tell youre thinking taking black good man someone mean sturdy old thing know calm thinking us raving ill go war never listen likes im duty thats got scar vicious sons whores saw youngest greyjoy lads winterfell doubt dont serve lord stark small pack wolves get back inside safe seems trouble road come stark youre right brother lord stark want back tyrion one men interfered speared leg could finish wouldnt clean could care less anyone thinks truth course bothers didnt realize placed high value brothers life lion concern opinions tywin lannister lady stark lve lost lm afraid could end war right boy save thousands lives look lovely tonight lady stark let show lf gods real world full injustice men like get sleep'

In [279]:
Jaime_String_Length = len(Jaime_Words_String)
Jaime_String_Length

973

In [280]:
TextBlob(Jaime_Words_String).sentiment

Sentiment(polarity=0.012112936083524324, subjectivity=0.5282767804091334)

### Joffrey Baratheon

In [281]:
Joffrey = season_one.loc['Joffrey Baratheon']
print Joffrey

0                                       0
1                                       0
2                                       0
3                                       0
4                                       0
5                                       0
6                                       0
7                                       0
8                                       0
9                                       0
10                                      0
11                                      0
12                                      0
13                                      0
14                                      0
15                                      0
16                                      0
17                                      0
18                                      0
19                                      0
20                                      0
21                                      0
22                                      0
23                                

In [282]:
Joffrey_Text = Joffrey.values.tolist()
Joffrey_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'good sympathies',
 u'boy means nothing',
 u'im telling mother',
 u'cant tyrion lannister',
 u'princess drink much wants',
 u'sister',
 u'butchers boy wants knight eh',
 u'im prince lord said pick sword',
 u'youre knight',
 u'wont hurt much',
 u'ill gut little cunt',
 u'please dont',
 u'go',
 u'yes',
 u'shut',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'ugly',
 u'im like',
 u'marry',
 u'dont want',
 u'allow northerners much power',
 u'id double taxes command supply men royal army',
 u'every lord command men',
 u'id crush',
 '',
 u'im asking',
 u'agree',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',

In [283]:
Joffrey_Words = []

for word in Joffrey_Text:
    if len(word)>=1:
        if word != '0':
            Joffrey_Words.append(word)
        
Joffrey_Words        

[u'good sympathies',
 u'boy means nothing',
 u'im telling mother',
 u'cant tyrion lannister',
 u'princess drink much wants',
 u'sister',
 u'butchers boy wants knight eh',
 u'im prince lord said pick sword',
 u'youre knight',
 u'wont hurt much',
 u'ill gut little cunt',
 u'please dont',
 u'go',
 u'yes',
 u'shut',
 u'ugly',
 u'im like',
 u'marry',
 u'dont want',
 u'allow northerners much power',
 u'id double taxes command supply men royal army',
 u'every lord command men',
 u'id crush',
 u'im asking',
 u'agree',
 u'lady',
 u'youll queen one day fitting look part',
 u'youre lady',
 u'let father die',
 u'come forward lady',
 u'said wasnt king',
 u'anything else',
 u'sweet words moved',
 u'mother wishes let lord eddard join nights watch',
 u'amusing',
 u'tell favor fingers tongue',
 u'fingers tongue',
 u'good',
 u'ser llyn better carry sentence',
 u'lm done day',
 u'look quite nice',
 u'grace',
 u'walk',
 u'soon youve blood lll put son',
 u'ones father',
 u'l',
 u'well',
 u'long pleases',
 

In [284]:
Joffrey_Words_String = ' '.join(Joffrey_Words)
Joffrey_Words_String

u'good sympathies boy means nothing im telling mother cant tyrion lannister princess drink much wants sister butchers boy wants knight eh im prince lord said pick sword youre knight wont hurt much ill gut little cunt please dont go yes shut ugly im like marry dont want allow northerners much power id double taxes command supply men royal army every lord command men id crush im asking agree lady youll queen one day fitting look part youre lady let father die come forward lady said wasnt king anything else sweet words moved mother wishes let lord eddard join nights watch amusing tell favor fingers tongue fingers tongue good ser llyn better carry sentence lm done day look quite nice grace walk soon youve blood lll put son ones father l well long pleases obey lords'

In [285]:
Joffrey_String_Length = len(Joffrey_Words_String)
Joffrey_String_Length

769

In [286]:
TextBlob(Joffrey_Words_String).sentiment

Sentiment(polarity=0.20750000000000002, subjectivity=0.5433333333333333)

### Jon Snow

In [287]:
Jon = season_one.loc['Jon Snow']
print Jon

0                                       dont think much bran
1                                                       well
2                                                           
3                                                       five
4                                                  want hold
5                                                   im stark
6                 whys mother deadset us getting pretty king
7                                               uncle benjen
8          lady stark thought might insult royal family s...
9                                               take go back
10                                       im ready swear oath
11                                                 dont care
12                                               whatre back
13                                    youre tyrion lannister
14                                  lord eddard stark father
15                                         hell know bastard
16                      

In [288]:
Jon_Text = Jon.values.tolist()
Jon_Text

[u'dont think much bran',
 u'well',
 '',
 u'five',
 u'want hold',
 u'im stark',
 u'whys mother deadset us getting pretty king',
 u'uncle benjen',
 u'lady stark thought might insult royal family seat bastard midst',
 u'take go back',
 u'im ready swear oath',
 u'dont care',
 u'whatre back',
 u'youre tyrion lannister',
 u'lord eddard stark father',
 u'hell know bastard',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'already one',
 u'course',
 u'good youve got help',
 u'impressive',
 u'youll work every day',
 u'first lesson',
 u'im going miss',
 u'wish could wake',
 u'read much',
 u'trick',
 u'brother killed king',
 u'ask nicely maybe ill tell dwarf',
 u'nights watch protects realm tyrion lannister',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'improvement',
 u'everybody knew place one told',
 u'youre leaving',
 u'kind reports',
 u'ready',
 u'im better every benjen stark',

In [289]:
Jon_Words = []

for word in Jon_Text:
    if len(word)>=1:
        if word != '0':
            Jon_Words.append(word)
        
Jon_Words        

[u'dont think much bran',
 u'well',
 u'five',
 u'want hold',
 u'im stark',
 u'whys mother deadset us getting pretty king',
 u'uncle benjen',
 u'lady stark thought might insult royal family seat bastard midst',
 u'take go back',
 u'im ready swear oath',
 u'dont care',
 u'whatre back',
 u'youre tyrion lannister',
 u'lord eddard stark father',
 u'hell know bastard',
 u'already one',
 u'course',
 u'good youve got help',
 u'impressive',
 u'youll work every day',
 u'first lesson',
 u'im going miss',
 u'wish could wake',
 u'read much',
 u'trick',
 u'brother killed king',
 u'ask nicely maybe ill tell dwarf',
 u'nights watch protects realm tyrion lannister',
 u'improvement',
 u'everybody knew place one told',
 u'youre leaving',
 u'kind reports',
 u'ready',
 u'im better every benjen stark',
 u'stop winterfell way south',
 u'see brother bran tell miss',
 u'hell never walk',
 u'farewell lord',
 u'enough',
 u'sure want',
 u'ive worse',
 u'going get easier know',
 u'walls place cowards',
 u'come sta

In [290]:
Jon_Words_String = ' '.join(Jon_Words)
Jon_Words_String

u'dont think much bran well five want hold im stark whys mother deadset us getting pretty king uncle benjen lady stark thought might insult royal family seat bastard midst take go back im ready swear oath dont care whatre back youre tyrion lannister lord eddard stark father hell know bastard already one course good youve got help impressive youll work every day first lesson im going miss wish could wake read much trick brother killed king ask nicely maybe ill tell dwarf nights watch protects realm tyrion lannister improvement everybody knew place one told youre leaving kind reports ready im better every benjen stark stop winterfell way south see brother bran tell miss hell never walk farewell lord enough sure want ive worse going get easier know walls place cowards come stand fire youre cant fight yes well cant get worse watch duty wasnt hungry one touches sam wouldnt doubt sally side didnt think youd upset matter fact im came close know put young gorgeous red better surname snow never

In [291]:
Jon_String_Length = len(Jon_Words_String)
Jon_String_Length

1503

In [292]:
TextBlob(Jon_Words_String).sentiment

Sentiment(polarity=0.15580357142857143, subjectivity=0.49243551587301587)

### Jorah Mormont

In [293]:
Jorah = season_one.loc['Jorah Mormont']
print Jorah

0                                    small gift new khaleesi
1                              ser jorah mormont bear island
2                                        word thank dothraki
3                                                          0
4                                                          0
5                                                          0
6                                                          0
7                                                          0
8                                                          0
9                                                          0
10                                                         0
11                                                         0
12                                                         0
13                                                         0
14                                                         0
15                                                         0
16                      

In [294]:
Jorah_Text = Jorah.values.tolist()
Jorah_Text

[u'small gift new khaleesi',
 u'ser jorah mormont bear island',
 u'word thank dothraki',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'dothraki two things abundance',
 u'still far pentos grace',
 u'wish grace',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'dothraki dont believe money',
 u'rule city see horde approaching two choices',
 u'want entire horde stop',
 u'youre learning talk like queen',
 u'shall return khalasar khaleesi',
 u'ive heard father famous warrior',
 u'still',
 u'dont think wants eat dog',
 u'ill boys butcher goat supper',
 u'dont worry',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'dothraki never 

In [295]:
Jorah_Words = []

for word in Jorah_Text:
    if len(word)>=1:
        if word != '0':
            Jorah_Words.append(word)
        
Jorah_Words        

[u'small gift new khaleesi',
 u'ser jorah mormont bear island',
 u'word thank dothraki',
 u'dothraki two things abundance',
 u'still far pentos grace',
 u'wish grace',
 u'dothraki dont believe money',
 u'rule city see horde approaching two choices',
 u'want entire horde stop',
 u'youre learning talk like queen',
 u'shall return khalasar khaleesi',
 u'ive heard father famous warrior',
 u'still',
 u'dont think wants eat dog',
 u'ill boys butcher goat supper',
 u'dont worry',
 u'dothraki never crossed narrow sea',
 u'king robert fool enough meet open battle men advising different',
 u'fought beside long ago',
 u'aye',
 u'money expensive wife',
 u'another place another man',
 u'brother rhaegar last dragon',
 u'truth',
 u'common people pray rain health summer never ends',
 u'home',
 u'prince riding',
 u'dont let see carrying sword vaes dothrak',
 u'dont belong',
 u'perhaps',
 u'three',
 u'go cant eggs',
 u'means everything',
 u'stand',
 u'come',
 u'put sword',
 u'look away khaleesi',
 u'kha

In [296]:
Jorah_Words_String = ' '.join(Jorah_Words)
Jorah_Words_String

u'small gift new khaleesi ser jorah mormont bear island word thank dothraki dothraki two things abundance still far pentos grace wish grace dothraki dont believe money rule city see horde approaching two choices want entire horde stop youre learning talk like queen shall return khalasar khaleesi ive heard father famous warrior still dont think wants eat dog ill boys butcher goat supper dont worry dothraki never crossed narrow sea king robert fool enough meet open battle men advising different fought beside long ago aye money expensive wife another place another man brother rhaegar last dragon truth common people pray rain health summer never ends home prince riding dont let see carrying sword vaes dothrak dont belong perhaps three go cant eggs means everything stand come put sword look away khaleesi khaleesi daenerys targaryen dothraki things time reasons forgive khaleesi ancestor aegon conqueror didnt seize six kingdoms right ah well dragons makes things easier ever seen dragon khalee

In [297]:
Jorah_String_Length = len(Jorah_Words_String)
Jorah_String_Length

1576

In [298]:
TextBlob(Jorah_Words_String).sentiment

Sentiment(polarity=0.0037662337662337573, subjectivity=0.4860389610389611)

### Petyr Baelish/Littlefinger

In [299]:
Littlefinger = season_one.loc['Petyr Baelish']
print Littlefinger

0                                                          0
1                                                          0
2                                                          0
3                                                          0
4                                                          0
5                                                          0
6                                                          0
7                                                          0
8                                                          0
9                                                          0
10                                                         0
11                                                         0
12                                                         0
13                                                         0
14                                                         0
15                                                         0
16                      

In [300]:
Littlefinger_Text = Littlefinger.values.tolist()
Littlefinger_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'lords small matters',
 u'mmm much',
 u'im telling crown six million debt',
 u'master coin finds money',
 '',
 u'cat',
 u'one come looking',
 u'dear friend told',
 u'good news',
 '',
 u'thought shed safest',
 u'lord tyrion say stolen',
 u'ill try keep alive sake',
 u'dont tell anyone',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'every inn city full whores walking bowlegged',
 u'never stops',
 u'promised cat id help',
 u'singularly bad idea',
 '',
 u'wiser answer lord',
 u'observers said possible saw lord arryn vi

In [301]:
Littlefinger_Words = []

for word in Littlefinger_Text:
    if len(word)>=1:
        if word != '0':
            Littlefinger_Words.append(word)
        
Littlefinger_Words        

[u'lords small matters',
 u'mmm much',
 u'im telling crown six million debt',
 u'master coin finds money',
 u'cat',
 u'one come looking',
 u'dear friend told',
 u'good news',
 u'thought shed safest',
 u'lord tyrion say stolen',
 u'ill try keep alive sake',
 u'dont tell anyone',
 u'every inn city full whores walking bowlegged',
 u'never stops',
 u'promised cat id help',
 u'singularly bad idea',
 u'wiser answer lord',
 u'observers said possible saw lord arryn visit armorer several times weeks death',
 u'quite right',
 u'ser gregor clegane',
 u'ser hugh vale',
 u'expecting',
 u'gold dragons mountain',
 u'buy gold dragons',
 u'loras knew mare heat',
 u'honor quite bit gold',
 u'move quietly',
 u'look bit lonely today',
 u'im purveyor beauty discretion equally important',
 u'desires valid man full purse',
 u'strictly speaking thing would accordance kings laws',
 u'tell',
 u'since last saw since last saw',
 u'saw eyes',
 u'council business',
 u'know something',
 u'yes',
 u'long saw escorting

In [302]:
Littlefinger_Words_String = ' '.join(Littlefinger_Words)
Littlefinger_Words_String

u'lords small matters mmm much im telling crown six million debt master coin finds money cat one come looking dear friend told good news thought shed safest lord tyrion say stolen ill try keep alive sake dont tell anyone every inn city full whores walking bowlegged never stops promised cat id help singularly bad idea wiser answer lord observers said possible saw lord arryn visit armorer several times weeks death quite right ser gregor clegane ser hugh vale expecting gold dragons mountain buy gold dragons loras knew mare heat honor quite bit gold move quietly look bit lonely today im purveyor beauty discretion equally important desires valid man full purse strictly speaking thing would accordance kings laws tell since last saw since last saw saw eyes council business know something yes long saw escorting certain foreign dignitary council business find position simple word king renly baratheon small council meeting jorah mormonts slaver traitor find bed ugly woman best close eyes get gra

In [303]:
Littlefinger_String_Length = len(Littlefinger_Words_String)
Littlefinger_String_Length

1797

In [304]:
TextBlob(Littlefinger_Words_String).sentiment

Sentiment(polarity=0.03150406504065041, subjectivity=0.5189121176926055)

### Robb Stark

In [305]:
Robb = season_one.loc['Robb Stark']
print Robb

0                          relax bow arm
1               lad go run back get rest
2                  direwolves south wall
3                                       
4          hear prince right royal prick
5                           uncle benjen
6                                im good
7                               time bed
8                                      0
9                                      0
10                                     0
11                                     0
12                                     0
13                                     0
14                                     0
15                                     0
16                                     0
17                                     0
18                                     0
19                                     0
20                                     0
21                                     0
22                                     0
23                                     0
24              

In [306]:
Robb_Text = Robb.values.tolist()
Robb_Text

[u'relax bow arm',
 u'lad go run back get rest',
 u'direwolves south wall',
 '',
 u'hear prince right royal prick',
 u'uncle benjen',
 u'im good',
 u'time bed',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'ill make appointments',
 u'last time left room',
 u'hes going die mother',
 u'rickon needs',
 u'fire',
 u'come home try murder brother',
 u'ill ride kings landing',
 u'mother cant',
 u'bran',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'get supper',
 u'feel',
 u'dont ever say',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'man nights watch welcome winterfell',
 u'im boy lannister',
 '',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0

In [307]:
Robb_Words = []

for word in Robb_Text:
    if len(word)>=1:
        if word != '0':
            Robb_Words.append(word)
        
Robb_Words        

[u'relax bow arm',
 u'lad go run back get rest',
 u'direwolves south wall',
 u'hear prince right royal prick',
 u'uncle benjen',
 u'im good',
 u'time bed',
 u'ill make appointments',
 u'last time left room',
 u'hes going die mother',
 u'rickon needs',
 u'fire',
 u'come home try murder brother',
 u'ill ride kings landing',
 u'mother cant',
 u'bran',
 u'get supper',
 u'feel',
 u'dont ever say',
 u'man nights watch welcome winterfell',
 u'im boy lannister',
 u'youre talking war',
 u'lord winterfell call bannermen raise army',
 u'duty house',
 u'wheres bran',
 u'drop knife',
 u'right',
 u'lost mind',
 u'dont right theon greyjoy',
 u'well keep alive',
 u'treason',
 u'joffrey puts father chains wants ass kissed',
 u'either need cross river crossing twins',
 u'find',
 u'high get',
 u'father understands mercy room',
 u'lannister scout',
 u'go',
 u'hes grandfathers bannerman',
 u'father rots dungeon',
 u'horse saddled ready',
 u'father would whatever took secure crossing',
 u'well',
 u'huh',
 u

In [308]:
Robb_Words_String = ' '.join(Robb_Words)
Robb_Words_String

u'relax bow arm lad go run back get rest direwolves south wall hear prince right royal prick uncle benjen im good time bed ill make appointments last time left room hes going die mother rickon needs fire come home try murder brother ill ride kings landing mother cant bran get supper feel dont ever say man nights watch welcome winterfell im boy lannister youre talking war lord winterfell call bannermen raise army duty house wheres bran drop knife right lost mind dont right theon greyjoy well keep alive treason joffrey puts father chains wants ass kissed either need cross river crossing twins find high get father understands mercy room lannister scout go hes grandfathers bannerman father rots dungeon horse saddled ready father would whatever took secure crossing well huh want return fine fine wont happy l see l refuse l consent time knew happening already happened hes use us alive dead lf way kingslayer youd win l sent men graves today aye lll kill renly king doesnt make renly king alway

In [309]:
Robb_String_Length = len(Robb_Words_String)
Robb_String_Length

999

In [310]:
TextBlob(Robb_Words_String).sentiment

Sentiment(polarity=0.2159307359307359, subjectivity=0.477900432900433)

### Samwell Tarly

In [311]:
Sam = season_one.loc['Samwell Tarly']
print Sam

0                        0
1                        0
2                        0
3                        0
4                        0
5                        0
6                        0
7                        0
8                        0
9                        0
10                       0
11                       0
12                       0
13                       0
14                       0
15                       0
16                       0
17                       0
18                       0
19                       0
20                       0
21                       0
22                       0
23                       0
24                       0
25                       0
26                       0
27                       0
28                       0
29                       0
30                       0
31                       0
32                       0
0_two                    0
1_two                    0
2_two                    0
3_two                    0
4

In [312]:
Sam_Text = Sam.values.tolist()
Sam_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'hurt',
 u'call sam',
 u'wanted',
 u'im coward',
 u'youre right',
 u'thats right',
 u'dont like high places',
 u'morning th nameday father came',
 u'im going get better know',
 u'dont think little bit unfair',
 u'silly isnt',
 '',
 u'find hard believe',
 u'old ugly',
 u'color hair',
 u'like red hair',
 u'good',
 u'oh',
 u'jon snow',
 u'youre bastard north',
 u'didnt know put',
 u'bit nippy',
 '0

In [313]:
Sam_Words = []

for word in Sam_Text:
    if len(word)>=1:
        if word != '0':
            Sam_Words.append(word)
        
Sam_Words        

[u'hurt',
 u'call sam',
 u'wanted',
 u'im coward',
 u'youre right',
 u'thats right',
 u'dont like high places',
 u'morning th nameday father came',
 u'im going get better know',
 u'dont think little bit unfair',
 u'silly isnt',
 u'find hard believe',
 u'old ugly',
 u'color hair',
 u'like red hair',
 u'good',
 u'oh',
 u'jon snow',
 u'youre bastard north',
 u'didnt know put',
 u'bit nippy',
 u'miss girls',
 u'one blast ranger returning two wildlings three jon snow',
 u'smell',
 u'none',
 u'l l cant',
 u'lm really supposed say',
 u'hes heading south',
 u'theyll put word',
 u'going',
 u'cant leave us',
 u'l wont let go',
 u'get',
 u'brothers']

In [314]:
Sam_Words_String = ' '.join(Sam_Words)
Sam_Words_String

u'hurt call sam wanted im coward youre right thats right dont like high places morning th nameday father came im going get better know dont think little bit unfair silly isnt find hard believe old ugly color hair like red hair good oh jon snow youre bastard north didnt know put bit nippy miss girls one blast ranger returning two wildlings three jon snow smell none l l cant lm really supposed say hes heading south theyll put word going cant leave us l wont let go get brothers'

In [315]:
Sam_String_Length = len(Sam_Words_String)
Sam_String_Length

477

In [316]:
TextBlob(Sam_Words_String).sentiment

Sentiment(polarity=0.004020146520146513, subjectivity=0.5406227106227107)

### Sansa Stark

In [317]:
Sansa = season_one.loc['Sansa Stark']
print Sansa

0                       thank
1                      robert
2           would please shut
3          think joffrey like
4                hes handsome
5               would married
6                   would say
7              left home come
8              thirteen grace
9                 think grace
10                       arya
11                          0
12                          0
13                          0
14                          0
15                          0
16                          0
17                          0
18                          0
19                          0
20                          0
21                          0
22                          0
23                          0
24                          0
25                          0
26                          0
27                          0
28                          0
29                          0
30                          0
31                          0
32                          0
0_two     

In [318]:
Sansa_Text = Sansa.values.tolist()
Sansa_Text

[u'thank',
 u'robert',
 u'would please shut',
 u'think joffrey like',
 u'hes handsome',
 u'would married',
 u'would say',
 u'left home come',
 u'thirteen grace',
 u'think grace',
 u'arya',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'practicing',
 u'hound killed friend',
 u'youre idiot',
 u'havent played dolls since eight',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'girls',
 u'jeyne pooles mother five children girls',
 '',
 u'everyone would hate',
 u'joffrey',
 u'aegon conqueror',
 u'maegor cruel',
 u'mad king',
 u'killed',
 u'dont want speak father ever',
 u'wont',

In [319]:
Sansa_Words = []

for word in Sansa_Text:
    if len(word)>=1:
        if word != '0':
            Sansa_Words.append(word)
        
Sansa_Words        

[u'thank',
 u'robert',
 u'would please shut',
 u'think joffrey like',
 u'hes handsome',
 u'would married',
 u'would say',
 u'left home come',
 u'thirteen grace',
 u'think grace',
 u'arya',
 u'practicing',
 u'hound killed friend',
 u'youre idiot',
 u'havent played dolls since eight',
 u'girls',
 u'jeyne pooles mother five children girls',
 u'everyone would hate',
 u'joffrey',
 u'aegon conqueror',
 u'maegor cruel',
 u'mad king',
 u'killed',
 u'dont want speak father ever',
 u'wont',
 u'im sorry',
 u'arya',
 u'gods',
 u'opponent',
 u'wont tell anyone',
 u'cant watch',
 u'hes going die',
 u'ser loras would never',
 u'well shouldnt',
 u'mother isnt north',
 u'care',
 u'ive never seen',
 u'prince',
 u'beautiful',
 u'theres nothing forgive',
 u'please father',
 u'cares stupid dancing teacher',
 u'wait',
 u'stay away',
 u'wouldnt',
 u'im',
 u'robb',
 u'ifif could see father talk cersei lannister',
 u'meant thatwhat happen',
 u'onon',
 u'lord gyles',
 u'grace',
 u'please grace ask mercy father 

In [320]:
Sansa_Words_String = ' '.join(Sansa_Words)
Sansa_Words_String

u'thank robert would please shut think joffrey like hes handsome would married would say left home come thirteen grace think grace arya practicing hound killed friend youre idiot havent played dolls since eight girls jeyne pooles mother five children girls everyone would hate joffrey aegon conqueror maegor cruel mad king killed dont want speak father ever wont im sorry arya gods opponent wont tell anyone cant watch hes going die ser loras would never well shouldnt mother isnt north care ive never seen prince beautiful theres nothing forgive please father cares stupid dancing teacher wait stay away wouldnt im robb ifif could see father talk cersei lannister meant thatwhat happen onon lord gyles grace please grace ask mercy father lord eddard stark hand king thank grace lords badly hurt still affection heart please kindness grace stop stop stop thank lord promised merciful please let go home long l look lf please grace maybe hell give'

In [321]:
Sansa_String_Length = len(Sansa_Words_String)
Sansa_String_Length

944

In [322]:
TextBlob(Sansa_Words_String).sentiment

Sentiment(polarity=-0.285, subjectivity=0.6411111111111111)

### Theon Greyjoy

In [323]:
Theon = season_one.loc['Theon Greyjoy']
print Theon

0                                             mountain lion
1                                                 queen bet
2          think southern girls gets stab right royal prick
3                                                         0
4                                                         0
5                                                         0
6                                                         0
7                                                         0
8                                                         0
9                                                         0
10                                                        0
11                                                        0
12                                                        0
13                                                        0
14                                                        0
15                                                        0
16                                      

In [324]:
Theon_Text = Theon.values.tolist()
Theon_Text

[u'mountain lion',
 u'queen bet',
 u'think southern girls gets stab right royal prick',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'saw lady',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'visitors',
 u'really',
 u'neither',
 u'couldnt resist northern ass',
 u'hes master',
 u'wasnt feeling well',
 u'ladys whereabouts tyrion lannister',
 u'must pretty sight',
 u'outnumbered one',
 u'careful imp',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 

In [325]:
Theon_Words = []

for word in Theon_Text:
    if len(word)>=1:
        if word != '0':
            Theon_Words.append(word)
        
Theon_Words        

[u'mountain lion',
 u'queen bet',
 u'think southern girls gets stab right royal prick',
 u'saw lady',
 u'visitors',
 u'really',
 u'neither',
 u'couldnt resist northern ass',
 u'hes master',
 u'wasnt feeling well',
 u'ladys whereabouts tyrion lannister',
 u'must pretty sight',
 u'outnumbered one',
 u'careful imp',
 u'important enough likes',
 u'jealous',
 u'anyone coppers pocket night',
 u'hmm',
 u'generous tipper',
 u'im greyjoy',
 u'ive lord starks ward since eight years old',
 u'im boy',
 u'dont want pay',
 u'blood blood',
 u'im talking justice',
 u'lannister put spear fathers leg',
 u'youre boy anymore',
 u'dont know',
 u'tough little lad',
 u'would killed cut brans throat',
 u'turnip cart',
 u'afford',
 u'theres thousand girls like kings landing',
 u'dont fool',
 u'let see one time',
 u'im going miss',
 u'youre lucky girl',
 u'iron islands',
 u'youve never heard iron islands',
 u'trust lord',
 u'lord',
 u'lord father',
 u'youyou go',
 u'im southerner',
 u'youre impudent little wenc

In [326]:
Theon_Words_String = ' '.join(Theon_Words)
Theon_Words_String

u'mountain lion queen bet think southern girls gets stab right royal prick saw lady visitors really neither couldnt resist northern ass hes master wasnt feeling well ladys whereabouts tyrion lannister must pretty sight outnumbered one careful imp important enough likes jealous anyone coppers pocket night hmm generous tipper im greyjoy ive lord starks ward since eight years old im boy dont want pay blood blood im talking justice lannister put spear fathers leg youre boy anymore dont know tough little lad would killed cut brans throat turnip cart afford theres thousand girls like kings landing dont fool let see one time im going miss youre lucky girl iron islands youve never heard iron islands trust lord lord lord father youyou go im southerner youre impudent little wench arent impudent thought prisoner lord frey controls bridge robbs right walder frey would think march gates tell youre crossing throw dungeon kill robb bards sing songs sacrifice l brother always sword victory defeat day 

In [327]:
Theon_String_Length = len(Theon_Words_String)
Theon_String_Length

1006

In [328]:
TextBlob(Theon_Words_String).sentiment

Sentiment(polarity=0.05272486772486774, subjectivity=0.5136507936507936)

### Tyrion Lannister

In [329]:
Tyrion = season_one.loc['Tyrion Lannister']
print Tyrion

0                                                        mmh
1                                             hear something
2                                                    brother
3                                          theres pretty one
4                                        hear hates nickname
5                                                clever girl
6                                     gods gave one blessing
7             explain meaning closed door whorehouse brother
8                                                      jaime
9                                                 close door
10                                       uncles nights watch
11                                                    offend
12                                         lady stark mother
13                             dwarves bastards fathers eyes
14                     get without squirting one end miracle
15                                             greatest land
16                      

In [330]:
Tyrion_Text = Tyrion.values.tolist()
Tyrion_Text

[u'mmh',
 u'hear something',
 u'brother',
 u'theres pretty one',
 u'hear hates nickname',
 u'clever girl',
 u'gods gave one blessing',
 u'explain meaning closed door whorehouse brother',
 u'jaime',
 u'close door',
 u'uncles nights watch',
 u'offend',
 u'lady stark mother',
 u'dwarves bastards fathers eyes',
 u'get without squirting one end miracle',
 u'greatest land',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'go call lord lady stark offer sympathies',
 u'none',
 u'one word ill hit',
 u'go',
 u'bread',
 u'beloved siblings',
 u'apparently',
 u'maester says boy may live',
 u'gods know certain',
 u'wheres sense wonder',
 u'go celibate',
 u'speaking grotesques id disagree',
 u'rapers',
 u'look tell see',
 u'see dwarf',
 u'yes brother killed',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'charming man',
 u'hows going commander mormont',
 u'good news bad',
 u'im looking',
 u'think would loo

In [331]:
Tyrion_Words = []

for word in Tyrion_Text:
    if len(word)>=1:
        if word != '0':
            Tyrion_Words.append(word)
        
Tyrion_Words        

[u'mmh',
 u'hear something',
 u'brother',
 u'theres pretty one',
 u'hear hates nickname',
 u'clever girl',
 u'gods gave one blessing',
 u'explain meaning closed door whorehouse brother',
 u'jaime',
 u'close door',
 u'uncles nights watch',
 u'offend',
 u'lady stark mother',
 u'dwarves bastards fathers eyes',
 u'get without squirting one end miracle',
 u'greatest land',
 u'go call lord lady stark offer sympathies',
 u'none',
 u'one word ill hit',
 u'go',
 u'bread',
 u'beloved siblings',
 u'apparently',
 u'maester says boy may live',
 u'gods know certain',
 u'wheres sense wonder',
 u'go celibate',
 u'speaking grotesques id disagree',
 u'rapers',
 u'look tell see',
 u'see dwarf',
 u'yes brother killed',
 u'charming man',
 u'hows going commander mormont',
 u'good news bad',
 u'im looking',
 u'think would look marvelous decorating spikes kings landing',
 u'youre joking',
 u'bears balls taste',
 u'dornish girls count',
 u'better chance finding feed glory',
 u'dont enough men army aside yoren 

In [332]:
Tyrion_Words_String = ' '.join(Tyrion_Words)
Tyrion_Words_String

u'mmh hear something brother theres pretty one hear hates nickname clever girl gods gave one blessing explain meaning closed door whorehouse brother jaime close door uncles nights watch offend lady stark mother dwarves bastards fathers eyes get without squirting one end miracle greatest land go call lord lady stark offer sympathies none one word ill hit go bread beloved siblings apparently maester says boy may live gods know certain wheres sense wonder go celibate speaking grotesques id disagree rapers look tell see see dwarf yes brother killed charming man hows going commander mormont good news bad im looking think would look marvelous decorating spikes kings landing youre joking bears balls taste dornish girls count better chance finding feed glory dont enough men army aside yoren none particularly funny think im plump im sure ive done offend think hes starting like youre heading kings landing lets share road time eight nine say winter birth three years long maester aemon yes fisherm

In [333]:
Tyrion_String_Length = len(Tyrion_Words_String)
Tyrion_String_Length

3173

In [334]:
TextBlob(Tyrion_Words_String).sentiment

Sentiment(polarity=0.1536992263056093, subjectivity=0.6116934926775351)

### Tywin Lannister

In [335]:
Tywin = season_one.loc['Tywin Lannister']
print Tywin

0                 0
1                 0
2                 0
3                 0
4                 0
5                 0
6                 0
7                 0
8                 0
9                 0
10                0
11                0
12                0
13                0
14                0
15                0
16                0
17                0
18                0
19                0
20                0
21                0
22                0
23                0
24                0
25                0
26                0
27                0
28                0
29                0
30                0
31                0
32                0
0_two             0
1_two             0
2_two             0
3_two             0
4_two             0
5_two             0
6_two             0
7_two             0
8_two             0
9_two             0
10_two            0
11_two            0
12_two            0
13_two            0
14_two            0
15_two            0
16_two            0


In [336]:
Tywin_Text = Tywin.values.tolist()
Tywin_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0'

In [337]:
Tywin_Words = []

for word in Tywin_Text:
    if len(word)>=1:
        if word != '0':
            Tywin_Words.append(word)
        
Tywin_Words        

[u'attacking stupid',
 u'gonna say something clever',
 u'still alive',
 u'ned stark',
 u'still alive',
 u'clean tywin lannister',
 u'thats want people think',
 u'hear whispering kingslayer behind back doesnt bother',
 u'lion doesnt concern opinions sheep',
 u'hes lannister',
 u'hmm',
 u'rumors demise unfounded',
 u'companions',
 u'shagga son dolf chieftain stone crows',
 u'left us choice',
 u'hostage',
 u'robert baratheon dead',
 u'green boy',
 u'wolf rushes lions jaws',
 u'said men mountain clans great warriors',
 u'boy may lack experience sense certain mindless provincial courage',
 u'l hope savages going use otherwise weve wasted good steel',
 u'battle commences wildlings vanguard',
 u'soldiers lack discipline fault lies commander',
 u'therell discussion matter',
 u'youre wounded',
 u'huh',
 u'wasnt',
 u'men',
 u'one stay',
 u'rule']

In [338]:
Tywin_Words_String = ' '.join(Tywin_Words)
Tywin_Words_String

u'attacking stupid gonna say something clever still alive ned stark still alive clean tywin lannister thats want people think hear whispering kingslayer behind back doesnt bother lion doesnt concern opinions sheep hes lannister hmm rumors demise unfounded companions shagga son dolf chieftain stone crows left us choice hostage robert baratheon dead green boy wolf rushes lions jaws said men mountain clans great warriors boy may lack experience sense certain mindless provincial courage l hope savages going use otherwise weve wasted good steel battle commences wildlings vanguard soldiers lack discipline fault lies commander therell discussion matter youre wounded huh wasnt men one stay rule'

In [339]:
Tywin_String_Length = len(Tywin_Words_String)
Tywin_String_Length

693

In [340]:
TextBlob(Tywin_Words_String).sentiment

Sentiment(polarity=0.015476190476190473, subjectivity=0.5096726190476191)

### Varys

In [341]:
Varys = season_one.loc['Varys']
print Varys

0                                                0
1                                                0
2                                                0
3                                                0
4                                                0
5                                                0
6                                                0
7                                                0
8                                                0
9                                                0
10                                               0
11                                               0
12                                               0
13                                               0
14                                               0
15                                               0
16                                               0
17                                               0
18                                               0
19                             

In [342]:
Varys_Text = Varys.values.tolist()
Varys_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'grievously sorry hear troubles kingsroad',
 u'grace many cares',
 u'kings hand lord stark serve pleasure',
 u'lady stark',
 u'see many years blessing',
 u'knowledge trade lady',
 u'must admit',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'dreadful',
 u'realm prospers events lord',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 

In [343]:
Varys_Words = []

for word in Varys_Text:
    if len(word)>=1:
        if word != '0':
            Varys_Words.append(word)
        
Varys_Words        

[u'grievously sorry hear troubles kingsroad',
 u'grace many cares',
 u'kings hand lord stark serve pleasure',
 u'lady stark',
 u'see many years blessing',
 u'knowledge trade lady',
 u'must admit',
 u'dreadful',
 u'realm prospers events lord',
 u'son lord',
 u'mind sound',
 u'blessing',
 u'wrong ears heard im tell comes head',
 u'didnt trust',
 u'eddard stark',
 u'sort jon arryn',
 u'dear friend doubt',
 u'pity happened life seemed going nicely',
 u'started asking questions',
 u'gods alone know',
 u'hand',
 u'delay say',
 u'qualities',
 u'think youre mistaking business pleasure',
 u'oh im sure',
 u'though suppose beauty subjective quality',
 u'heard awful rumor certain lord taste fresh cadavers',
 u'strictly speaking',
 u'know idea',
 u'last time saw talking hand king',
 u'eyes',
 u'everyones well aware enduring fondness lord starks wife',
 u'oh',
 u'bed',
 u'oh please',
 u'rumor lord',
 u'ser jorah mormont',
 u'understand misgivings lord',
 u'wonder ser barristan gave king wine',
 u'du

In [344]:
Varys_Words_String = ' '.join(Varys_Words)
Varys_Words_String

u'grievously sorry hear troubles kingsroad grace many cares kings hand lord stark serve pleasure lady stark see many years blessing knowledge trade lady must admit dreadful realm prospers events lord son lord mind sound blessing wrong ears heard im tell comes head didnt trust eddard stark sort jon arryn dear friend doubt pity happened life seemed going nicely started asking questions gods alone know hand delay say qualities think youre mistaking business pleasure oh im sure though suppose beauty subjective quality heard awful rumor certain lord taste fresh cadavers strictly speaking know idea last time saw talking hand king eyes everyones well aware enduring fondness lord starks wife oh bed oh please rumor lord ser jorah mormont understand misgivings lord wonder ser barristan gave king wine dutiful boy make sure grace lack refreshment im afraid birds flown many still love wrong lord l still boy cut balls hot knife l traveled group actors free cities l could peace boys conquerors sansa 

In [345]:
Varys_String_Length = len(Varys_Words_String)
Varys_String_Length

1248

In [346]:
TextBlob(Varys_Words_String).sentiment

Sentiment(polarity=0.07933273622928795, subjectivity=0.6403592576006368)